In [1]:
import openfst_python as fst
import math
import glob
from subprocess import check_call
from IPython.display import Image

class CreateWFST:
    
    def __init__(self, n_phone=3, n_word=1):
        self.num_per_phone=n_phone
        self.num_per_word=n_word
        self.end_weight=fst.Weight('log',-math.log(1))
        self.lex=self.parse_lexicon('lexicon.txt')
        self.word_table, self.phone_table, self.state_table=self.generate_symbol_tables(self.lex,3)
        self.word_table.write_text('word_table.txt')
        self.phone_table.write_text('phone_table.txt')
        self.state_table.write_text('state_table.txt')
        self.unigram_dic={}
        self.unigram_dic_cp={}
        self.bigram_dic={}
        self.bigram_dic_cp={}
        self.st_w={}
        for word in self.lex.keys():
            self.st_w[word]=fst.Weight('log',-math.log(1/len(self.lex.keys())))
            
    #1***: parse lexicon into a dic: { word: [phones] }
    def parse_lexicon(self,lex_file):
        lex={}
        with open(lex_file,'r') as f:
            for line in f:
                line=line.split()
                if line[0] in lex.keys():
                    line[0]=line[0]+'*'
                lex[line[0]]=line[1:]
        return lex

    #2***: generate fst. word_table; phone_table; state_table
    def generate_symbol_tables(self,lex_dic, n):
        word_table=fst.SymbolTable()
        phone_table=fst.SymbolTable()
        state_table=fst.SymbolTable()

        word_table.add_symbol('<eps>')
        phone_table.add_symbol('<eps>')
        state_table.add_symbol('<eps>')

        for w, ps in lex_dic.items():
            word_table.add_symbol(w)

            for p in ps:
                phone_table.add_symbol(p)
                for i in range(1,n+1):
                    state_table.add_symbol("{}_{}".format(p,i))

        return word_table, phone_table, state_table



    #3***: generate phone_n state wfst with final output phone
    def generate_phone_sequence_wfst(self, f, start_state, phone, n, sl_w, tr_w):
        
        current_state=start_state
        for i in range(1,n+1):
            in_label=self.state_table.find('{}_{}'.format(phone,i))
            f.add_arc(current_state, fst.Arc(in_label, 0, sl_w, current_state))
            if i==n:
                out_label=self.phone_table.find(phone)
            else:
                out_label=0
            next_state=f.add_state()
            f.add_arc(current_state, fst.Arc(in_label, out_label, tr_w, next_state))
            current_state=next_state
        return current_state
    
    #4***: generate word recognition wfst with phone_n state for each phone,
    # phone as output of each word sequence endstate
    def generate_word_recognition_wfst(self, n, sl_w, tr_w):
        f=fst.Fst('log')
        start_state=f.add_state()
        f.set_start(start_state)
        
        #remove_duplicate_phone=set()
        #for allphone in self.lex.values():
        #    remove_duplicate_phone = remove_duplicate_phone.union(allphone)
        
        for word, phones in self.lex.items():
            current_state=f.add_state()
            f.add_arc(start_state, fst.Arc(0, 0, self.st_w[word], current_state))
            for phone in phones:
                current_state=self.generate_phone_sequence_wfst(f, current_state, phone, n, sl_w, tr_w)
            f.set_final(current_state)
            f.add_arc(current_state, fst.Arc(0, 0, self.end_weight, start_state))
        f.set_input_symbols(self.state_table)
        f.set_output_symbols(self.phone_table)
        return f
    #5***: generate lexicon into wfst
    def generate_L_wfst(self):
        L=fst.Fst()
        start_state=L.add_state()
        L.set_start(start_state)
        
        for word, phones in self.lex.items():
            current_state=start_state
            for (i,phone) in enumerate(phones):
                next_state=L.add_state()
                if i==len(phones)-1:
                    L.add_arc(current_state, fst.Arc(self.phone_table.find(phone), self.word_table.find(word), None, next_state))
                else:
                    L.add_arc(current_state, fst.Arc(self.phone_table.find(phone), 0, None, next_state))
                current_state=next_state
            L.set_final(current_state)
            L.add_arc(current_state, fst.Arc(0,0,None,start_state))
        L.set_input_symbols(self.phone_table)
        L.set_output_symbols(self.word_table)
        return L
    
    #6***: generate linear phone sequence wfst
    def generate_linear_phone_wfst(self,seq_list):
        P=fst.Fst()
        start_state=P.add_state()
        P.set_start(start_state)
        
        for phone in seq_list:
            i_label=self.phone_table.find(phone)
            current_state=P.add_state()
            P.add_arc(start_state, fst.Arc(i_label,i_label,None,current_state))
            start_state=current_state
        P.set_final(start_state)
        P.set_input_symbols(self.phone_table)
        P.set_output_symbols(self.phone_table)
        return P                    
        
    #5***:generate word recognition wfst with phone_n state for each phone
    # word as final output of each word sequence endstate
    def generate_ow_word_recognition_wfst(self, n, sl_w, tr_w):
        fw=fst.Fst('log')
        start_state=fw.add_state()
        fw.set_start(start_state)
        
        for word, phones in self.lex.items():
            current_state=fw.add_state()
            fw.add_arc(start_state, fst.Arc(0, 0, self.st_w[word], current_state))
            for phone in phones:
                for i in range(1, n+1):
                    inlabel=self.state_table.find('{}_{}'.format(phone,i))
                    fw.add_arc(current_state, fst.Arc(inlabel, 0, sl_w, current_state))
                    if i==n and phone==phones[-1]:
                        outlabel=self.word_table.find(word)
                    else:
                        outlabel=0
                    next_state=fw.add_state()
                    fw.add_arc(current_state, fst.Arc(inlabel, outlabel, tr_w, next_state))
                    current_state=next_state
            fw.set_final(current_state)
            fw.add_arc(current_state, fst.Arc(0, 0, self.end_weight, start_state))
        fw.set_input_symbols(self.state_table)
        fw.set_output_symbols(self.word_table)
        return fw
    
    #6***: generate word recognition wfst with unigram probability with for each word path
    # with phone_n state for each phone
    # word as final output of each word sequence end state
    def generate_unigram_word_recognition_wfst(self, n, sl_w, tr_w, unigram_dic):
        fu=fst.Fst('log')
        start_state=fu.add_state()
        fu.set_start(start_state)
        
        for word, phones in self.lex.items():
            current_state=fu.add_state()
            if '*' in word:
                fu.add_arc(start_state, fst.Arc(0, 0, unigram_dic[word.rstrip('*')], current_state))
            else:
                fu.add_arc(start_state, fst.Arc(0, 0, unigram_dic[word], current_state))
            for phone in phones:
                for i in range(1, n+1):
                    inlabel=self.state_table.find('{}_{}'.format(phone,i))
                    fu.add_arc(current_state, fst.Arc(inlabel, 0, sl_w, current_state))
                    if i==n and phone==phones[-1]:
                        outlabel=self.word_table.find(word)
                    else:
                        outlabel=0
                    next_state=fu.add_state()
                    fu.add_arc(current_state, fst.Arc(inlabel, outlabel, tr_w, next_state))
                    current_state=next_state
            fu.set_final(current_state)
            fu.add_arc(current_state, fst.Arc(0, 0, self.end_weight, start_state))
        fu.set_input_symbols(self.state_table)
        fu.set_output_symbols(self.word_table)
        return fu
    # generate unigram dic: {'word': 'fst_type' log of probability} P(word_i)= word_i count / total words count
    def generate_unigram(self, txt_file_path):
        to_transcription=[]
        for txt_f in glob.glob(txt_file_path):
            with open(txt_f,'r') as f:
                tst=f.readline().strip()
                to_transcription+=tst.split( )
        for token in to_transcription:
            if token not in self.unigram_dic.keys():
                self.unigram_dic[token]=1
            else:
                self.unigram_dic[token]+=1
        self.unigram_dic_cp=self.unigram_dic.copy()
        for word in self.unigram_dic.keys():
            self.unigram_dic[word]=fst.Weight('log',-math.log(self.unigram_dic[word]/len(to_transcription)))
        return self.unigram_dic
    
    #7*** genenrate 5 state silence wfst:
    def add_silence_wfst(self, afst):
        n=5 # per silence state
        self.state_table.add_symbol('sil_1')
        self.state_table.add_symbol('sil_2')
        self.state_table.add_symbol('sil_3')
        self.state_table.add_symbol('sil_4')
        self.state_table.add_symbol('sil_5')
        wei_next=fst.Weight('log',-math.log(0.3))
        wei_3=fst.Weight('log',-math.log(1/3))
        wei_back=fst.Weight('log',-math.log(0.1))
        
        start_state=0
        afst.set_start(start_state)
        st_record=[]
        current_state=start_state
        
        for i in range(1,n+1):
            next_state=afst.add_state()
            st_record.append(next_state)
            if i== 3 or i==4:
                in_label= self.state_table.find('{}_{}'.format('sil',i))
                afst.add_arc(current_state, fst.Arc(in_label,0,wei_next,next_state))
                afst.add_arc(next_state, fst.Arc(in_label,0,wei_next,next_state))
                in_label= self.state_table.find('{}_{}'.format('sil',i-1))
                afst.add_arc(next_state, fst.Arc(in_label,0,wei_back,current_state))
            else:
                in_label= self.state_table.find('{}_{}'.format('sil',i))
                afst.add_arc(current_state, fst.Arc(in_label,0,wei_3,next_state))
                afst.add_arc(next_state, fst.Arc(in_label,0,wei_3,next_state))
            current_state=next_state
        for i in range(len(st_record)-1):
            i_label1=self.state_table.find('sil_5')
            if i ==2 or i==3:
                afst.add_arc(st_record[i], fst.Arc(i_label1,0,wei_next,next_state))
            else:
                afst.add_arc(st_record[i], fst.Arc(i_label1,0,wei_3,next_state))
        afst.set_final(next_state)
        afst.add_arc(next_state, fst.Arc(0,0,self.end_weight,start_state))
        afst.set_input_symbols(self.state_table)
        #afst.set_output_symbols(self.phone_table)
        return afst
    
    #8***:generate wfst with bigram language model weight
    def generate_bigram_word_recognition_wfst(self, n, sl_w, tr_w, unigram_dic, bigram_dic):
     
        #bigram_dict = generate_bigram_dict(recording_txt_files,lex)

        G = fst.Fst('log')
        start_state = G.add_state()
        G.set_start(start_state)

        for wordi, phones in self.lex.items():
            current_state=G.add_state()
            if '*' in wordi:
                G.add_arc(start_state, fst.Arc(0, 0, unigram_dic[wordi.rstrip('*')], current_state))
            else:
                G.add_arc(start_state, fst.Arc(0, 0, unigram_dic[wordi], current_state))
            for phone in phones:
                for i in range(1, n+1):
                    in_label=self.state_table.find('{}_{}'.format(phone, i))
                    G.add_arc(current_state, fst.Arc(in_label, 0, sl_w, current_state))
                    if i==n and phone==phones[-1]:
                        out_label=self.word_table.find(word)
                    else:
                        out_label=0
                    next_state=G.add_state()
                    G.add_arc(current_state, fst.Arc(in_label, out_label, tr_w, next_state))
                    current_state=next_state
            #add bigram model by change weight here, as we know Sum[ P(w'_i | w_1), ...., P(w'_i | w_n) ]= 1
            start_state_ii=current_state
            for wordii, phoneiis in self.lex.items():
                current_state_ii=G.add_state()
                if '*' in wordii:
                    wordii=wordii.rstrip('*')
                    G.add_arc(start_state_ii, fst.Arc(0, 0, bigram_dic[(wordi, wordii)], current_state_ii))
                else:
                    G.add_arc(start_state_ii, fst.Arc(0, 0, bigram_dic[(wordi, wordii)], current_state_ii))
                for phone in phoneiis:
                    for j in range(1, n+1):
                        inlabel_ii=self.state_table.find('{}_{}'.format(phone, i))
                        G.add_arc(current_state_ii, fst.Arc(inlabel_ii, 0, sl_w, current_state_ii))
                        if j==n and phone==phones[-1]:
                            outlabel_ii=self.word_table.find(wordii)
                        else:
                            outlabel_ii=0
                        next_state_ii=G.add_state()
                        G.add_arc(current_state_ii, fst.Arc(inlabel_ii, outlabel_ii, tr_w, next_state_ii))
                        current_state_ii=next_state_ii
            G.set_final(current_state_ii)
            G.add_arc(current_state_ii, fst.Arc(0, 0, self.end_weight, start_state))
        G.set_input_symbols(self.state_table)
        G.set_output_symbols(self.word_table)

        return G
    # compute the bigram dic: {'(w_i, w_i+1)' :  'fst_type' log of probability} P(w_i | w_i+1)= 'w_i, w_i+1' count / w_i count
    def generate_bigram(self, txt_file_path):
        to_transcription1=[]
        for txt_f in glob.glob(txt_file_path):
            with open(txt_f,'r') as f:
                tst=f.readline().strip()
                to_transcription1+=tst.split( )
        for ti in range(len(to_transcription1)-1):
            if (to_transcription1[ti],to_transcription1[ti+1]) not in self.bigram_dic.keys():
                self.bigram_dic[(to_transcription1[ti],to_transcription1[ti+1])]=1
            else:
                self.bigram_dic[(to_transcription1[ti],to_transcription1[ti+1])]+=1
        self.bigram_dic_cp=self.bigram_dic.copy()
        for ty in self.bigram_dic_cp:
            self.bigram_dic[ty]=fst.Weight('log',-math.log(self.bigram_dic[ty] / self.unigram_dic_cp[ty[0]]))
        return self.bigram_dic

In [2]:
import observation_model
import math

class ViterbiDecoder:
    Infinity=1e10 # define a constant represent -log(0)
    
    def __init__(self, f, audio_file_name):
        
        self.om=observation_model.ObservationModel()
        self.f=f
        self.forward_count=0
        if audio_file_name:
            self.om.load_audio(audio_file_name)
        self.initialise_decoding()
    
    #11***: initialise variables, function calling for assigning initial values
    def initialise_decoding(self):
        
        self.V=[]
        self.B=[]
        self.W=[]
        
        for t in range(self.om.observation_length()+1):
            self.V.append([self.Infinity]*self.f.num_states()) # V[t: 0->initial, 1~T][state number: 0~N] => values: maxP() or min-Log(P)
            self.B.append([-1]*self.f.num_states()) # B[t: 0 will not use, 1~T][state number: 0~N] => values: current state j B[t][j]=last state number i of BEST PATH( min(V[t][i]+ arc[i->j]_weight) )
            self.W.append([[] for i in range(self.f.num_states())]) # W[t: 0 will not use, 1~T][state number: 0~N] => values: [output_label] if output <eps> -> [], and the initial all are [] empty list
        
        self.V[0][self.f.start()]=0.0 #V[0][0]=0.0
        self.traverse_epsilon_arcs(0) #actually, t never has value '0'; this will give initil values of V[0][...]
        # consider every path (arcm, arcn,...) ends into a state j which's V[0][j]= min(arcm_w, arcn_w, ...)
        # consider the normal (word) wfst, state 0 has k arcs means k words (phone sequence sub_wfst)
        # maybe one example: V[0][1, 9, 15, 32] (so k here is 4), and the 1~8(8 as end state) is a phone sequence wfst
        # after do "self.traverse_epsilon_arcs(0)", only V[0][0, 1, 9, 15, 32] has values and V[0][0]=0.0 because
        # each V[0][i] will compare and save the smallest one! V[0][0] will compare V[0][8]+ arc[8->0]_weight; & V[0][14]+ arc[14->0]_weight
        # so I think whatever that V of (state pointer to state 0) and plus a arc_weight will be greater than just 0.0 => so V[0][0]= 0.0
        # Reminder!!! the min path only compare and asign when arc_input_label is <eps>! " if arc.ilabel==0: "
    
    #12***: traverse arcs with <eps> on the input at time t
    def traverse_epsilon_arcs(self, t):
        
        states_to_traverse=list(self.f.states())
        
        while states_to_traverse:
            i=states_to_traverse.pop(0) # always pop out the first (state number) of current state list
                                        # start from the first state (maybe 0)
            
            if self.V[t][i]==self.Infinity:
                continue # 0 probability means a disavaliable path
            for arc in self.f.arcs(i):
                
                if arc.ilabel==0: # if this is <eps> transition
                    j=arc.nextstate
                    
                    if self.V[t][j] > self.V[t][i]+float(arc.weight):
                        # if this path (at time t, V[t][i]+arc.w less than the original saved cost 
                        # at time t state, V[t][j])
                        # we may want to save this lowwer path to update the probability V[][]
                        # also, we need update the previous state number B[][]
                        self.V[t][j]= self.V[t][i]+float(arc.weight)
                        self.B[t][j]=self.B[t][i]
                        self.forward_count+=1
                        
                        if arc.olabel != 0: # also, if there's output, we should record that.
                                            # <eps> input laways have multiple arcs with multiple outputs
                                            # if the outputs is <eps>, it just pass this list to state J;
                                            # if not add the output label in the tail of the list and pass to state J
                            self.W[t][j] = self.W[t][i] + [arc.olabel]
                        else:
                            self.W[t][j] = self.W[t][i]
                        
                        if j not in states_to_traverse:
                            states_to_traverse.append(j)
    
    #13***: forward_step:
    def forward_step(self, t):
        
        for i in self.f.states(): # start with the fist state (maybe 0)
            if not self.V[t-1][i] == self.Infinity: # because the following assign is on state j, if previous t-1 and last i cost V[t-1][i] is 0 probability, pass by
                
                for arc in self.f.arcs(i): # arcs: selfloop, next phone_n, other connection
                    if arc.ilabel !=0: # <eps> transitions don't emit observation, so the <eps> input arc will not calculate here
                        #but the <eps> path will be compared in traverse Fnc, then the end state k (of other paths & <eps> path) 's V[at every t][k] will have the min(-log)
                        
                        j=arc.nextstate # laways assign next state; the 0 state will be (compare) and assign by all the end states' back arc
                        t_p=float(arc.weight) # arc_weigh = transition probability aij (qi->qj)
                        e_p= -self.om.log_observation_probability( self.f.input_symbols().find(arc.ilabel), t) # emission probability: P(label | obsevation Ot) label: state represent <=> also equals to (arc points to state j)'s inlabel 
                        # class om has log_observation_probability object, which input ('string', 'int')
                        p_j = t_p + e_p + self.V[t-1][i] # p_j also means temp V[t][j], the path cost in state j at time t = transition_P + emission_P + V[t-1][i] (becasue last time t-1 state i --arc--> current state j) 
                        
                        if p_j < self.V[t][j]: # Viterbi key not sum(path1 + path2), but compare and save min(paths) at each state
                            self.V[t][j]=p_j # this assign actually contains V[t-1][last state i], so imagine all the (future t)'s cost V will contain previous (t-1)'s cost; so this is how propagation in HMM (from one state to next time's state)
                            self.B[t][j]=i # So we need the best path from: from lower arc's parent state i
                            self.forward_count+=1
                            
                            if arc.olabel !=0: # example n=3, so only the phone_3 state has output: W[any t][phone_3]=[phone label]; else: W[any t][phone_1,2]=[]
                                self.W[t][j]=[arc.olabel]
                            else:
                                self.W[t][j]=[]
    #14***: generate finalise_decoding for make no output state in V[T] sets Inifinity value (which we won't except to compare in backtrace: min(V[-1]))
    # And we use float(f.final(end_state)) to get the end_state weight (intial 0.0) to add in the V[T][end_state]; float(not end state weight) intial is math.inf
    def finalise_decoding(self):
        for state in self.f.states():
            final_weight=float(self.f.final(state)) #if state isn't final state, output inf
            if self.V[-1][state]!=self.Infinity:
                if final_weight==math.inf:
                    self.V[-1][state]=self.Infinity # inf means the state is not a end_state, so there's no emit
                    #so set the cost to infinity, then we won't compare in backtrce
                else:
                    self.V[-1][state]=self.V[-1][state]+final_weight #if the end state has a weight, it will also be added in V
        finished=[x for x in self.V[-1] if x < self.Infinity]
        if not finished: #means there's no end_state in the V[T] <=> all state_weight is inf (as initial)
            print("No path got to the end of the observations.")
    
    #15***: decode main
    def decode(self):
        self.initialise_decoding()
        t=1
        while t<= self.om.observation_length():
            self.forward_step(t)
            self.traverse_epsilon_arcs(t)
            t+=1
        self.finalise_decoding()
    
    #16***: generate Viterbi algorithm to find minist cost path by backtracing
    def backtrace(self):
        best_final_state=self.V[-1].index(min(self.V[-1])) # this is min cost state index
        best_state_sequence=[best_final_state]
        best_out_sequence=[]
        
        t=self.om.observation_length()
        j=best_final_state
        
        while t>=0: # we can print W[t][j] & j & t to understand
            i=self.B[t][j] # as we save in B[t][j] is always the last best state i; here for intuition: there may be several same state here becasue they were in the selfloop, so the previous state is itself.
            best_state_sequence.append(i) #here add the connect state number of best path to the list behind, so it needs reverse.
            best_out_sequence=self.W[t][j]+best_out_sequence #each output will add in the list front, as it's from T to 1, so the final list will be correct sequence.
            j=i
            t-=1
        
        best_state_sequence.reverse() #from 'T to 1' to '1 to T'
        best_out_sequence=' '.join([self.f.output_symbols().find(label) for label in best_out_sequence]) #f.output_symbols() as set before is list of words in wfst
        
        return (best_state_sequence, best_out_sequence)
    
    #17***: pruning method decode & forward
    def decode_pruning(self,p_td):
        self.initialise_decoding()
        t=1
        while t<= self.om.observation_length():
            self.forward_step_pruning(t,p_td)
            self.traverse_epsilon_arcs(t)
            t+=1
        self.finalise_decoding()
    def forward_step_pruning(self, t, pruning_threshold):
        for i in self.f.states(): # start with the fist state (maybe 0)
            if not self.V[t-1][i] == self.Infinity: # because the following assign is on state j, if previous t-1 and last i cost V[t-1][i] is 0 probability, pass by
                
                if self.V[t-1][i]< pruning_threshold: # the path cost is P*P*P... for eahc time, when -log(): it should be v1+v2+v3+...vT
                    for arc in self.f.arcs(i): # arcs: selfloop, next phone_n, other connection
                        if arc.ilabel !=0: # <eps> transitions don't emit observation, so the <eps> input arc will not calculate here
                            #but the <eps> path will be compared in traverse Fnc, then the end state k (of other paths & <eps> path) 's V[at every t][k] will have the min(-log)

                            j=arc.nextstate # laways assign next state; the 0 state will be (compare) and assign by all the end states' back arc
                            t_p=float(arc.weight) # arc_weigh = transition probability aij (qi->qj)
                            e_p= -self.om.log_observation_probability( self.f.input_symbols().find(arc.ilabel), t) # emission probability: P(label | obsevation Ot) label: state represent <=> also equals to (arc points to state j)'s inlabel 
                            # class om has log_observation_probability object, which input ('string', 'int')
                            p_j = t_p + e_p + self.V[t-1][i] # p_j also means temp V[t][j], the path cost in state j at time t = transition_P + emission_P + V[t-1][i] (becasue last time t-1 state i --arc--> current state j) 

                            if p_j < self.V[t][j]: # Viterbi key not sum(path1 + path2), but compare and save min(paths) at each state
                                self.V[t][j]=p_j # this assign actually contains V[t-1][last state i], so imagine all the (future t)'s cost V will contain previous (t-1)'s cost; so this is how propagation in HMM (from one state to next time's state)
                                self.B[t][j]=i # So we need the best path from: from lower arc's parent state i
                                self.forward_count+=1

                                if arc.olabel !=0: # example n=3, so only the phone_3 state has output: W[any t][phone_3]=[phone label]; else: W[any t][phone_1,2]=[]
                                    self.W[t][j]=[arc.olabel]
                                else:
                                    self.W[t][j]=[]
    
    #17***: Beamsearch method decode & forward
    def decode_beamsearch(self,b_td):
        self.initialise_decoding()
        t=1
        while t<= self.om.observation_length():
            self.forward_step_beam(t,b_td)
            self.traverse_epsilon_arcs(t)
            t+=1
        self.finalise_decoding()
    def forward_step_beam(self, t, beam_threshold):
        Vt=[self.V[t-1][i] for i in self.f.states()]#collect all of the probs for states in timestep t-1
        beam_s = []
        for index, value in sorted(enumerate(Vt), key=lambda x:x[1]):
            beam_s.append(index)
        beam_s=beam_s[:beam_threshold]
        for i in beam_s: # start with the fist state (maybe 0)
            if not self.V[t-1][i] == self.Infinity: # because the following assign is on state j, if previous t-1 and last i cost V[t-1][i] is 0 probability, pass by
                
                for arc in self.f.arcs(i): # arcs: selfloop, next phone_n, other connection
                    if arc.ilabel !=0: # <eps> transitions don't emit observation, so the <eps> input arc will not calculate here
                        #but the <eps> path will be compared in traverse Fnc, then the end state k (of other paths & <eps> path) 's V[at every t][k] will have the min(-log)
                        
                        j=arc.nextstate # laways assign next state; the 0 state will be (compare) and assign by all the end states' back arc
                        t_p=float(arc.weight) # arc_weigh = transition probability aij (qi->qj)
                        e_p= -self.om.log_observation_probability( self.f.input_symbols().find(arc.ilabel), t) # emission probability: P(label | obsevation Ot) label: state represent <=> also equals to (arc points to state j)'s inlabel 
                        # class om has log_observation_probability object, which input ('string', 'int')
                        p_j = t_p + e_p + self.V[t-1][i] # p_j also means temp V[t][j], the path cost in state j at time t = transition_P + emission_P + V[t-1][i] (becasue last time t-1 state i --arc--> current state j) 
                        
                        if p_j < self.V[t][j]: # Viterbi key not sum(path1 + path2), but compare and save min(paths) at each state
                            self.V[t][j]=p_j # this assign actually contains V[t-1][last state i], so imagine all the (future t)'s cost V will contain previous (t-1)'s cost; so this is how propagation in HMM (from one state to next time's state)
                            self.B[t][j]=i # So we need the best path from: from lower arc's parent state i
                            self.forward_count+=1
                            
                            if arc.olabel !=0: # example n=3, so only the phone_3 state has output: W[any t][phone_3]=[phone label]; else: W[any t][phone_1,2]=[]
                                self.W[t][j]=[arc.olabel]
                            else:
                                self.W[t][j]=[]

In [3]:
import glob
import os
import wer
import observation_model
import timeit
import numpy

txt_files = '/group/teaching/asr/labs/recordings/*.txt'
wav_files = '/group/teaching/asr/labs/recordings/*.wav'

#21***: Fnc for get standard transcription from wav matched file
def get_transcription(f_wav):
    f_txt=os.path.splitext(f_wav)[0]+'.txt'
    with open(f_txt, 'r') as f:
        transcription=f.readline().strip()
    return transcription

#22***: Fnc for experiment set up
def experiment_set_up(mode, s_w, t_w, pru_td):
    wfst=CreateWFST()
    L=wfst.generate_L_wfst()
    selfloop_weight=fst.Weight('log',-math.log(s_w))
    transist_weight=fst.Weight('log',-math.log(t_w))
    if mode == 'pru_b_w':
        pruning_threshold=float(fst.Weight('log',pru_td))
    elif mode == 'beam_b_w':
        beam_threshold=int(pru_td)
    #v1=ViterbiDecoder()
    #1****b_p
    if mode == 'b_p':
        F=wfst.generate_word_recognition_wfst(3,selfloop_weight,transist_weight) #step1: create wfst
        
        print("Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence")
        print("Phone per state: 3\nStart Weight: -log(1.0)\nEnd Weight: initial(0.0)")
        print("Selfloop Weight:",selfloop_weight,"-log({})".format(s_w))
        print("Transist Weight:",transist_weight,"-log({})".format(t_w))
        arcs_1=0
        states_1=0
        for s_1 in F.states():
            states_1+=1
            for a_1 in F.arcs(s_1):
                arcs_1+=1
        print("Memory Cost: States Count: %d  Arcs Count:%d"%(states_1,arcs_1))
        
        decode_time_1=[]
        backtrace_time_1=[]
        forward_count_1=[]
        to_error_count_1=[]
        to_transcription_1=[]
        for wav in glob.glob(wav_files):
            v1=ViterbiDecoder(F,wav)
            
            start_de_time_1= timeit.default_timer() #decode
            v1.decode()
            end_de_time_1= timeit.default_timer()
            decode_time_1.append(end_de_time_1-start_de_time_1)
            
            start_ba_time_1= timeit.default_timer() #backtrace
            (path_states_1, phone_seq_1)=v1.backtrace()
            #print(list(phone_seq_1))
            #s=input()
            P_1=wfst.generate_linear_phone_wfst(phone_seq_1.split())# input should be list
            P_1.arcsort(sort_type='ilabel')
            comp_1=fst.compose(P_1,L)
            comp_1.project(project_output='True')
            comp_1.rmepsilon()
            #comp_1.draw('tu.dot',portrait=True)
            #check_call(['dot','-Tpng','-Gdpi=1000','tu.dot','-o','tu.png'])
            #Image(filename='tu.png')
            #s=input()
            word_seq_1=[]
            for q_1 in comp_1.states():
                for arc_1 in comp_1.arcs(q_1):
                    word_seq_1.append(comp_1.output_symbols().find(arc_1.olabel))
            end_ba_time_1= timeit.default_timer()
            backtrace_time_1.append(end_ba_time_1-start_ba_time_1)
            forward_count_1.append(v1.forward_count) # after decode, the count should has values
            
            word_seq_1=' '.join(word_seq_1)
            word_seq_1=word_seq_1.replace('*','')
            transcription_1=get_transcription(wav)
            error_counts_1=wer.compute_alignment_errors(transcription_1,word_seq_1)
            WER_1=sum(error_counts_1)/len(transcription_1.split())
            to_error_count_1.append(sum(error_counts_1))
            to_transcription_1.append(len(transcription_1.split()))
            
            print("\n\n*****************************************")
            print("File:",wav,"\nSpeed of Viterbi Decoder:",decode_time_1[-1],"s"," Speed of Backtrace:",backtrace_time_1[-1],"s"," Forward Count:",forward_count_1[-1])
            #print("D:",(start_de_time_1-end_de_time_1),decode_time_1[-1],"B:",start_ba_time_1-end_ba_time_1,backtrace_time_1[-1],"F:",v1.forward_count,forward_count_1[-1])
            print("(Substitutions, Deletions, Insertions) N:", error_counts_1, len(transcription_1.split()))
            print("WER:",WER_1)
            print("Trascription:",transcription_1)
            print("Recognition:",word_seq_1)
        print("Average")
        print("Total Errors:",sum(to_error_count_1))
        print("Total Transcription Words:",sum(to_transcription_1))
        print("Total WER:",sum(to_error_count_1) / sum(to_transcription_1))
        print("The number of forward computations per wav: ",sum(forward_count_1)/len(forward_count_1))
        print("Average decode time:",numpy.mean(decode_time_1))
        print("Average backtrace time:",numpy.mean(backtrace_time_1))
    
    #2****b_w
    elif mode == 'b_w':
        F_bw=wfst.generate_ow_word_recognition_wfst(3,selfloop_weight,transist_weight) #step1: create specific kind of wfst
        
        print("Mode: Baseline Recognition, WFST set only word label output on its arc path")
        print("Phone per state: 3\nStart Weight: -log(1.0)\nEnd Weight: initial(0.0)")
        print("Selfloop Weight:",selfloop_weight,"-log({})".format(s_w))
        print("Transist Weight:",transist_weight,"-log({})".format(t_w))
        arcs_2=0
        states_2=0
        for s_2 in F_bw.states():
            states_2+=1
            for a_2 in F_bw.arcs(s_2):
                arcs_2+=1
        print("Memory Cost: States Count: %d  Arcs Count:%d"%(states_2,arcs_2))
        
        decode_time_2=[]
        backtrace_time_2=[]
        forward_count_2=[]
        to_error_count_2=[]
        to_transcription_2=[]
        for wav_2 in glob.glob(wav_files):
            v2=ViterbiDecoder(F_bw,wav_2) #step2: create Viterbi instance for wfst
            
            start_de_time_2= timeit.default_timer() #step3: decode
            v2.decode()
            end_de_time_2= timeit.default_timer()
            decode_time_2.append(end_de_time_2-start_de_time_2)
            
            start_ba_time_2= timeit.default_timer() #step4: backtrace
            (path_states_2, word_seq_2)=v2.backtrace()
            #word_seq_1=[]
            
            end_ba_time_2= timeit.default_timer()
            backtrace_time_2.append(end_ba_time_2-start_ba_time_2)
            forward_count_2.append(v2.forward_count) # after decode, the count should has values
            
            word_seq_2=word_seq_2.replace('*','') #step5: compare result with transcript and comput WER
            transcription_2=get_transcription(wav_2)
            error_counts_2=wer.compute_alignment_errors(transcription_2,word_seq_2)
            WER_2=sum(error_counts_2)/len(transcription_2.split())
            to_error_count_2.append(sum(error_counts_2))
            to_transcription_2.append(len(transcription_2.split()))
            
            print("\n\n*****************************************")
            print("File:",wav_2,"\nSpeed of Viterbi Decoder:",decode_time_2[-1],"s"," Speed of Backtrace:",backtrace_time_2[-1],"s"," Forward Count:",forward_count_2[-1])
            #print("D:",(start_de_time_1-end_de_time_1),decode_time_1[-1],"B:",start_ba_time_1-end_ba_time_1,backtrace_time_1[-1],"F:",v1.forward_count,forward_count_1[-1])
            print("(Substitutions, Deletions, Insertions) N:", error_counts_2, len(transcription_2.split()))
            print("WER:",WER_2)
            print("Trascription:",transcription_2)
            print("Recognition:",word_seq_2)
        print("Average")
        print("Total Errors:",sum(to_error_count_2))
        print("Total Transcription Words:",sum(to_transcription_2))
        print("Total WER:",sum(to_error_count_2) / sum(to_transcription_2))
        print("The number of forward computations per wav: ",sum(forward_count_2)/len(forward_count_2))
        print("Average decode time:",numpy.mean(decode_time_2))
        print("Average backtrace time:",numpy.mean(backtrace_time_2))
    
    #3****uni_w
    elif mode == 'uni_w':
        #txt_files = '/group/teaching/asr/labs/recordings/*.txt'
        uni_dic_3=wfst.generate_unigram(txt_files)
        F_uni=wfst.generate_unigram_word_recognition_wfst(3,selfloop_weight,transist_weight,uni_dic_3) #step1: create wfst
        
        print("Mode: Baseline Recognition, WFST set only word label output on its arc path")
        print("Phone per state: 3\nStart Weight: -log(1.0)\nEnd Weight: initial(0.0)")
        print("Selfloop Weight:",selfloop_weight,"-log({})".format(s_w))
        print("Transist Weight:",transist_weight,"-log({})".format(t_w))
        arcs_3=0
        states_3=0
        for s_3 in F_uni.states():
            states_3+=1
            for a_3 in F_uni.arcs(s_3):
                arcs_3+=1
        print("Memory Cost: States Count: %d  Arcs Count:%d"%(states_3,arcs_3))
        
        decode_time_3=[]
        backtrace_time_3=[]
        forward_count_3=[]
        to_error_count_3=[]
        to_transcription_3=[]
        for wav_3 in glob.glob(wav_files):
            v3=ViterbiDecoder(F_uni,wav_3)
            
            start_de_time_3= timeit.default_timer() #decode
            v3.decode()
            end_de_time_3= timeit.default_timer()
            decode_time_3.append(end_de_time_3-start_de_time_3)
            
            start_ba_time_3= timeit.default_timer() #backtrace
            (path_states_3, word_seq_3)=v3.backtrace()
            #word_seq_1=[]
            
            end_ba_time_3= timeit.default_timer()
            backtrace_time_3.append(end_ba_time_3-start_ba_time_3)
            forward_count_3.append(v3.forward_count) # after decode, the count should has values
            
            word_seq_3=word_seq_3.replace('*','')
            transcription_3=get_transcription(wav_3)
            error_counts_3=wer.compute_alignment_errors(transcription_3,word_seq_3)
            WER_3=sum(error_counts_3)/len(transcription_3.split())
            to_error_count_3.append(sum(error_counts_3))
            to_transcription_3.append(len(transcription_3.split()))
            
            print("\n\n*****************************************")
            print("File:",wav_3,"\nSpeed of Viterbi Decoder:",decode_time_3[-1],"s"," Speed of Backtrace:",backtrace_time_3[-1],"s"," Forward Count:",forward_count_3[-1])
            #print("D:",(start_de_time_1-end_de_time_1),decode_time_1[-1],"B:",start_ba_time_1-end_ba_time_1,backtrace_time_1[-1],"F:",v1.forward_count,forward_count_1[-1])
            print("(Substitutions, Deletions, Insertions) N:", error_counts_3, len(transcription_3.split()))
            print("WER:",WER_3)
            print("Trascription:",transcription_3)
            print("Recognition:",word_seq_3)
        print("Average")
        print("Total Errors:",sum(to_error_count_3))
        print("Total Transcription Words:",sum(to_transcription_3))
        print("Total WER:",sum(to_error_count_3) / sum(to_transcription_3))
        print("The number of forward computations per wav: ",sum(forward_count_3)/len(forward_count_3))
        print("Average decode time:",numpy.mean(decode_time_3))
        print("Average backtrace time:",numpy.mean(backtrace_time_3))
    
    #4*** Pruning implement in baseline 
    elif mode == 'pru_b_w':
        Pru_bw=wfst.generate_ow_word_recognition_wfst(3,selfloop_weight,transist_weight) #step1: create wfst
        
        print("Mode: Baseline Recognition, WFST set only word label output on its arc path")
        print("Phone per state: 3\nStart Weight: -log(1.0)\nEnd Weight: initial(0.0)")
        print("Selfloop Weight:",selfloop_weight,"-log({})".format(s_w))
        print("Transist Weight:",transist_weight,"-log({})".format(t_w))
        arcs_4=0
        states_4=0
        for s_4 in Pru_bw.states():
            states_4+=1
            for a_4 in Pru_bw.arcs(s_4):
                arcs_4+=1
        print("Memory Cost: States Count: %d  Arcs Count:%d"%(states_4,arcs_4))
        
        decode_time_4=[]
        backtrace_time_4=[]
        forward_count_4=[]
        to_error_count_4=[]
        to_transcription_4=[]
        for wav_4 in glob.glob(wav_files):
            v4=ViterbiDecoder(Pru_bw,wav_4)
            
            start_de_time_4= timeit.default_timer() #decode
            v4.decode_pruning(pruning_threshold)
            end_de_time_4= timeit.default_timer()
            decode_time_4.append(end_de_time_4-start_de_time_4)
            
            start_ba_time_4= timeit.default_timer() #backtrace
            (path_states_4, word_seq_4)=v4.backtrace()
            #word_seq_1=[]
            
            end_ba_time_4= timeit.default_timer()
            backtrace_time_4.append(end_ba_time_4-start_ba_time_4)
            forward_count_4.append(v4.forward_count) # after decode, the count should has values
            
            word_seq_4=word_seq_4.replace('*','')
            transcription_4=get_transcription(wav_4)
            error_counts_4=wer.compute_alignment_errors(transcription_4,word_seq_4)
            WER_4=sum(error_counts_4)/len(transcription_4.split())
            to_error_count_4.append(sum(error_counts_4))
            to_transcription_4.append(len(transcription_4.split()))
            
            print("\n\n*****************************************")
            print("File:",wav_4,"\nSpeed of Viterbi Decoder:",decode_time_4[-1],"s"," Speed of Backtrace:",backtrace_time_4[-1],"s"," Forward Count:",forward_count_4[-1])
            print("(Substitutions, Deletions, Insertions) N:", error_counts_4, len(transcription_4.split()))
            print("WER:",WER_4)
            print("Trascription:",transcription_4)
            print("Recognition:",word_seq_4)
        print("Average")
        print("Total Errors:",sum(to_error_count_4))
        print("Total Transcription Words:",sum(to_transcription_4))
        print("Total WER:",sum(to_error_count_4) / sum(to_transcription_4))
        print("The number of forward computations per wav: ",sum(forward_count_4)/len(forward_count_4))
        print("Average decode time:",numpy.mean(decode_time_4))
        print("Average backtrace time:",numpy.mean(backtrace_time_4))
    
    #5*** Beamsearch implement in baseline 
    elif mode == 'beam_b_w':
        Beam_bw=wfst.generate_ow_word_recognition_wfst(3,selfloop_weight,transist_weight) #step1: create wfst
        
        print("Mode: Baseline Recognition, WFST set only word label output on its arc path")
        print("Phone per state: 3\nStart Weight: -log(1.0)\nEnd Weight: initial(0.0)")
        print("Selfloop Weight:",selfloop_weight,"-log({})".format(s_w))
        print("Transist Weight:",transist_weight,"-log({})".format(t_w))
        arcs_5=0
        states_5=0
        for s_5 in Beam_bw.states():
            states_5+=1
            for a_5 in Beam_bw.arcs(s_5):
                arcs_5+=1
        print("Memory Cost: States Count: %d  Arcs Count:%d"%(states_5,arcs_5))
        
        decode_time_5=[]
        backtrace_time_5=[]
        forward_count_5=[]
        to_error_count_5=[]
        to_transcription_5=[]
        for wav_5 in glob.glob(wav_files):
            v5=ViterbiDecoder(Beam_bw,wav_5)
            
            start_de_time_5= timeit.default_timer() #decode
            v5.decode_beamsearch(beam_threshold)
            end_de_time_5= timeit.default_timer()
            decode_time_5.append(end_de_time_5-start_de_time_5)
            
            start_ba_time_5= timeit.default_timer() #backtrace
            (path_states_5, word_seq_5)=v5.backtrace()
            #word_seq_1=[]
            
            end_ba_time_5= timeit.default_timer()
            backtrace_time_5.append(end_ba_time_5-start_ba_time_5)
            forward_count_5.append(v5.forward_count) # after decode, the count should has values
            
            word_seq_5=word_seq_5.replace('*','')
            transcription_5=get_transcription(wav_5)
            error_counts_5=wer.compute_alignment_errors(transcription_5,word_seq_5)
            WER_5=sum(error_counts_5)/len(transcription_5.split())
            to_error_count_5.append(sum(error_counts_5))
            to_transcription_5.append(len(transcription_5.split()))
            
            print("\n\n*****************************************")
            print("File:",wav_5,"\nSpeed of Viterbi Decoder:",decode_time_5[-1],"s"," Speed of Backtrace:",backtrace_time_5[-1],"s"," Forward Count:",forward_count_5[-1])
            print("(Substitutions, Deletions, Insertions) N:", error_counts_5, len(transcription_5.split()))
            print("WER:",WER_5)
            print("Trascription:",transcription_5)
            print("Recognition:",word_seq_5)
        print("Average")
        print("Total Errors:",sum(to_error_count_5))
        print("Total Transcription Words:",sum(to_transcription_5))
        print("Total WER:",sum(to_error_count_5) / sum(to_transcription_5))
        print("The number of forward computations per wav: ",sum(forward_count_5)/len(forward_count_5))
        print("Average decode time:",numpy.mean(decode_time_5))
        print("Average backtrace time:",numpy.mean(backtrace_time_5))
    
    #6****add silence to baseline
    elif mode == 'sil_b_w':
        Sil_bw=wfst.generate_ow_word_recognition_wfst(3,selfloop_weight,transist_weight) #step1: create wfst
        Sil_bw=wfst.add_silence_wfst(Sil_bw)
        
        print("Mode: Baseline Recognition, WFST set only word label output on its arc path")
        print("Phone per state: 3\nStart Weight: -log(1.0)\nEnd Weight: initial(0.0)")
        print("Selfloop Weight:",selfloop_weight,"-log({})".format(s_w))
        print("Transist Weight:",transist_weight,"-log({})".format(t_w))
        arcs_6=0
        states_6=0
        for s_6 in Sil_bw.states():
            states_6+=1
            for a_6 in Sil_bw.arcs(s_6):
                arcs_6+=1
        print("Memory Cost: States Count: %d  Arcs Count:%d"%(states_6,arcs_6))
        
        decode_time_6=[]
        backtrace_time_6=[]
        forward_count_6=[]
        to_error_count_6=[]
        to_transcription_6=[]
        for wav_6 in glob.glob(wav_files):
            v6=ViterbiDecoder(Sil_bw,wav_6)
            
            start_de_time_6= timeit.default_timer() #decode
            v6.decode()
            end_de_time_6= timeit.default_timer()
            decode_time_6.append(end_de_time_6-start_de_time_6)
            
            start_ba_time_6= timeit.default_timer() #backtrace
            (path_states_6, word_seq_6)=v6.backtrace()
            #word_seq_1=[]
            
            end_ba_time_6= timeit.default_timer()
            backtrace_time_6.append(end_ba_time_6-start_ba_time_6)
            forward_count_6.append(v6.forward_count) # after decode, the count should has values
            
            word_seq_6=word_seq_6.replace('*','')
            transcription_6=get_transcription(wav_6)
            error_counts_6=wer.compute_alignment_errors(transcription_6,word_seq_6)
            WER_6=sum(error_counts_6)/len(transcription_6.split())
            to_error_count_6.append(sum(error_counts_6))
            to_transcription_6.append(len(transcription_6.split()))
            
            print("\n\n*****************************************")
            print("File:",wav_6,"\nSpeed of Viterbi Decoder:",decode_time_6[-1],"s"," Speed of Backtrace:",backtrace_time_6[-1],"s"," Forward Count:",forward_count_6[-1])
            #print("D:",(start_de_time_1-end_de_time_1),decode_time_1[-1],"B:",start_ba_time_1-end_ba_time_1,backtrace_time_1[-1],"F:",v1.forward_count,forward_count_1[-1])
            print("(Substitutions, Deletions, Insertions) N:", error_counts_6, len(transcription_6.split()))
            print("WER:",WER_6)
            print("Trascription:",transcription_6)
            print("Recognition:",word_seq_6)
        print("Average")
        print("Total Errors:",sum(to_error_count_6))
        print("Total Transcription Words:",sum(to_transcription_6))
        print("Total WER:",sum(to_error_count_6) / sum(to_transcription_6))
        print("The number of forward computations per wav: ",sum(forward_count_6)/len(forward_count_6))
        print("Average decode time:",numpy.mean(decode_time_6))
        print("Average backtrace time:",numpy.mean(backtrace_time_6))
    #7****preprocess the lexicon into Tree structure generate wfst
    elif mode == 'tree_b_w':
        Tree_bw=wfst.generate_ow_word_recognition_wfst(3,selfloop_weight,transist_weight) #step1: create wfst
        Tree_bw=fst.determinize(Tree_bw)
        
        print("Mode: Baseline Recognition, WFST set only word label output on its arc path")
        print("Phone per state: 3\nStart Weight: -log(1.0)\nEnd Weight: initial(0.0)")
        print("Selfloop Weight:",selfloop_weight,"-log({})".format(s_w))
        print("Transist Weight:",transist_weight,"-log({})".format(t_w))
        arcs_7=0
        states_7=0
        for s_7 in Tree_bw.states():
            states_7+=1
            for a_7 in Tree_bw.arcs(s_7):
                arcs_7+=1
        print("Memory Cost: States Count: %d  Arcs Count:%d"%(states_7,arcs_7))
        
        decode_time_7=[]
        backtrace_time_7=[]
        forward_count_7=[]
        to_error_count_7=[]
        to_transcription_7=[]
        for wav_7 in glob.glob(wav_files):
            v7=ViterbiDecoder(Tree_bw,wav_7)
            
            start_de_time_7= timeit.default_timer() #decode
            v7.decode()
            end_de_time_7= timeit.default_timer()
            decode_time_7.append(end_de_time_7-start_de_time_7)
            
            start_ba_time_7= timeit.default_timer() #backtrace
            (path_states_7, word_seq_7)=v7.backtrace()
            #word_seq_1=[]
            
            end_ba_time_7= timeit.default_timer()
            backtrace_time_7.append(end_ba_time_7-start_ba_time_7)
            forward_count_7.append(v7.forward_count) # after decode, the count should has values
            
            word_seq_7=word_seq_7.replace('*','')
            transcription_7=get_transcription(wav_7)
            error_counts_7=wer.compute_alignment_errors(transcription_7,word_seq_7)
            WER_7=sum(error_counts_7)/len(transcription_7.split())
            to_error_count_7.append(sum(error_counts_7))
            to_transcription_7.append(len(transcription_7.split()))
            
            print("\n\n*****************************************")
            print("File:",wav_7,"\nSpeed of Viterbi Decoder:",decode_time_7[-1],"s"," Speed of Backtrace:",backtrace_time_7[-1],"s"," Forward Count:",forward_count_7[-1])
            #print("D:",(start_de_time_1-end_de_time_1),decode_time_1[-1],"B:",start_ba_time_1-end_ba_time_1,backtrace_time_1[-1],"F:",v1.forward_count,forward_count_1[-1])
            print("(Substitutions, Deletions, Insertions) N:", error_counts_7, len(transcription_7.split()))
            print("WER:",WER_7)
            print("Trascription:",transcription_7)
            print("Recognition:",word_seq_7)
        print("Average")
        print("Total Errors:",sum(to_error_count_7))
        print("Total Transcription Words:",sum(to_transcription_7))
        print("Total WER:",sum(to_error_count_7) / sum(to_transcription_7))
        print("The number of forward computations per wav: ",sum(forward_count_7)/len(forward_count_7))
        print("Average decode time:",numpy.mean(decode_time_7))
        print("Average backtrace time:",numpy.mean(backtrace_time_7))
    #8****b_w
    elif mode == 'big_b_w':
        Bi_f=wfst.generate_ow_word_recognition_wfst(3,selfloop_weight,transist_weight) #step1: create wfst
        uni_dic_8=wfst.generate_unigram(txt_files)
        big_dic_8=wfst.generate_bigram(txt_files)
        Bi_g=wfst.generate_bigram_word_recognition_wfst(3,selfloop_weight,transist_weight,uni_dic_3,big_dic_8)
        #Bi_g=fst.determinize(Bi_g)
        #Bi_f=fst.determinize(Bi_f)
        Bi_f.arcsort(sort_type ='olabel')
        #g=fst.determinize(g)
        #f1=fst.determinize(f1)
        Bi_bw=fst.compose(Bi_f, Bi_g)
        #Bi_bw=fst.determinize(Bi_bw)
        #Bi_bw.minimize()
        #Bi_bw.rmepsilon()
        
        print("Mode: Baseline Recognition, WFST set only word label output on its arc path")
        print("Phone per state: 3\nStart Weight: -log(1.0)\nEnd Weight: initial(0.0)")
        print("Selfloop Weight:",selfloop_weight,"-log({})".format(s_w))
        print("Transist Weight:",transist_weight,"-log({})".format(t_w))
        arcs_8=0
        states_8=0
        for s_8 in Bi_bw.states():
            states_8+=1
            for a_8 in Bi_bw.arcs(s_8):
                arcs_8+=1
        print("Memory Cost: States Count: %d  Arcs Count:%d"%(states_8,arcs_8))
        
        decode_time_8=[]
        backtrace_time_8=[]
        forward_count_8=[]
        to_error_count_8=[]
        to_transcription_8=[]
        for wav_8 in glob.glob(wav_files):
            v8=ViterbiDecoder(Bi_bw,wav_8)
            
            start_de_time_8= timeit.default_timer() #decode
            v8.decode()
            end_de_time_8= timeit.default_timer()
            decode_time_8.append(end_de_time_8-start_de_time_8)
            
            start_ba_time_8= timeit.default_timer() #backtrace
            (path_states_8, word_seq_8)=v8.backtrace()
            #word_seq_1=[]
            
            end_ba_time_8= timeit.default_timer()
            backtrace_time_8.append(end_ba_time_8-start_ba_time_8)
            forward_count_8.append(v8.forward_count) # after decode, the count should has values
            
            word_seq_8=word_seq_8.replace('*','')
            transcription_8=get_transcription(wav_8)
            error_counts_8=wer.compute_alignment_errors(transcription_8,word_seq_8)
            WER_8=sum(error_counts_8)/len(transcription_8.split())
            to_error_count_8.append(sum(error_counts_8))
            to_transcription_8.append(len(transcription_8.split()))
            
            print("\n\n*****************************************")
            print("File:",wav_8,"\nSpeed of Viterbi Decoder:",decode_time_8[-1],"s"," Speed of Backtrace:",backtrace_time_8[-1],"s"," Forward Count:",forward_count_8[-1])
            #print("D:",(start_de_time_1-end_de_time_1),decode_time_1[-1],"B:",start_ba_time_1-end_ba_time_1,backtrace_time_1[-1],"F:",v1.forward_count,forward_count_1[-1])
            print("(Substitutions, Deletions, Insertions) N:", error_counts_8, len(transcription_8.split()))
            print("WER:",WER_8)
            print("Trascription:",transcription_8)
            print("Recognition:",word_seq_8)
        print("Average")
        print("Total Errors:",sum(to_error_count_8))
        print("Total Transcription Words:",sum(to_transcription_8))
        print("Total WER:",sum(to_error_count_8) / sum(to_transcription_8))
        print("The number of forward computations per wav: ",sum(forward_count_8)/len(forward_count_8))
        print("Average decode time:",numpy.mean(decode_time_8))
        print("Average backtrace time:",numpy.mean(backtrace_time_8))
    
    return

# Baseline selfloop weight & transist weight 0.1 -> 0.9

In [5]:
experiment_set_up('b_p', 0.1, 0.9, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 2.30258512 -log(0.1)
Transist Weight: 0.105360515 -log(0.9)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 5.537143981084228 s  Speed of Backtrace: 0.008577633649110794 s  Forward Count: 79131
(Substitutions, Deletions, Insertions) N: (1, 0, 15) 8
WER: 2.0
Trascription: of of a peter the piper the pickled
Recognition: peck the a of a of the of peter the peck a of picked a piper pickled the the pickled picked the a


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 8.127777324058115 s  Speed of Backtrace: 0.0072995759546756744 s  Forward Count: 149566
(Substitutions, Deletions, Insertions) N: (0, 1, 13) 10
WER: 1.4
Tra



*****************************************
File: /group/teaching/asr/labs/recordings/0019.wav 
Speed of Viterbi Decoder: 6.39090842474252 s  Speed of Backtrace: 0.009684259071946144 s  Forward Count: 116404
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 8
WER: 1.5
Trascription: the peck of pickled peppers peter piper picked
Recognition: pickled the picked picked of pickled peppers the of peck picked picked the the picked the the


*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.5110816154628992 s  Speed of Backtrace: 0.0038913479074835777 s  Forward Count: 24646
(Substitutions, Deletions, Insertions) N: (1, 0, 7) 3
WER: 2.6666666666666665
Trascription: peter piper picked
Recognition: peck the peter of of of a peppers picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.924666746519506 s  Speed of Backtrace: 0.00689839199185371



*****************************************
File: /group/teaching/asr/labs/recordings/0038.wav 
Speed of Viterbi Decoder: 7.207703908905387 s  Speed of Backtrace: 0.008431981317698956 s  Forward Count: 111758
(Substitutions, Deletions, Insertions) N: (7, 0, 11) 17
WER: 1.0588235294117647
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the pickled piper of a picked peck of the peck of where's where's picked of picked the peck of where's the pickled piper peck picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 6.204834218136966 s  Speed of Backtrace: 0.00684063695371151 s  Forward Count: 124304
(Substitutions, Deletions, Insertions) N: (4, 0, 14) 17
WER: 1.0588235294117647
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the of pete



*****************************************
File: /group/teaching/asr/labs/recordings/0057.wav 
Speed of Viterbi Decoder: 5.574689255096018 s  Speed of Backtrace: 0.0059271641075611115 s  Forward Count: 96781
(Substitutions, Deletions, Insertions) N: (2, 0, 10) 13
WER: 0.9230769230769231
Trascription: where's peter pickled peck of pickled peppers the peck piper picked a peppers
Recognition: the the where's peter of pickled peck of pickled peppers the peck picked picked picked of peppers picked the the picked the the


*****************************************
File: /group/teaching/asr/labs/recordings/0058.wav 
Speed of Viterbi Decoder: 3.794733145274222 s  Speed of Backtrace: 0.0041648633778095245 s  Forward Count: 77304
(Substitutions, Deletions, Insertions) N: (2, 0, 8) 10
WER: 1.0
Trascription: a peck of peter pickled the peppers peck of pickled
Recognition: picked the of peck of peter of pickled of peppers peck of pickled picked the the the the


***********************************



*****************************************
File: /group/teaching/asr/labs/recordings/0077.wav 
Speed of Viterbi Decoder: 2.382128926925361 s  Speed of Backtrace: 0.003993799909949303 s  Forward Count: 41489
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 6
WER: 1.0
Trascription: the pickled peppers picked peter piper
Recognition: picked the pickled peck where's picked peter of piper pickled peck


*****************************************
File: /group/teaching/asr/labs/recordings/0078.wav 
Speed of Viterbi Decoder: 3.9232603134587407 s  Speed of Backtrace: 0.0049406057223677635 s  Forward Count: 63188
(Substitutions, Deletions, Insertions) N: (1, 0, 8) 9
WER: 1.0
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: picked the where's the peck of pickled the peck where's peter of piper picked picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0079.wav 
Speed of Viterbi Decoder: 6.619112306274474 s  Sp

...



*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 4.028520032763481 s  Speed of Backtrace: 0.004181358963251114 s  Forward Count: 56108
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: picked the picked where's of piper a picked of peck of pickled peck where's picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 8.735237875953317 s  Speed of Backtrace: 0.010338272899389267 s  Forward Count: 113585
(Substitutions, Deletions, Insertions) N: (7, 0, 8) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked where's of piper picked of pickled pickled peppers picked where's of peck of pickled of where's a of piper picked picked the


**********



*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 14.001388152129948 s  Speed of Backtrace: 0.013535291887819767 s  Forward Count: 186409
(Substitutions, Deletions, Insertions) N: (2, 0, 14) 19
WER: 0.8421052631578947
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: picked picked the a the peck picked piper picked a the pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled picked the the the the


*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 6.1236041421070695 s  Speed of Backtrace: 0.006546294316649437 s  Forward Count: 80405
(Substitutions, Deletions, Insertions) N: (1, 0, 11) 6
WER: 2.0
Trascription: peck peck pickled peck of peppers
Recognition: picked picked the picked a peck pick



*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 3.804984957911074 s  Speed of Backtrace: 0.0054190438240766525 s  Forward Count: 54153
(Substitutions, Deletions, Insertions) N: (1, 0, 9) 6
WER: 1.6666666666666667
Trascription: where's the peck peter piper picked
Recognition: picked the where's where's of peck picked a peter of piper of picked picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 3.6116317631676793 s  Speed of Backtrace: 0.0036200527101755142 s  Forward Count: 42227
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 6
WER: 1.0
Trascription: where's a peck of pickled peter
Recognition: picked the where's of peck of pickled peter a picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 12.071967803873122 s  Speed of Backtrace: 0.016606564



*****************************************
File: /group/teaching/asr/labs/recordings/0320.wav 
Speed of Viterbi Decoder: 4.805362976156175 s  Speed of Backtrace: 0.004811895079910755 s  Forward Count: 66011
(Substitutions, Deletions, Insertions) N: (1, 1, 10) 8
WER: 1.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the peter piper the of the pickled picked the pickled picked a picked the of peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 3.307662660256028 s  Speed of Backtrace: 0.003765636123716831 s  Forward Count: 63093
(Substitutions, Deletions, Insertions) N: (3, 0, 7) 6
WER: 1.6666666666666667
Trascription: where's the peck of pickled peppers
Recognition: picked the where's where's picked where's pickled picked where's the of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 5.381807547



*****************************************
File: /group/teaching/asr/labs/recordings/0338.wav 
Speed of Viterbi Decoder: 5.082740576937795 s  Speed of Backtrace: 0.00764638464897871 s  Forward Count: 66712
(Substitutions, Deletions, Insertions) N: (5, 0, 18) 8
WER: 2.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: where's the picked where's where's of where's of of pickled the where's of picked where's where's where's picked picked picked where's the the the the the


*****************************************
File: /group/teaching/asr/labs/recordings/0339.wav 
Speed of Viterbi Decoder: 5.953862546943128 s  Speed of Backtrace: 0.009001567028462887 s  Forward Count: 78093
(Substitutions, Deletions, Insertions) N: (3, 0, 16) 8
WER: 2.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: where's the peter where's the of piper picked where's the of pickled picked the where's the picked of where's picked picked the the the


****************

In [6]:
experiment_set_up('b_p', 0.2, 0.8, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 1.60943794 -log(0.2)
Transist Weight: 0.223143548 -log(0.8)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 6.254638326354325 s  Speed of Backtrace: 0.006072536110877991 s  Forward Count: 79551
(Substitutions, Deletions, Insertions) N: (3, 0, 11) 8
WER: 1.75
Trascription: of of a peter the piper the pickled
Recognition: peck the a of a of the of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 10.944417485035956 s  Speed of Backtrace: 0.006860584020614624 s  Forward Count: 150097
(Substitutions, Deletions, Insertions) N: (2, 0, 9) 10
WER: 1.1
Trascription: piper peck



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.935191249474883 s  Speed of Backtrace: 0.0035672513768076897 s  Forward Count: 24917
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 4.749196362681687 s  Speed of Backtrace: 0.005549105815589428 s  Forward Count: 60593
(Substitutions, Deletions, Insertions) N: (4, 0, 8) 8
WER: 1.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper picked of of of picked of peck of picked peck where's the a


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 7.909918875433505 s  Speed of Backtrace: 0.009932172484695911 s  Forward Count: 106690
(Substi



*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 9.400125439278781 s  Speed of Backtrace: 0.009549416601657867 s  Forward Count: 125178
(Substitutions, Deletions, Insertions) N: (3, 2, 10) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the of peter of the of a of picked the pickled pickled peppers where's peck of pickled peppers the of piper picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 7.073363057337701 s  Speed of Backtrace: 0.007718306966125965 s  Forward Count: 102607
(Substitutions, Deletions, Insertions) N: (4, 1, 9) 17
WER: 0.8235294117647058
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the peppers of piper of picked 



*****************************************
File: /group/teaching/asr/labs/recordings/0059.wav 
Speed of Viterbi Decoder: 6.531699205748737 s  Speed of Backtrace: 0.006482964381575584 s  Forward Count: 85066
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 7
WER: 1.7142857142857142
Trascription: peter pickled a peck of pickled peppers
Recognition: the the picked the the the of pickled of peck of pickled the of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0060.wav 
Speed of Viterbi Decoder: 3.461506293155253 s  Speed of Backtrace: 0.0031212493777275085 s  Forward Count: 52055
(Substitutions, Deletions, Insertions) N: (2, 0, 9) 5
WER: 2.2
Trascription: piper peter picked a peck
Recognition: the the pickled the of of peter of picked the the of peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.8159642945975065 s  Speed of Backtrace: 0.002266650088131427



*****************************************
File: /group/teaching/asr/labs/recordings/0080.wav 
Speed of Viterbi Decoder: 4.932533818297088 s  Speed of Backtrace: 0.004244227893650532 s  Forward Count: 71206
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 8
WER: 0.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked of peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0081.wav 
Speed of Viterbi Decoder: 4.519314178265631 s  Speed of Backtrace: 0.0031418167054653168 s  Forward Count: 64333
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 9
WER: 0.2222222222222222
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 3.330011473968625 s  Speed of Backtrace: 0.0040

...



*****************************************
File: /group/teaching/asr/labs/recordings/0278.wav 
Speed of Viterbi Decoder: 10.20291873253882 s  Speed of Backtrace: 0.01228256430476904 s  Forward Count: 121321
(Substitutions, Deletions, Insertions) N: (4, 0, 11) 13
WER: 1.1538461538461537
Trascription: peter picked a peck of peppers where's the peck of peppers peter picked
Recognition: picked the peter a picked picked piper of peck of the peppers where's picked of picked of the a where's peter picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0279.wav 
Speed of Viterbi Decoder: 14.233989056199789 s  Speed of Backtrace: 0.010648847557604313 s  Forward Count: 151831
(Substitutions, Deletions, Insertions) N: (5, 0, 10) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked piper the peter piper picked the of peck of pickled peck wher



*****************************************
File: /group/teaching/asr/labs/recordings/0296.wav 
Speed of Viterbi Decoder: 3.0276277251541615 s  Speed of Backtrace: 0.003675933927297592 s  Forward Count: 40323
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 6
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers
Recognition: the where's the peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0297.wav 
Speed of Viterbi Decoder: 4.243301222100854 s  Speed of Backtrace: 0.004522442817687988 s  Forward Count: 54702
(Substitutions, Deletions, Insertions) N: (0, 1, 2) 8
WER: 0.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0298.wav 
Speed of Viterbi Decoder: 6.469357002526522 s  Speed of Backtrace: 0.007850012741982937 s  Forward Count: 63801
(S



*****************************************
File: /group/teaching/asr/labs/recordings/0315.wav 
Speed of Viterbi Decoder: 4.997155497781932 s  Speed of Backtrace: 0.0031002601608633995 s  Forward Count: 70575
(Substitutions, Deletions, Insertions) N: (3, 1, 4) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter a piper picked the piper pickled piper where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0316.wav 
Speed of Viterbi Decoder: 3.949140633456409 s  Speed of Backtrace: 0.003691929392516613 s  Forward Count: 54452
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 6
WER: 0.8333333333333334
Trascription: where's the peppers peter piper picked
Recognition: the where's of piper where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0317.wav 
Speed of Viterbi Decoder: 6.136166977696121 s  Speed of Backtrace: 0.007443144917488098 s  Forw



*****************************************
File: /group/teaching/asr/labs/recordings/0334.wav 
Speed of Viterbi Decoder: 5.586129306815565 s  Speed of Backtrace: 0.007963385432958603 s  Forward Count: 76418
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 7
WER: 1.2857142857142858
Trascription: picked peter peck pickled the piper peter
Recognition: picked the picked picked of a picked pickled the piper picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0335.wav 
Speed of Viterbi Decoder: 7.3633692702278495 s  Speed of Backtrace: 0.007138148881494999 s  Forward Count: 98568
(Substitutions, Deletions, Insertions) N: (4, 0, 13) 8
WER: 2.125
Trascription: peter piper picked a peck of pickled peppers
Recognition: a a picked the picked a piper of pickled of pickled picked the pickled of where's picked picked where's picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0336.wav 
Speed of Vi



*****************************************
File: /group/teaching/asr/labs/recordings/0354.wav 
Speed of Viterbi Decoder: 6.213083256036043 s  Speed of Backtrace: 0.005894498899579048 s  Forward Count: 81670
(Substitutions, Deletions, Insertions) N: (2, 0, 9) 8
WER: 1.375
Trascription: peter piper pickled a peck of picked peppers
Recognition: picked the a picked piper peter the pickled of peck of picked a picked peppers picked the
Average
Total Errors: 2926
Total Transcription Words: 2846
Total WER: 1.028109627547435
The number of forward computations per wav:  75615.14366197183
Average decode time: 5.7655221834909955
Average backtrace time: 0.005560145786845348


In [7]:
experiment_set_up('b_p', 0.3, 0.7, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 1.20397282 -log(0.3)
Transist Weight: 0.356674939 -log(0.7)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 5.947340127080679 s  Speed of Backtrace: 0.007037948817014694 s  Forward Count: 79805
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 8
WER: 1.5
Trascription: of of a peter the piper the pickled
Recognition: the a of a of of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 15.812044320628047 s  Speed of Backtrace: 0.008737902157008648 s  Forward Count: 150495
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers pe



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.7943792827427387 s  Speed of Backtrace: 0.002814079634845257 s  Forward Count: 25091
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 4.359623139724135 s  Speed of Backtrace: 0.003944694995880127 s  Forward Count: 60973
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper picked of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 6.074146907776594 s  Speed of Backtrace: 0.008870440535247326 s  Forward Count: 107102
(Substi



*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 9.044711329974234 s  Speed of Backtrace: 0.0075841182842850685 s  Forward Count: 125824
(Substitutions, Deletions, Insertions) N: (6, 1, 6) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the of peter of the of of picked the pickled pickled peppers where's peck of pickled peppers the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 7.5516479490324855 s  Speed of Backtrace: 0.012430100701749325 s  Forward Count: 103088
(Substitutions, Deletions, Insertions) N: (6, 0, 7) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the picked piper of picked peck of the picke



*****************************************
File: /group/teaching/asr/labs/recordings/0059.wav 
Speed of Viterbi Decoder: 6.361658846959472 s  Speed of Backtrace: 0.004624856635928154 s  Forward Count: 85396
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 7
WER: 1.5714285714285714
Trascription: peter pickled a peck of pickled peppers
Recognition: the the the the of picked of peck of pickled the of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0060.wav 
Speed of Viterbi Decoder: 3.8230003882199526 s  Speed of Backtrace: 0.003907156176865101 s  Forward Count: 52369
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 5
WER: 2.2
Trascription: piper peter picked a peck
Recognition: the the pickled the of of peter of of the of peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 2.6001725187525153 s  Speed of Backtrace: 0.0029881317168474197 s  Forward Count: 



*****************************************
File: /group/teaching/asr/labs/recordings/0080.wav 
Speed of Viterbi Decoder: 5.35852381400764 s  Speed of Backtrace: 0.004879599437117577 s  Forward Count: 71451
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 8
WER: 0.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked a peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0081.wav 
Speed of Viterbi Decoder: 4.693809784017503 s  Speed of Backtrace: 0.004370317794382572 s  Forward Count: 64592
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 9
WER: 0.2222222222222222
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 3.4128990452736616 s  Speed of Backtrace: 0.0039435

...



*****************************************
File: /group/teaching/asr/labs/recordings/0259.wav 
Speed of Viterbi Decoder: 3.4667019955813885 s  Speed of Backtrace: 0.0044575827196240425 s  Forward Count: 47978
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 8
WER: 0.875
Trascription: pickled peter piper picked a peck of peppers
Recognition: picked the pickled peter piper of picked of peck of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0260.wav 
Speed of Viterbi Decoder: 5.506291036494076 s  Speed of Backtrace: 0.006611206568777561 s  Forward Count: 77763
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 10
WER: 0.2
Trascription: peppers peppers pickled peppers where's the peck of pickled peppers
Recognition: the peppers peppers pickled peppers where's the peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0261.wav 
Speed of Viterbi Decoder: 3.729727783240378 s  Spee



*****************************************
File: /group/teaching/asr/labs/recordings/0279.wav 
Speed of Viterbi Decoder: 11.146986488252878 s  Speed of Backtrace: 0.01454413216561079 s  Forward Count: 152581
(Substitutions, Deletions, Insertions) N: (5, 0, 7) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: piper the peter piper picked of peck of pickled peck where's where's of peck of pickled the where's peter pickled picked the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0280.wav 
Speed of Viterbi Decoder: 6.384991543367505 s  Speed of Backtrace: 0.005602329038083553 s  Forward Count: 93257
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 10
WER: 0.8
Trascription: peter piper picked peppers where's the peppers peter piper picked
Recognition: picked the of piper picked the where's where's the peppers peter where's pickled pic



*****************************************
File: /group/teaching/asr/labs/recordings/0298.wav 
Speed of Viterbi Decoder: 4.687751209363341 s  Speed of Backtrace: 0.00312787014991045 s  Forward Count: 64081
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0299.wav 
Speed of Viterbi Decoder: 4.631541910581291 s  Speed of Backtrace: 0.004206588491797447 s  Forward Count: 63231
(Substitutions, Deletions, Insertions) N: (1, 0, 6) 6
WER: 1.1666666666666667
Trascription: pickled peppers peck where's peter piper
Recognition: picked the pickled of where's peck the where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0300.wav 
Speed of Viterbi Decoder: 5.8001934150233865 s  S



*****************************************
File: /group/teaching/asr/labs/recordings/0317.wav 
Speed of Viterbi Decoder: 4.256196508184075 s  Speed of Backtrace: 0.004458708688616753 s  Forward Count: 58982
(Substitutions, Deletions, Insertions) N: (3, 1, 4) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter of piper picked the pickled pickled piper where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0318.wav 
Speed of Viterbi Decoder: 4.702126733958721 s  Speed of Backtrace: 0.004428990185260773 s  Forward Count: 66478
(Substitutions, Deletions, Insertions) N: (1, 1, 3) 9
WER: 0.5555555555555556
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's of picked pickled peppers peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0319.wav 
Speed of Viterbi Decoder: 10.547265886329114 s  Speed of Backtrac



*****************************************
File: /group/teaching/asr/labs/recordings/0336.wav 
Speed of Viterbi Decoder: 5.796299670822918 s  Speed of Backtrace: 0.004088221117854118 s  Forward Count: 79868
(Substitutions, Deletions, Insertions) N: (4, 0, 9) 8
WER: 1.625
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the where's the where's of of peter the of peck of the pickled peppers piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0337.wav 
Speed of Viterbi Decoder: 7.084430715069175 s  Speed of Backtrace: 0.004614131525158882 s  Forward Count: 75954
(Substitutions, Deletions, Insertions) N: (6, 0, 6) 8
WER: 1.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the where's of peter where's of the pickled the of picked of the


*****************************************
File: /group/teaching/asr/labs/recordings/0338.wav 
Speed of Viterbi Decoder: 5.199622613377869 s  Speed of Backtr

In [8]:
experiment_set_up('b_p', 0.4, 0.6, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.91629076 -log(0.4)
Transist Weight: 0.510825634 -log(0.6)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 5.694674090482295 s  Speed of Backtrace: 0.004923648200929165 s  Forward Count: 80038
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 8
WER: 1.5
Trascription: of of a peter the piper the pickled
Recognition: the a of a of of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 11.237344096414745 s  Speed of Backtrace: 0.007112222723662853 s  Forward Count: 150761
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers pe



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.9728124924004078 s  Speed of Backtrace: 0.002895837649703026 s  Forward Count: 25205
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 6.403003277257085 s  Speed of Backtrace: 0.008775590918958187 s  Forward Count: 61268
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 8.224081382155418 s  Speed of Backtrace: 0.007124524563550949 s  Forward Count: 107504
(Substitutio



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 6.172382641583681 s  Speed of Backtrace: 0.009076964110136032 s  Forward Count: 103566
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 3.8189368303865194 s  Speed of Backtrace: 0.0035588815808296204 s  Forward Count: 51147
(Substitutions, Deletions, Insertions) N: (1, 0, 4) 5
WER: 1.0
Trascription: pickled piper of the picked
Recognition: picked the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 3.854135314002633 s  Speed of Backtrace: 0.003734324127435684 s  Forward Count: 36573
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 2
WER: 3.0
Trascription: piper picked
Recognition: the peck the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 4.239218263886869 s  Speed of Backtrace: 0.0036075422540307045 s  Forward Count: 51726
(Substitutions, Deletions, Insertions) N: (3, 0, 7) 3
WER: 3.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of of of of picked of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 4.827800600789487 s  Speed of Backtrace: 0.0039248038083314896 s  Forward Count: 63510
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 6
WER: 1.5
Trascription:



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 4.726099893450737 s  Speed of Backtrace: 0.0032167229801416397 s  Forward Count: 46858
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 2.762819819152355 s  Speed of Backtrace: 0.00525528471916914 s  Forward Count: 28593
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper peck


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 4.23546976596117 s  Speed of Backtrace: 0.0046160100027918816 s  Forward Count: 40546
(Substitutions, Deletions, I

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 2.8222048487514257 s  Speed of Backtrace: 0.002647041343152523 s  Forward Count: 60336
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.240403245203197 s  Speed of Backtrace: 0.0030519329011440277 s  Forward Count: 71106
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.5559792816638947 s  Speed of Backtrace: 0.0029025981202721



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 4.914962848648429 s  Speed of Backtrace: 0.0031909625977277756 s  Forward Count: 105455
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.618708483874798 s  Speed of Backtrace: 0.005651442334055901 s  Forward Count: 187895
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 19
WER: 0.3684210526315789
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: peck the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled t



*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.5144808860495687 s  Speed of Backtrace: 0.0024412469938397408 s  Forward Count: 55039
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 1.926733990199864 s  Speed of Backtrace: 0.002369052730500698 s  Forward Count: 42975
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.648749374784529 s  Speed of Backtrace: 0.007518262602388859 s  Forward Count: 144741
(Substitutions, 



*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 2.9306083377450705 s  Speed of Backtrace: 0.0024217963218688965 s  Forward Count: 64321
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.2582583278417587 s  Speed of Backtrace: 0.003300693817436695 s  Forward Count: 71761
(Substitutions, Deletions, Insertions) N: (4, 0, 8) 7
WER: 1.7142857142857142
Trascription: where's the pickled peppers peter piper picked
Recognition: picked the where's where's where's of picked of where's peck of piper a picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 1.985777610912919 s  Speed of Backtr



*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 2.6284204721450806 s  Speed of Backtrace: 0.002406446263194084 s  Forward Count: 57494
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.7778712436556816 s  Speed of Backtrace: 0.002274804748594761 s  Forward Count: 39102
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 4
WER: 2.25
Trascription: peter peter peter peter
Recognition: the a the the the peter the peck picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.2806112244725227 s  Speed of Backtrace: 0.0028360728174448013 s  Forward Count: 70805
(Substitutions, Deletions, Insertions) N: (1, 0, 7)

In [9]:
experiment_set_up('b_p', 0.5, 0.5, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7234231336042285 s  Speed of Backtrace: 0.003208599053323269 s  Forward Count: 80212
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a of a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.048473914153874 s  Speed of Backtrace: 0.004006249830126762 s  Forward Count: 151127
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers pe



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1072205854579806 s  Speed of Backtrace: 0.0019353004172444344 s  Forward Count: 25342
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7684966819360852 s  Speed of Backtrace: 0.003196878358721733 s  Forward Count: 61467
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.789649149402976 s  Speed of Backtrace: 0.004517118446528912 s  Forward Count: 107839
(Substitut



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.672468409873545 s  Speed of Backtrace: 0.004640251398086548 s  Forward Count: 103946
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.360761249437928 s  Speed of Backtrace: 0.0021899063140153885 s  Forward Count: 51282
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.7094866707921028 s  Speed of Backtrace: 0.0017102183774113655 s  Forward Count: 36693
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.405155803076923 s  Speed of Backtrace: 0.002407526597380638 s  Forward Count: 51959
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 3
WER: 2.6666666666666665
Trascription: peck peppers peter
Recognition: the pickled of of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.9501346247270703 s  Speed of Backtrace: 0.002580977976322174 s  Forward Count: 63724
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter piper pick



*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.3014897145330906 s  Speed of Backtrace: 0.0017151180654764175 s  Forward Count: 28689
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.805898018181324 s  Speed of Backtrace: 0.0022369157522916794 s  Forward Count: 40652
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 2.9392738761380315 s  Speed of Backtrace: 0.002567727118730545 s  Forward Count: 63616
(Substitutions, Deletions, Insertion

...



*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.282230759039521 s  Speed of Backtrace: 0.003925505094230175 s  Forward Count: 71296
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.5582598922774196 s  Speed of Backtrace: 0.0029441239312291145 s  Forward Count: 57091
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 8
WER: 1.125
Trascription: peter piper picked a peck of pickled peppers
Recognition: the where's of piper a picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 5.243555646389723 s  Speed of Bac



*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.6196727482602 s  Speed of Backtrace: 0.00554251205176115 s  Forward Count: 188341
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 3.762864815071225 s  Speed of Backtrace: 0.0026365788653492928 s  Forward Count: 81221
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 6
WER: 0.5
Trascription: peck peck pickled peck of peppers
Recognition: the a peck pickled peck of peppers the


*****************************************
File: /group



*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.668805703520775 s  Speed of Backtrace: 0.004852072335779667 s  Forward Count: 145301
(Substitutions, Deletions, Insertions) N: (10, 0, 7) 17
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the of piper of picked the a where's picked picked where's where's the picked of picked where's a a piper a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0305.wav 
Speed of Viterbi Decoder: 5.9115289459005 s  Speed of Backtrace: 0.005062555894255638 s  Forward Count: 131526
(Substitutions, Deletions, Insertions) N: (6, 0, 7) 17
WER: 0.7647058823529411
Trascription: peter piper pickled a peck of picked peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper picked a a peck of the picked where's the where



*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 1.9971699016168714 s  Speed of Backtrace: 0.002156364731490612 s  Forward Count: 44385
(Substitutions, Deletions, Insertions) N: (2, 1, 3) 5
WER: 1.2
Trascription: a peck of pickled peppers
Recognition: the of pickled pickled of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0324.wav 
Speed of Viterbi Decoder: 7.234713300131261 s  Speed of Backtrace: 0.0068537387996912 s  Forward Count: 160071
(Substitutions, Deletions, Insertions) N: (5, 0, 8) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked of piper of picked the the pickled peck where's peck where's where's the peck of pickled peppers peter the piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/



*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.2887407951056957 s  Speed of Backtrace: 0.002547883428633213 s  Forward Count: 70961
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: piper pickled pickled peppers
Recognition: the of piper the where's the peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0344.wav 
Speed of Viterbi Decoder: 5.1983167147263885 s  Speed of Backtrace: 0.004380285739898682 s  Forward Count: 116357
(Substitutions, Deletions, Insertions) N: (6, 0, 8) 14
WER: 1.0
Trascription: peter piper pickled a peck of pickled peppers the peck of pickled peppers picked
Recognition: the a of a of a the picked of peck of pickled peppers of picked of pickled the where's picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0345.wav 
Speed of Viterbi Decoder: 2.4849875820

In [10]:
experiment_set_up('b_p', 0.6, 0.4, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.510825634 -log(0.6)
Transist Weight: 0.91629076 -log(0.4)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7163672456517816 s  Speed of Backtrace: 0.0030372636392712593 s  Forward Count: 80395
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.032117087393999 s  Speed of Backtrace: 0.005871669389307499 s  Forward Count: 151418
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1237587947398424 s  Speed of Backtrace: 0.0020735133439302444 s  Forward Count: 25505
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.6912544583901763 s  Speed of Backtrace: 0.003884078934788704 s  Forward Count: 61633
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.848603175953031 s  Speed of Backtrace: 0.004672613926231861 s  Forward Count: 108218
(Substitutions, 



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.686782744713128 s  Speed of Backtrace: 0.004475755617022514 s  Forward Count: 104315
(Substitutions, Deletions, Insertions) N: (3, 1, 5) 17
WER: 0.5294117647058824
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.3637215569615364 s  Speed of Backtrace: 0.0023700250312685966 s  Forward Count: 51390
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of 



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.690586376003921 s  Speed of Backtrace: 0.0016904519870877266 s  Forward Count: 36818
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.399794541299343 s  Speed of Backtrace: 0.001970146782696247 s  Forward Count: 52160
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.9171005403622985 s  Speed of Backtrace: 0.002189389429986477 s  Forward Count: 63963
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: peter



*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.2870149109512568 s  Speed of Backtrace: 0.0017466610297560692 s  Forward Count: 28801
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.8148981966078281 s  Speed of Backtrace: 0.0022273706272244453 s  Forward Count: 40791
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 2.9317272258922458 s  Speed of Backtrace: 0.002622258849442005 s  Forward Count: 63943
(Substitutions, Deletions, Insertio

...



*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.287419868633151 s  Speed of Backtrace: 0.003023063763976097 s  Forward Count: 71475
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.583344304934144 s  Speed of Backtrace: 0.002917896956205368 s  Forward Count: 57233
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: the where's of piper a picked of peck of picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 5.257823245599866 s  Speed of Backtrace:



*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.673221874050796 s  Speed of Backtrace: 0.005670866928994656 s  Forward Count: 188720
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 3.8019331749528646 s  Speed of Backtrace: 0.0025312062352895737 s  Forward Count: 81331
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 6
WER: 0.5
Trascription: peck peck pickled peck of peppers
Recognition: the a peck pickled peck of peppers the


*****************************************
File: /g



*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.659357494674623 s  Speed of Backtrace: 0.004620363004505634 s  Forward Count: 145816
(Substitutions, Deletions, Insertions) N: (9, 1, 7) 17
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the of piper of picked the a where's picked where's where's the picked of picked where's a a piper a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0305.wav 
Speed of Viterbi Decoder: 5.954930583015084 s  Speed of Backtrace: 0.004810386337339878 s  Forward Count: 132065
(Substitutions, Deletions, Insertions) N: (5, 1, 8) 17
WER: 0.8235294117647058
Trascription: peter piper pickled a peck of picked peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper picked a a peck of the picked where's the a the peck 



*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 2.042591425590217 s  Speed of Backtrace: 0.002186995930969715 s  Forward Count: 44565
(Substitutions, Deletions, Insertions) N: (2, 1, 3) 5
WER: 1.2
Trascription: a peck of pickled peppers
Recognition: the of pickled pickled of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0324.wav 
Speed of Viterbi Decoder: 7.424202820286155 s  Speed of Backtrace: 0.005448183976113796 s  Forward Count: 160586
(Substitutions, Deletions, Insertions) N: (5, 0, 7) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the piper of picked the the pickled peck where's peck where's where's the peck of pickled peppers peter the piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0325.



*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.265624564141035 s  Speed of Backtrace: 0.002492331899702549 s  Forward Count: 71160
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: piper pickled pickled peppers
Recognition: the of piper the where's the peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0344.wav 
Speed of Viterbi Decoder: 5.218392903916538 s  Speed of Backtrace: 0.0042571816593408585 s  Forward Count: 116739
(Substitutions, Deletions, Insertions) N: (6, 0, 7) 14
WER: 0.9285714285714286
Trascription: peter piper pickled a peck of pickled peppers the peck of pickled peppers picked
Recognition: the a of a of a the the peck of pickled peppers of picked of pickled the where's picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0345.wav 
Speed of Viterbi Decoder: 2.47

In [11]:
experiment_set_up('b_p', 0.7, 0.3, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.356674939 -log(0.7)
Transist Weight: 1.20397282 -log(0.3)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.6916574789211154 s  Speed of Backtrace: 0.003072427585721016 s  Forward Count: 80570
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.037519549950957 s  Speed of Backtrace: 0.0038437452167272568 s  Forward Count: 151682
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 10
WER: 0.7
Trascription: piper peck peppers peter



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1419261861592531 s  Speed of Backtrace: 0.0017564482986927032 s  Forward Count: 25698
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.763091418892145 s  Speed of Backtrace: 0.002954302355647087 s  Forward Count: 61835
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.8073780834674835 s  Speed of Backtrace: 0.0057217394933104515 s  Forward Count: 108601
(Substitutions, Delet



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.636215810663998 s  Speed of Backtrace: 0.004484248347580433 s  Forward Count: 104789
(Substitutions, Deletions, Insertions) N: (5, 1, 5) 17
WER: 0.6470588235294118
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked peck of pickled peppers where's the a of pickled the where's the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.3541202135384083 s  Speed of Backtrace: 0.002259824424982071 s  Forward Count: 51517
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterb



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 2.2537120869383216 s  Speed of Backtrace: 0.0020648548379540443 s  Forward Count: 36962
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 3.169132291339338 s  Speed of Backtrace: 0.002502119168639183 s  Forward Count: 52444
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 3.8604993084445596 s  Speed of Backtrace: 0.0027363765984773636 s  Forward Count: 64266
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: pet



*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.28096086345613 s  Speed of Backtrace: 0.0017173076048493385 s  Forward Count: 28939
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.8355820076540112 s  Speed of Backtrace: 0.0022264663130044937 s  Forward Count: 40946
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 2.9395940834656358 s  Speed of Backtrace: 0.002589370124042034 s  Forward Count: 64255
(Substitutions, Deletions, Insertions

...



*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.287058774381876 s  Speed of Backtrace: 0.0036936402320861816 s  Forward Count: 71661
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.542075860314071 s  Speed of Backtrace: 0.002837231382727623 s  Forward Count: 57427
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: the where's of piper a picked of peck of picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 5.266358007676899 s  Speed of Backtrace



*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.687761322595179 s  Speed of Backtrace: 0.0055670365691185 s  Forward Count: 189184
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 3.778837607242167 s  Speed of Backtrace: 0.0025191204622387886 s  Forward Count: 81461
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 6
WER: 0.5
Trascription: peck peck pickled peck of peppers
Recognition: the a peck pickled peck of peppers the


*****************************************
File: /grou



*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.676902264356613 s  Speed of Backtrace: 0.004616637714207172 s  Forward Count: 146347
(Substitutions, Deletions, Insertions) N: (9, 1, 6) 17
WER: 0.9411764705882353
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the piper of picked the a where's picked where's where's the picked of picked where's a a piper a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0305.wav 
Speed of Viterbi Decoder: 5.933557904325426 s  Speed of Backtrace: 0.006708935834467411 s  Forward Count: 132665
(Substitutions, Deletions, Insertions) N: (6, 1, 8) 17
WER: 0.8823529411764706
Trascription: peter piper pickled a peck of picked peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper picked a a peck of the picked where's the



*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 1.9882269520312548 s  Speed of Backtrace: 0.002179664559662342 s  Forward Count: 44821
(Substitutions, Deletions, Insertions) N: (2, 1, 3) 5
WER: 1.2
Trascription: a peck of pickled peppers
Recognition: the of pickled pickled of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0324.wav 
Speed of Viterbi Decoder: 7.305223983712494 s  Speed of Backtrace: 0.005161935463547707 s  Forward Count: 161092
(Substitutions, Deletions, Insertions) N: (3, 1, 7) 17
WER: 0.6470588235294118
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the piper of picked the the pickled peck where's peppers where's the peck of pickled peppers peter the piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0325.wav 



*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.3047611117362976 s  Speed of Backtrace: 0.002533070743083954 s  Forward Count: 71356
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: piper pickled pickled peppers
Recognition: the of piper the where's the peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0344.wav 
Speed of Viterbi Decoder: 5.251542798243463 s  Speed of Backtrace: 0.004302334040403366 s  Forward Count: 117128
(Substitutions, Deletions, Insertions) N: (6, 0, 7) 14
WER: 0.9285714285714286
Trascription: peter piper pickled a peck of pickled peppers the peck of pickled peppers picked
Recognition: the a of a of a the the peck of pickled peppers of picked of pickled the where's picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0345.wav 
Speed of Viterbi Decoder: 2.47

In [12]:
experiment_set_up('b_p', 0.8, 0.2, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.223143548 -log(0.8)
Transist Weight: 1.60943794 -log(0.2)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7055394323542714 s  Speed of Backtrace: 0.002985764294862747 s  Forward Count: 80795
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.050577267073095 s  Speed of Backtrace: 0.003704136237502098 s  Forward Count: 151995
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 10
WER: 0.6
Trascription: piper peck peppers peter 



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1120347706601024 s  Speed of Backtrace: 0.0017102733254432678 s  Forward Count: 25852
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7524047205224633 s  Speed of Backtrace: 0.003012813627719879 s  Forward Count: 62189
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.822685607708991 s  Speed of Backtrace: 0.004407549276947975 s  Forward Count: 109121
(Substitutions, Deleti



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.660423688590527 s  Speed of Backtrace: 0.004119417630136013 s  Forward Count: 105296
(Substitutions, Deletions, Insertions) N: (7, 2, 5) 17
WER: 0.8235294117647058
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked of of peppers where's the a of picked the where's the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.332691195420921 s  Speed of Backtrace: 0.0022826986387372017 s  Forward Count: 51681
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterbi Decoder: 



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.703153982758522 s  Speed of Backtrace: 0.0016907863318920135 s  Forward Count: 37101
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.396993008442223 s  Speed of Backtrace: 0.0020118504762649536 s  Forward Count: 52767
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.9680666802451015 s  Speed of Backtrace: 0.002248300239443779 s  Forward Count: 64483
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: pete



*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.306086434982717 s  Speed of Backtrace: 0.0016994206234812737 s  Forward Count: 29130
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.7978794425725937 s  Speed of Backtrace: 0.002171098254621029 s  Forward Count: 41075
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 2.947360803373158 s  Speed of Backtrace: 0.00243487861007452 s  Forward Count: 64593
(Substitutions, Deletions, Insertions) 

...



*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.561419937759638 s  Speed of Backtrace: 0.0027752965688705444 s  Forward Count: 57676
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: the where's of piper a picked of peck of picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 5.291463385336101 s  Speed of Backtrace: 0.004457525908946991 s  Forward Count: 116885
(Substitutions, Deletions, Insertions) N: (4, 2, 6) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the a of piper picked of pickled the of peppers where's of peck of pickled where's a of piper picked the


*****************************************
File: /group/teaching/asr/labs



*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 3.7438241308555007 s  Speed of Backtrace: 0.0024575404822826385 s  Forward Count: 81632
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 6
WER: 0.5
Trascription: peck peck pickled peck of peppers
Recognition: the a peck pickled peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0286.wav 
Speed of Viterbi Decoder: 5.784633551724255 s  Speed of Backtrace: 0.003916943445801735 s  Forward Count: 126730
(Substitutions, Deletions, Insertions) N: (3, 0, 3) 13
WER: 0.46153846153846156
Trascription: piper picked piper picked piper peck where's of piper picked peck picked the
Recognition: the piper peck piper peck piper peck where's of piper picked picked picked a the the


*****************************************
File: /group/teaching/asr/labs/recordings/0287.wav 
Speed of Viterbi Decoder: 9.169162598438561 s  Speed 



*****************************************
File: /group/teaching/asr/labs/recordings/0305.wav 
Speed of Viterbi Decoder: 5.96878610830754 s  Speed of Backtrace: 0.004709193482995033 s  Forward Count: 133430
(Substitutions, Deletions, Insertions) N: (8, 0, 6) 17
WER: 0.8235294117647058
Trascription: peter piper pickled a peck of picked peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper picked a a peck of the peck where's the a the peck of picked where's the a pickled picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0306.wav 
Speed of Viterbi Decoder: 6.491704613901675 s  Speed of Backtrace: 0.005034619942307472 s  Forward Count: 146831
(Substitutions, Deletions, Insertions) N: (10, 1, 6) 17
WER: 1.0
Trascription: where's the peck of pickled peppers peter piper picked peter piper pickled a peck of picked peppers
Recognition: the pickled a the where's pickled where's of picked of of picked the pickl



*****************************************
File: /group/teaching/asr/labs/recordings/0325.wav 
Speed of Viterbi Decoder: 3.012882336974144 s  Speed of Backtrace: 0.0027401018887758255 s  Forward Count: 67238
(Substitutions, Deletions, Insertions) N: (5, 0, 3) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the of of picked of peck of picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0326.wav 
Speed of Viterbi Decoder: 4.071491592563689 s  Speed of Backtrace: 0.0029264185577630997 s  Forward Count: 89385
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers the piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0327.wav 
Speed of Viterbi Decoder: 2.7912645367905498 s  Speed of Backtrace: 0.002462822



*****************************************
File: /group/teaching/asr/labs/recordings/0345.wav 
Speed of Viterbi Decoder: 2.455877219326794 s  Speed of Backtrace: 0.002510877326130867 s  Forward Count: 56392
(Substitutions, Deletions, Insertions) N: (2, 2, 4) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the piper a of peck pickled where's a the


*****************************************
File: /group/teaching/asr/labs/recordings/0346.wav 
Speed of Viterbi Decoder: 2.1092194952070713 s  Speed of Backtrace: 0.0024916380643844604 s  Forward Count: 48849
(Substitutions, Deletions, Insertions) N: (4, 0, 2) 8
WER: 0.75
Trascription: a peck of pickled peppers peter piper picked
Recognition: the a picked of piper picked of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0347.wav 
Speed of Viterbi Decoder: 1.7800996787846088 s  Speed of Backtrace: 0.0025423532351851463 s  Forward Count: 41380
(Subst

In [13]:
experiment_set_up('b_p', 0.9, 0.1, 0.0)

Mode: Baseline Recognition, Use Compose To Transfer Recognized Phone Sequecen Into Word Sequence
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.105360515 -log(0.9)
Transist Weight: 2.30258512 -log(0.1)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.756315021775663 s  Speed of Backtrace: 0.00280161015689373 s  Forward Count: 81197
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 8
WER: 1.125
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.025251662358642 s  Speed of Backtrace: 0.0036821048706769943 s  Forward Count: 152644
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 10
WER: 0.5
Trascription: piper peck peppers peter peter pick



*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.76476255338639 s  Speed of Backtrace: 0.0030871955677866936 s  Forward Count: 62726
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.807115291245282 s  Speed of Backtrace: 0.004093733616173267 s  Forward Count: 109859
(Substitutions, Deletions, Insertions) N: (6, 3, 3) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the of of picked of peck picked where's peck the peck picked where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/



*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.3646374829113483 s  Speed of Backtrace: 0.0020624399185180664 s  Forward Count: 51920
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 5
WER: 0.6
Trascription: pickled piper of the picked
Recognition: the of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterbi Decoder: 4.12698689289391 s  Speed of Backtrace: 0.0039283717051148415 s  Forward Count: 94801
(Substitutions, Deletions, Insertions) N: (6, 2, 2) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked of picked peck of picked peppers where's peck of picked where's the piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0043.wav 
Speed of Viterbi Decoder: 2.9997334



*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.96525118406862 s  Speed of Backtrace: 0.0022876951843500137 s  Forward Count: 64907
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: peter piper picked a pickled peter
Recognition: the of of of picked the of a the the


*****************************************
File: /group/teaching/asr/labs/recordings/0064.wav 
Speed of Viterbi Decoder: 3.812456391751766 s  Speed of Backtrace: 0.002508651465177536 s  Forward Count: 83510
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 5
WER: 1.2
Trascription: piper peter picked pickled peppers
Recognition: the piper of a of a pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0065.wav 
Speed of Viterbi Decoder: 2.9103811364620924 s  Speed of Backtrace: 0.002120720222592354 s  Forward Count: 64906
(Substitutions, Deletions, Insert



*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.81147641222924 s  Speed of Backtrace: 0.0021887952461838722 s  Forward Count: 41336
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 2.9417421761900187 s  Speed of Backtrace: 0.0024333838373422623 s  Forward Count: 65189
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 4
WER: 1.75
Trascription: peck pickled peck piper
Recognition: peter the peck the a peck a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0086.wav 
Speed of Viterbi Decoder: 2.6039386400952935 s  Speed of Backtrace: 0.002395475283265114 s  Forward Count: 58265
(Substitutions, Deletions, Insertions

...



*****************************************
File: /group/teaching/asr/labs/recordings/0268.wav 
Speed of Viterbi Decoder: 3.137522370554507 s  Speed of Backtrace: 0.0029859859496355057 s  Forward Count: 69897
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 7
WER: 1.1428571428571428
Trascription: peter picked a peck of pickled peppers
Recognition: the peter of picked of piper pickled pickled picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0269.wav 
Speed of Viterbi Decoder: 1.7935349568724632 s  Speed of Backtrace: 0.0017398344352841377 s  Forward Count: 39606
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 2
WER: 1.0
Trascription: pickled peppers
Recognition: the pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0270.wav 
Speed of Viterbi Decoder: 2.019510163925588 s  Speed of Backtrace: 0.0022122636437416077 s  Forward Count: 45223
(Substitutions, Deletions, Inserti



*****************************************
File: /group/teaching/asr/labs/recordings/0288.wav 
Speed of Viterbi Decoder: 5.1250226981937885 s  Speed of Backtrace: 0.0029048658907413483 s  Forward Count: 111671
(Substitutions, Deletions, Insertions) N: (1, 2, 3) 8
WER: 0.75
Trascription: peter piper picked a peck of pickled peppers
Recognition: the of piper peck of pickled pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0289.wav 
Speed of Viterbi Decoder: 3.992378493770957 s  Speed of Backtrace: 0.003088166005909443 s  Forward Count: 87682
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's of peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0290.wav 
Speed of Viterbi Decoder: 2.7022567791864276 s  Speed of Backtrace: 0.00214315



*****************************************
File: /group/teaching/asr/labs/recordings/0308.wav 
Speed of Viterbi Decoder: 6.312557418830693 s  Speed of Backtrace: 0.004665604792535305 s  Forward Count: 142623
(Substitutions, Deletions, Insertions) N: (5, 1, 8) 17
WER: 0.8235294117647058
Trascription: peter piper pickled a picked peck of peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper the of a of picked peck of where's of the a the peck of picked where's the a piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0309.wav 
Speed of Viterbi Decoder: 1.8019280545413494 s  Speed of Backtrace: 0.0016863113269209862 s  Forward Count: 39493
(Substitutions, Deletions, Insertions) N: (0, 0, 1) 3
WER: 0.3333333333333333
Trascription: where's peter piper
Recognition: where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0310.wav 
Speed of Viterbi De



*****************************************
File: /group/teaching/asr/labs/recordings/0329.wav 
Speed of Viterbi Decoder: 7.805930472910404 s  Speed of Backtrace: 0.005001782439649105 s  Forward Count: 173780
(Substitutions, Deletions, Insertions) N: (3, 1, 5) 17
WER: 0.5294117647058824
Trascription: peppers peck picked the piper where's piper peppers picked peter a peck pickled of peter of pickled
Recognition: the peppers peck peck picked the piper where's the piper peter picked picked a picked the pickled of of pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0330.wav 
Speed of Viterbi Decoder: 3.3626619102433324 s  Speed of Backtrace: 0.0026350654661655426 s  Forward Count: 74021
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 7
WER: 0.42857142857142855
Trascription: where's the peppers peter piper peck picked
Recognition: the where's the where's peter piper peck picked the


*****************************************
File: /group/



*****************************************
File: /group/teaching/asr/labs/recordings/0350.wav 
Speed of Viterbi Decoder: 3.817960516549647 s  Speed of Backtrace: 0.003045464865863323 s  Forward Count: 85838
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: the a peter piper picked picked of peck a pickled where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0351.wav 
Speed of Viterbi Decoder: 4.036280079744756 s  Speed of Backtrace: 0.003310464322566986 s  Forward Count: 89429
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 9
WER: 0.8888888888888888
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the a where's of peck of the picked of where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0352.wav 
Speed of Viterbi Decoder: 2.371325584128499 s  Speed of Bac

# 2 Baseline selfloop weight & transist weight 0.1 -> 0.9

In [15]:
experiment_set_up('b_w', 0.1, 0.9, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 2.30258512 -log(0.1)
Transist Weight: 0.105360515 -log(0.9)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7186971651390195 s  Speed of Backtrace: 0.000498439185321331 s  Forward Count: 79131
(Substitutions, Deletions, Insertions) N: (1, 0, 15) 8
WER: 2.0
Trascription: of of a peter the piper the pickled
Recognition: peck the a of a of the of peter the peck a of picked a piper pickled the the pickled picked the a


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.042723276652396 s  Speed of Backtrace: 0.0008596666157245636 s  Forward Count: 149566
(Substitutions, Deletions, Insertions) N: (0, 1, 13) 10
WER: 1.4
Trascription: piper pec



*****************************************
File: /group/teaching/asr/labs/recordings/0019.wav 
Speed of Viterbi Decoder: 5.455040234141052 s  Speed of Backtrace: 0.0006659319624304771 s  Forward Count: 116404
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 8
WER: 1.5
Trascription: the peck of pickled peppers peter piper picked
Recognition: pickled the picked picked of pickled peppers the of peck picked picked the the picked the the


*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1015400476753712 s  Speed of Backtrace: 0.00018828082829713821 s  Forward Count: 24646
(Substitutions, Deletions, Insertions) N: (1, 0, 7) 3
WER: 2.6666666666666665
Trascription: peter piper picked
Recognition: peck the peter of of of a peppers picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7417550487443805 s  Speed of Backtrace: 0.0003933515399



*****************************************
File: /group/teaching/asr/labs/recordings/0038.wav 
Speed of Viterbi Decoder: 5.035531917586923 s  Speed of Backtrace: 0.000660378485918045 s  Forward Count: 111758
(Substitutions, Deletions, Insertions) N: (7, 0, 11) 17
WER: 1.0588235294117647
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the pickled piper of a picked peck of the peck of where's where's picked of picked the peck of where's the pickled piper peck picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 5.691830838099122 s  Speed of Backtrace: 0.0007510734722018242 s  Forward Count: 124304
(Substitutions, Deletions, Insertions) N: (4, 0, 14) 17
WER: 1.0588235294117647
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the of pe



*****************************************
File: /group/teaching/asr/labs/recordings/0057.wav 
Speed of Viterbi Decoder: 4.371194534003735 s  Speed of Backtrace: 0.0005758563056588173 s  Forward Count: 96781
(Substitutions, Deletions, Insertions) N: (2, 0, 10) 13
WER: 0.9230769230769231
Trascription: where's peter pickled peck of pickled peppers the peck piper picked a peppers
Recognition: the the where's peter of pickled peck of pickled peppers the peck picked picked picked of peppers picked the the picked the the


*****************************************
File: /group/teaching/asr/labs/recordings/0058.wav 
Speed of Viterbi Decoder: 3.527489966712892 s  Speed of Backtrace: 0.00047738291323184967 s  Forward Count: 77304
(Substitutions, Deletions, Insertions) N: (2, 0, 8) 10
WER: 1.0
Trascription: a peck of peter pickled the peppers peck of pickled
Recognition: picked the of peck of peter of pickled of peppers peck of pickled picked the the the the


**********************************



*****************************************
File: /group/teaching/asr/labs/recordings/0077.wav 
Speed of Viterbi Decoder: 1.8976005921140313 s  Speed of Backtrace: 0.00025943573564291 s  Forward Count: 41489
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 6
WER: 1.0
Trascription: the pickled peppers picked peter piper
Recognition: picked the pickled peck where's picked peter of piper pickled peck


*****************************************
File: /group/teaching/asr/labs/recordings/0078.wav 
Speed of Viterbi Decoder: 2.856858109124005 s  Speed of Backtrace: 0.00038859806954860687 s  Forward Count: 63188
(Substitutions, Deletions, Insertions) N: (1, 0, 8) 9
WER: 1.0
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: picked the where's the peck of pickled the peck where's peter of piper picked picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0079.wav 
Speed of Viterbi Decoder: 5.66344534419477 s  Spe

...



*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.593412089161575 s  Speed of Backtrace: 0.00035538431257009506 s  Forward Count: 56108
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: picked the picked where's of piper a picked of peck of pickled peck where's picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 5.264894190244377 s  Speed of Backtrace: 0.0006818240508437157 s  Forward Count: 113585
(Substitutions, Deletions, Insertions) N: (7, 0, 8) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked where's of piper picked of pickled pickled peppers picked where's of peck of pickled of where's a of piper picked picked the


*******



*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.640973346307874 s  Speed of Backtrace: 0.0010971985757350922 s  Forward Count: 186409
(Substitutions, Deletions, Insertions) N: (2, 0, 14) 19
WER: 0.8421052631578947
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: picked picked the a the peck picked piper picked a the pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled picked the the the the


*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 3.7625406654551625 s  Speed of Backtrace: 0.0004964526742696762 s  Forward Count: 80405
(Substitutions, Deletions, Insertions) N: (1, 0, 11) 6
WER: 2.0
Trascription: peck peck pickled peck of peppers
Recognition: picked picked the picked a peck pic



*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.5527624785900116 s  Speed of Backtrace: 0.00034161563962697983 s  Forward Count: 54153
(Substitutions, Deletions, Insertions) N: (1, 0, 9) 6
WER: 1.6666666666666667
Trascription: where's the peck peter piper picked
Recognition: picked the where's where's of peck picked a peter of piper of picked picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 1.9354466293007135 s  Speed of Backtrace: 0.0002782512456178665 s  Forward Count: 42227
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 6
WER: 1.0
Trascription: where's a peck of pickled peter
Recognition: picked the where's of peck of pickled peter a picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.666366928257048 s  Speed of Backtrace: 0.00129433



*****************************************
File: /group/teaching/asr/labs/recordings/0320.wav 
Speed of Viterbi Decoder: 3.041851901449263 s  Speed of Backtrace: 0.00038358476012945175 s  Forward Count: 66011
(Substitutions, Deletions, Insertions) N: (1, 1, 10) 8
WER: 1.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the peter piper the of the pickled picked the pickled picked a picked the of peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 2.91616577655077 s  Speed of Backtrace: 0.0003703581169247627 s  Forward Count: 63093
(Substitutions, Deletions, Insertions) N: (3, 0, 7) 6
WER: 1.6666666666666667
Trascription: where's the peck of pickled peppers
Recognition: picked the where's where's picked where's pickled picked where's the of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.2858829



*****************************************
File: /group/teaching/asr/labs/recordings/0338.wav 
Speed of Viterbi Decoder: 3.1008434602990746 s  Speed of Backtrace: 0.0004577590152621269 s  Forward Count: 66712
(Substitutions, Deletions, Insertions) N: (5, 0, 18) 8
WER: 2.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: where's the picked where's where's of where's of of pickled the where's of picked where's where's where's picked picked picked where's the the the the the


*****************************************
File: /group/teaching/asr/labs/recordings/0339.wav 
Speed of Viterbi Decoder: 3.6540633467957377 s  Speed of Backtrace: 0.000494023784995079 s  Forward Count: 78093
(Substitutions, Deletions, Insertions) N: (3, 0, 16) 8
WER: 2.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: where's the peter where's the of piper picked where's the of pickled picked the where's the picked of where's picked picked the the the


************

In [16]:
experiment_set_up('b_w', 0.2, 0.8, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 1.60943794 -log(0.2)
Transist Weight: 0.223143548 -log(0.8)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7125737676396966 s  Speed of Backtrace: 0.00048618484288454056 s  Forward Count: 79551
(Substitutions, Deletions, Insertions) N: (3, 0, 11) 8
WER: 1.75
Trascription: of of a peter the piper the pickled
Recognition: peck the a of a of the of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.03025898616761 s  Speed of Backtrace: 0.0008615599945187569 s  Forward Count: 150097
(Substitutions, Deletions, Insertions) N: (2, 0, 9) 10
WER: 1.1
Trascription: piper peck peppers peter pete



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1381515078246593 s  Speed of Backtrace: 0.00016678310930728912 s  Forward Count: 24917
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7677727304399014 s  Speed of Backtrace: 0.00037342309951782227 s  Forward Count: 60593
(Substitutions, Deletions, Insertions) N: (4, 0, 8) 8
WER: 1.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper picked of of of picked of peck of picked peck where's the a


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.802108873613179 s  Speed of Backtrace: 0.0005935709923505783 s  Forward Count: 106690
(



*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 5.74507571849972 s  Speed of Backtrace: 0.0007556872442364693 s  Forward Count: 125178
(Substitutions, Deletions, Insertions) N: (3, 2, 10) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the of peter of the of a of picked the pickled pickled peppers where's peck of pickled peppers the of piper picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.656061393208802 s  Speed of Backtrace: 0.0005981279537081718 s  Forward Count: 102607
(Substitutions, Deletions, Insertions) N: (4, 1, 9) 17
WER: 0.8235294117647058
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the peppers of piper of picked



*****************************************
File: /group/teaching/asr/labs/recordings/0059.wav 
Speed of Viterbi Decoder: 4.037820560857654 s  Speed of Backtrace: 0.0005034748464822769 s  Forward Count: 85066
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 7
WER: 1.7142857142857142
Trascription: peter pickled a peck of pickled peppers
Recognition: the the picked the the the of pickled of peck of pickled the of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0060.wav 
Speed of Viterbi Decoder: 2.403123751282692 s  Speed of Backtrace: 0.00033735670149326324 s  Forward Count: 52055
(Substitutions, Deletions, Insertions) N: (2, 0, 9) 5
WER: 2.2
Trascription: piper peter picked a peck
Recognition: the the pickled the of of peter of picked the the of peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.724893412552774 s  Speed of Backtrace: 0.00025430507957935



*****************************************
File: /group/teaching/asr/labs/recordings/0080.wav 
Speed of Viterbi Decoder: 3.2820800291374326 s  Speed of Backtrace: 0.0004227636381983757 s  Forward Count: 71206
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 8
WER: 0.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked of peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0081.wav 
Speed of Viterbi Decoder: 2.932781646028161 s  Speed of Backtrace: 0.0003965646028518677 s  Forward Count: 64333
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 9
WER: 0.2222222222222222
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.1246679620817304 s  Speed of Backtrace: 0.0

...



*****************************************
File: /group/teaching/asr/labs/recordings/0278.wav 
Speed of Viterbi Decoder: 5.633312203921378 s  Speed of Backtrace: 0.0007154801860451698 s  Forward Count: 121321
(Substitutions, Deletions, Insertions) N: (4, 0, 11) 13
WER: 1.1538461538461537
Trascription: peter picked a peck of peppers where's the peck of peppers peter picked
Recognition: picked the peter a picked picked piper of peck of the peppers where's picked of picked of the a where's peter picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0279.wav 
Speed of Viterbi Decoder: 6.984884278848767 s  Speed of Backtrace: 0.0008715298026800156 s  Forward Count: 151831
(Substitutions, Deletions, Insertions) N: (5, 0, 10) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked piper the peter piper picked the of peck of pickled peck wh



*****************************************
File: /group/teaching/asr/labs/recordings/0296.wav 
Speed of Viterbi Decoder: 1.8202973790466785 s  Speed of Backtrace: 0.0002429615706205368 s  Forward Count: 40323
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 6
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers
Recognition: the where's the peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0297.wav 
Speed of Viterbi Decoder: 2.4668308487161994 s  Speed of Backtrace: 0.0003181183710694313 s  Forward Count: 54702
(Substitutions, Deletions, Insertions) N: (0, 1, 2) 8
WER: 0.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0298.wav 
Speed of Viterbi Decoder: 2.8701017079874873 s  Speed of Backtrace: 0.000371759757399559 s  Forward Count: 6380



*****************************************
File: /group/teaching/asr/labs/recordings/0315.wav 
Speed of Viterbi Decoder: 3.238551734946668 s  Speed of Backtrace: 0.0003949776291847229 s  Forward Count: 70575
(Substitutions, Deletions, Insertions) N: (3, 1, 4) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter a piper picked the piper pickled piper where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0316.wav 
Speed of Viterbi Decoder: 2.545406180433929 s  Speed of Backtrace: 0.0003322698175907135 s  Forward Count: 54452
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 6
WER: 0.8333333333333334
Trascription: where's the peppers peter piper picked
Recognition: the where's of piper where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0317.wav 
Speed of Viterbi Decoder: 2.691808342002332 s  Speed of Backtrace: 0.00034570973366498947 s  F



*****************************************
File: /group/teaching/asr/labs/recordings/0334.wav 
Speed of Viterbi Decoder: 3.5599414790049195 s  Speed of Backtrace: 0.00045163650065660477 s  Forward Count: 76418
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 7
WER: 1.2857142857142858
Trascription: picked peter peck pickled the piper peter
Recognition: picked the picked picked of a picked pickled the piper picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0335.wav 
Speed of Viterbi Decoder: 4.515949887223542 s  Speed of Backtrace: 0.0005679959431290627 s  Forward Count: 98568
(Substitutions, Deletions, Insertions) N: (4, 0, 13) 8
WER: 2.125
Trascription: peter piper picked a peck of pickled peppers
Recognition: a a picked the picked a piper of pickled of pickled picked the pickled of where's picked picked where's picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0336.wav 
Speed of



*****************************************
File: /group/teaching/asr/labs/recordings/0354.wav 
Speed of Viterbi Decoder: 3.7503908034414053 s  Speed of Backtrace: 0.0004927925765514374 s  Forward Count: 81670
(Substitutions, Deletions, Insertions) N: (2, 0, 9) 8
WER: 1.375
Trascription: peter piper pickled a peck of picked peppers
Recognition: picked the a picked piper peter the pickled of peck of picked a picked peppers picked the
Average
Total Errors: 2926
Total Transcription Words: 2846
Total WER: 1.028109627547435
The number of forward computations per wav:  75615.14366197183
Average decode time: 3.5881621049690833
Average backtrace time: 0.0004864513900288394


In [17]:
experiment_set_up('b_w', 0.3, 0.7, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 1.20397282 -log(0.3)
Transist Weight: 0.356674939 -log(0.7)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7227382361888885 s  Speed of Backtrace: 0.00046341121196746826 s  Forward Count: 79805
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 8
WER: 1.5
Trascription: of of a peter the piper the pickled
Recognition: the a of a of of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.0495046600699425 s  Speed of Backtrace: 0.0008503412827849388 s  Forward Count: 150495
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked 



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1079889591783285 s  Speed of Backtrace: 0.0001787794753909111 s  Forward Count: 25091
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.749205640517175 s  Speed of Backtrace: 0.0004096934571862221 s  Forward Count: 60973
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper picked of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.792613399215043 s  Speed of Backtrace: 0.0006409455090761185 s  Forward Count: 107102
(Sub



*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 5.7299487283453345 s  Speed of Backtrace: 0.0007097898051142693 s  Forward Count: 125824
(Substitutions, Deletions, Insertions) N: (6, 1, 6) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the of peter of the of of picked the pickled pickled peppers where's peck of pickled peppers the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.650797466747463 s  Speed of Backtrace: 0.0006054751574993134 s  Forward Count: 103088
(Substitutions, Deletions, Insertions) N: (6, 0, 7) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the picked piper of picked peck of the pick



*****************************************
File: /group/teaching/asr/labs/recordings/0059.wav 
Speed of Viterbi Decoder: 3.999104266986251 s  Speed of Backtrace: 0.0004946766421198845 s  Forward Count: 85396
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 7
WER: 1.5714285714285714
Trascription: peter pickled a peck of pickled peppers
Recognition: the the the the of picked of peck of pickled the of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0060.wav 
Speed of Viterbi Decoder: 2.4164811614900827 s  Speed of Backtrace: 0.0003176005557179451 s  Forward Count: 52369
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 5
WER: 2.2
Trascription: piper peter picked a peck
Recognition: the the pickled the of of peter of of the of peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.6888828976079822 s  Speed of Backtrace: 0.00023467745631933212 s  Forward Coun



*****************************************
File: /group/teaching/asr/labs/recordings/0080.wav 
Speed of Viterbi Decoder: 4.337949715554714 s  Speed of Backtrace: 0.0004334719851613045 s  Forward Count: 71451
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 8
WER: 0.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked a peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0081.wav 
Speed of Viterbi Decoder: 3.8189858999103308 s  Speed of Backtrace: 0.000389687716960907 s  Forward Count: 64592
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 9
WER: 0.2222222222222222
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.761863366700709 s  Speed of Backtrace: 0.00030

...



*****************************************
File: /group/teaching/asr/labs/recordings/0259.wav 
Speed of Viterbi Decoder: 2.193377778865397 s  Speed of Backtrace: 0.0003251228481531143 s  Forward Count: 47978
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 8
WER: 0.875
Trascription: pickled peter piper picked a peck of peppers
Recognition: picked the pickled peter piper of picked of peck of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0260.wav 
Speed of Viterbi Decoder: 3.51606975402683 s  Speed of Backtrace: 0.00043824873864650726 s  Forward Count: 77763
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 10
WER: 0.2
Trascription: peppers peppers pickled peppers where's the peck of pickled peppers
Recognition: the peppers peppers pickled peppers where's the peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0261.wav 
Speed of Viterbi Decoder: 2.3882199712097645 s  Spe



*****************************************
File: /group/teaching/asr/labs/recordings/0279.wav 
Speed of Viterbi Decoder: 7.011000952683389 s  Speed of Backtrace: 0.0009308867156505585 s  Forward Count: 152581
(Substitutions, Deletions, Insertions) N: (5, 0, 7) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: piper the peter piper picked of peck of pickled peck where's where's of peck of pickled the where's peter pickled picked the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0280.wav 
Speed of Viterbi Decoder: 4.299542821012437 s  Speed of Backtrace: 0.0005265241488814354 s  Forward Count: 93257
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 10
WER: 0.8
Trascription: peter piper picked peppers where's the peppers peter piper picked
Recognition: picked the of piper picked the where's where's the peppers peter where's pickled p



*****************************************
File: /group/teaching/asr/labs/recordings/0298.wav 
Speed of Viterbi Decoder: 2.8824074752628803 s  Speed of Backtrace: 0.0003795633092522621 s  Forward Count: 64081
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0299.wav 
Speed of Viterbi Decoder: 2.9004708230495453 s  Speed of Backtrace: 0.00038324110209941864 s  Forward Count: 63231
(Substitutions, Deletions, Insertions) N: (1, 0, 6) 6
WER: 1.1666666666666667
Trascription: pickled peppers peck where's peter piper
Recognition: picked the pickled of where's peck the where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0300.wav 
Speed of Viterbi Decoder: 3.594350450672209



*****************************************
File: /group/teaching/asr/labs/recordings/0317.wav 
Speed of Viterbi Decoder: 2.6318411864340305 s  Speed of Backtrace: 0.00033231452107429504 s  Forward Count: 58982
(Substitutions, Deletions, Insertions) N: (3, 1, 4) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter of piper picked the pickled pickled piper where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0318.wav 
Speed of Viterbi Decoder: 2.9686898542568088 s  Speed of Backtrace: 0.0003824755549430847 s  Forward Count: 66478
(Substitutions, Deletions, Insertions) N: (1, 1, 3) 9
WER: 0.5555555555555556
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's of picked pickled peppers peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0319.wav 
Speed of Viterbi Decoder: 6.439530480653048 s  Speed of Back



*****************************************
File: /group/teaching/asr/labs/recordings/0336.wav 
Speed of Viterbi Decoder: 3.647024570032954 s  Speed of Backtrace: 0.00046848319470882416 s  Forward Count: 79868
(Substitutions, Deletions, Insertions) N: (4, 0, 9) 8
WER: 1.625
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the where's the where's of of peter the of peck of the pickled peppers piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0337.wav 
Speed of Viterbi Decoder: 3.483098426833749 s  Speed of Backtrace: 0.0004420401528477669 s  Forward Count: 75954
(Substitutions, Deletions, Insertions) N: (6, 0, 6) 8
WER: 1.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the where's of peter where's of the pickled the of picked of the


*****************************************
File: /group/teaching/asr/labs/recordings/0338.wav 
Speed of Viterbi Decoder: 3.0840350668877363 s  Speed of Ba

In [18]:
experiment_set_up('b_w', 0.4, 0.6, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.91629076 -log(0.4)
Transist Weight: 0.510825634 -log(0.6)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 4.837698686867952 s  Speed of Backtrace: 0.0005007004365324974 s  Forward Count: 80038
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 8
WER: 1.5
Trascription: of of a peter the piper the pickled
Recognition: the a of a of of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.02598249912262 s  Speed of Backtrace: 0.0008767098188400269 s  Forward Count: 150761
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pick



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.4749327963218093 s  Speed of Backtrace: 0.0001906091347336769 s  Forward Count: 25205
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.6089462973177433 s  Speed of Backtrace: 0.00037486758083105087 s  Forward Count: 61268
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 6.319224235601723 s  Speed of Backtrace: 0.0006501907482743263 s  Forward Count: 107504
(Substi



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.645856758579612 s  Speed of Backtrace: 0.001333877444267273 s  Forward Count: 103566
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.368335761129856 s  Speed of Backtrace: 0.0003723781555891037 s  Forward Count: 51147
(Substitutions, Deletions, Insertions) N: (1, 0, 4) 5
WER: 1.0
Trascription: pickled piper of the picked
Recognition: picked the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.w



*****************************************
File: /group/teaching/asr/labs/recordings/0060.wav 
Speed of Viterbi Decoder: 3.140666000545025 s  Speed of Backtrace: 0.0003175158053636551 s  Forward Count: 52691
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 5
WER: 1.8
Trascription: piper peter picked a peck
Recognition: the pickled the of of peter of of of peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 2.242046194151044 s  Speed of Backtrace: 0.00024202372878789902 s  Forward Count: 36573
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 2
WER: 3.0
Trascription: piper picked
Recognition: the peck the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 3.1758738718926907 s  Speed of Backtrace: 0.0003266334533691406 s  Forward Count: 51726
(Substitutions, Deletions, Insertions) N: (3, 0, 7) 3
WER: 3.333333333333333



*****************************************
File: /group/teaching/asr/labs/recordings/0081.wav 
Speed of Viterbi Decoder: 2.9688388388603926 s  Speed of Backtrace: 0.00037170853465795517 s  Forward Count: 64768
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 9
WER: 0.2222222222222222
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.097829442471266 s  Speed of Backtrace: 0.00027790293097496033 s  Forward Count: 46858
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.279924239963293 s  Speed of Backtrace:

...



*****************************************
File: /group/teaching/asr/labs/recordings/0262.wav 
Speed of Viterbi Decoder: 2.274430246092379 s  Speed of Backtrace: 0.00032005738466978073 s  Forward Count: 48471
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 8
WER: 0.25
Trascription: where's the piper of peppers pickled peter peck
Recognition: the where's the piper of peppers pickled peter peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 2.874800017103553 s  Speed of Backtrace: 0.0003850813955068588 s  Forward Count: 60336
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.405900211073458 s  Speed of Backtrace: 0.0004252670332789421 s  Forward Count: 71106
(S



*****************************************
File: /group/teaching/asr/labs/recordings/0282.wav 
Speed of Viterbi Decoder: 4.465972503647208 s  Speed of Backtrace: 0.0005479790270328522 s  Forward Count: 94192
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 11
WER: 0.45454545454545453
Trascription: a peck of pickled peppers where's the peck of pickled peppers
Recognition: peck the of peck of pickled peppers where's the peck where's pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 5.143205667845905 s  Speed of Backtrace: 0.0015527615323662758 s  Forward Count: 105455
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decod



*****************************************
File: /group/teaching/asr/labs/recordings/0301.wav 
Speed of Viterbi Decoder: 3.836973783560097 s  Speed of Backtrace: 0.00045127328485250473 s  Forward Count: 78004
(Substitutions, Deletions, Insertions) N: (0, 0, 5) 7
WER: 0.7142857142857143
Trascription: of pickled peppers picked peter piper peck
Recognition: the where's the of pickled peppers picked peter of piper peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.688821733929217 s  Speed of Backtrace: 0.00035677943378686905 s  Forward Count: 55039
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 2.112730865366757 s  Speed of Backtrace: 0.0002795867621898651 s  F



*****************************************
File: /group/teaching/asr/labs/recordings/0320.wav 
Speed of Viterbi Decoder: 3.0928077679127455 s  Speed of Backtrace: 0.0003744298592209816 s  Forward Count: 67690
(Substitutions, Deletions, Insertions) N: (0, 3, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the peter piper of picked pickled picked peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 2.921976494602859 s  Speed of Backtrace: 0.0003536725416779518 s  Forward Count: 64321
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.240916347131133 s  Speed of Backtrace: 0.0004339804872870445 s  Forward Count:



*****************************************
File: /group/teaching/asr/labs/recordings/0340.wav 
Speed of Viterbi Decoder: 3.1803510347381234 s  Speed of Backtrace: 0.0004068715497851372 s  Forward Count: 68151
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 5
WER: 1.4
Trascription: peter piper picked a peck
Recognition: the of peter picked piper the picked the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 2.651194333098829 s  Speed of Backtrace: 0.00033600442111492157 s  Forward Count: 57494
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.7817137399688363 s  Speed of Backtrace: 0.0002574669197201729 s  Forward Count: 39102
(Substitutions, Deletions, Insertions) N

In [19]:
experiment_set_up('b_w', 0.5, 0.5, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.726129007525742 s  Speed of Backtrace: 0.0005085635930299759 s  Forward Count: 80212
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a of a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.0553675619885325 s  Speed of Backtrace: 0.0012887055054306984 s  Forward Count: 151127
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pi



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1143504502251744 s  Speed of Backtrace: 0.0001667700707912445 s  Forward Count: 25342
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.742362485267222 s  Speed of Backtrace: 0.00037461984902620316 s  Forward Count: 61467
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.815522318705916 s  Speed of Backtrace: 0.0006195623427629471 s  Forward Count: 107839
(Substit



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.650782257318497 s  Speed of Backtrace: 0.0006012599915266037 s  Forward Count: 103946
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.3274826677516103 s  Speed of Backtrace: 0.00032395869493484497 s  Forward Count: 51282
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Sp



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.687647863291204 s  Speed of Backtrace: 0.000252588652074337 s  Forward Count: 36693
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 3.154765646904707 s  Speed of Backtrace: 0.00033099204301834106 s  Forward Count: 51959
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 3
WER: 2.6666666666666665
Trascription: peck peppers peter
Recognition: the pickled of of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.9147161273285747 s  Speed of Backtrace: 0.00036781560629606247 s  Forward Count: 63724
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter piper pi



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.790783992037177 s  Speed of Backtrace: 0.00028825365006923676 s  Forward Count: 46976
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.6895179068669677 s  Speed of Backtrace: 0.00020695291459560394 s  Forward Count: 28689
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.8189254747703671 s  Speed of Backtrace: 0.0002547251060605049 s  Forward Count: 40652
(Substitutions, Deleti

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 2.7549565993249416 s  Speed of Backtrace: 0.0003509828820824623 s  Forward Count: 60495
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 4.26690827216953 s  Speed of Backtrace: 0.0004183659330010414 s  Forward Count: 71296
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.5513562439009547 s  Speed of Backtrace: 0.0003528343513607



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 4.9099223194643855 s  Speed of Backtrace: 0.0005957130342721939 s  Forward Count: 105715
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.65507058892399 s  Speed of Backtrace: 0.0010201064869761467 s  Forward Count: 188341
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the





*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.5214050952345133 s  Speed of Backtrace: 0.00034663453698158264 s  Forward Count: 55172
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 1.9315807353705168 s  Speed of Backtrace: 0.0002606762573122978 s  Forward Count: 43085
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.649913711473346 s  Speed of Backtrace: 0.0008330335840582848 s  Forward Count: 145301
(Substitutio



*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 3.8336042035371065 s  Speed of Backtrace: 0.0003793202340602875 s  Forward Count: 64578
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 4.262938665226102 s  Speed of Backtrace: 0.00045008864253759384 s  Forward Count: 72117
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 7
WER: 1.2857142857142858
Trascription: where's the pickled peppers peter piper picked
Recognition: the where's where's where's of of where's peck of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 2.613714043982327 s  Speed of Backtrace: 0.00030455



*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 2.6584622897207737 s  Speed of Backtrace: 0.0003658505156636238 s  Forward Count: 57639
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.7877041371539235 s  Speed of Backtrace: 0.00024361908435821533 s  Forward Count: 39309
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 4
WER: 2.0
Trascription: peter peter peter peter
Recognition: the the the the peter the peck picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.277930793352425 s  Speed of Backtrace: 0.0004109032452106476 s  Forward Count: 70961
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 

In [21]:
experiment_set_up('b_w', 0.6, 0.4, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.510825634 -log(0.6)
Transist Weight: 0.91629076 -log(0.4)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7492879182100296 s  Speed of Backtrace: 0.0004884498193860054 s  Forward Count: 80395
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.002289846539497 s  Speed of Backtrace: 0.0008663088083267212 s  Forward Count: 151418
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pickle



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.0870927209034562 s  Speed of Backtrace: 0.00015375670045614243 s  Forward Count: 25505
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.6667784126475453 s  Speed of Backtrace: 0.0003447355702519417 s  Forward Count: 61633
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.685991985723376 s  Speed of Backtrace: 0.0005810027942061424 s  Forward Count: 108218
(Substitution



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.553249042481184 s  Speed of Backtrace: 0.0006152484565973282 s  Forward Count: 104315
(Substitutions, Deletions, Insertions) N: (3, 1, 5) 17
WER: 0.5294117647058824
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.2965829726308584 s  Speed of Backtrace: 0.00032027624547481537 s  Forward Count: 51390
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed o



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.6483913669362664 s  Speed of Backtrace: 0.0002270350232720375 s  Forward Count: 36818
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.3331600995734334 s  Speed of Backtrace: 0.0002924622967839241 s  Forward Count: 52160
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.910472300834954 s  Speed of Backtrace: 0.00037453602999448776 s  Forward Count: 63963
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: p



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.0584512297064066 s  Speed of Backtrace: 0.0002974988892674446 s  Forward Count: 47095
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.285576470196247 s  Speed of Backtrace: 0.00017471704632043839 s  Forward Count: 28801
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.7534037716686726 s  Speed of Backtrace: 0.00023036915808916092 s  Forward Count: 40791
(Substitutions, Deleti

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 2.733495756983757 s  Speed of Backtrace: 0.000941823236644268 s  Forward Count: 60658
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.1803542505949736 s  Speed of Backtrace: 0.00039854366332292557 s  Forward Count: 71475
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.510907565243542 s  Speed of Backtrace: 0.0003462703898549



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 4.8799256309866905 s  Speed of Backtrace: 0.0005969135090708733 s  Forward Count: 105999
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.627610980533063 s  Speed of Backtrace: 0.0010423781350255013 s  Forward Count: 188720
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the




*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 1.9149676943197846 s  Speed of Backtrace: 0.00027912016957998276 s  Forward Count: 43182
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.540094746276736 s  Speed of Backtrace: 0.0008835950866341591 s  Forward Count: 145816
(Substitutions, Deletions, Insertions) N: (9, 1, 7) 17
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the of piper of picked the a where's picked where's where's the picked of picked where's a a piper a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0305.wa



*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.2736018979921937 s  Speed of Backtrace: 0.0004190634936094284 s  Forward Count: 72478
(Substitutions, Deletions, Insertions) N: (4, 0, 3) 7
WER: 1.0
Trascription: where's the pickled peppers peter piper picked
Recognition: where's where's of of where's peck of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 2.0014170482754707 s  Speed of Backtrace: 0.0002536904066801071 s  Forward Count: 44565
(Substitutions, Deletions, Insertions) N: (2, 1, 3) 5
WER: 1.2
Trascription: a peck of pickled peppers
Recognition: the of pickled pickled of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0324.wav 
Speed of Viterbi Decoder: 7.380393176339567 s  Speed of Backtrace: 0.0010719383135437965 s  Forward Count: 160586
(Substitutions, Deletion



*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.8223108798265457 s  Speed of Backtrace: 0.000269097276031971 s  Forward Count: 39510
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 4
WER: 2.0
Trascription: peter peter peter peter
Recognition: the the the the peter the peck picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.335092102177441 s  Speed of Backtrace: 0.0004433784633874893 s  Forward Count: 71160
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: piper pickled pickled peppers
Recognition: the of piper the where's the peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0344.wav 
Speed of Viterbi Decoder: 5.230070103891194 s  Speed of Backtrace: 0.0006510959938168526 s  Forward Count: 116739
(Substitutions, Deletions, Insertions) N: (6, 0

In [22]:
experiment_set_up('b_w', 0.7, 0.3, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.356674939 -log(0.7)
Transist Weight: 1.20397282 -log(0.3)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 4.79605554509908 s  Speed of Backtrace: 0.0005124965682625771 s  Forward Count: 80570
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.093042140826583 s  Speed of Backtrace: 0.001070912927389145 s  Forward Count: 151682
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 10
WER: 0.7
Trascription: piper peck peppers peter peter picked pickled p



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1155948657542467 s  Speed of Backtrace: 0.0001846151426434517 s  Forward Count: 25698
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7382390620186925 s  Speed of Backtrace: 0.0003673601895570755 s  Forward Count: 61835
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.818101219832897 s  Speed of Backtrace: 0.000613408163189888 s  Forward Count: 108601
(Substitutions, Delet



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.711401336826384 s  Speed of Backtrace: 0.000637478195130825 s  Forward Count: 104789
(Substitutions, Deletions, Insertions) N: (5, 1, 5) 17
WER: 0.6470588235294118
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked peck of pickled peppers where's the a of pickled the where's the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.352974963374436 s  Speed of Backtrace: 0.00032052770256996155 s  Forward Count: 51517
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viter



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.6971081551164389 s  Speed of Backtrace: 0.0003854651004076004 s  Forward Count: 36962
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.396514732390642 s  Speed of Backtrace: 0.00030792970210313797 s  Forward Count: 52444
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.94572317507118 s  Speed of Backtrace: 0.0003948863595724106 s  Forward Count: 64266
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: pet



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.09774733427912 s  Speed of Backtrace: 0.0003113541752099991 s  Forward Count: 47215
(Substitutions, Deletions, Insertions) N: (1, 0, 1) 7
WER: 0.2857142857142857
Trascription: the pickled peppers of the piper peter
Recognition: the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.3177055343985558 s  Speed of Backtrace: 0.00017846934497356415 s  Forward Count: 28939
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.7846963414922357 s  Speed of Backtrace: 0.0002589831128716469 s  Forward Count: 40946
(Substitutions, Deletions, Inse

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 3.5852117463946342 s  Speed of Backtrace: 0.0003854827955365181 s  Forward Count: 60859
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.2604745533317327 s  Speed of Backtrace: 0.00046791043132543564 s  Forward Count: 71661
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.548733811825514 s  Speed of Backtrace: 0.00032353121787



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 5.0770125621929765 s  Speed of Backtrace: 0.0015991423279047012 s  Forward Count: 106288
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.641659590415657 s  Speed of Backtrace: 0.001047670841217041 s  Forward Count: 189184
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the





*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 1.9283995926380157 s  Speed of Backtrace: 0.0002537239342927933 s  Forward Count: 43295
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.700428116135299 s  Speed of Backtrace: 0.0010493919253349304 s  Forward Count: 146347
(Substitutions, Deletions, Insertions) N: (9, 1, 6) 17
WER: 0.9411764705882353
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the piper of picked the a where's picked where's where's the picked of picked where's a a piper a peter the


*****************************************
File: /group/teaching/asr/labs/recordi



*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.2506374549120665 s  Speed of Backtrace: 0.0004593515768647194 s  Forward Count: 72743
(Substitutions, Deletions, Insertions) N: (5, 0, 2) 7
WER: 1.0
Trascription: where's the pickled peppers peter piper picked
Recognition: where's where's of of where's peck of piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 1.9918923266232014 s  Speed of Backtrace: 0.00028015393763780594 s  Forward Count: 44821
(Substitutions, Deletions, Insertions) N: (2, 1, 3) 5
WER: 1.2
Trascription: a peck of pickled peppers
Recognition: the of pickled pickled of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0324.wav 
Speed of Viterbi Decoder: 7.392616507597268 s  Speed of Backtrace: 0.0009265458211302757 s  Forward Count: 161092
(Substitutions, Deletions, Ins



*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.8308317745104432 s  Speed of Backtrace: 0.00026227720081806183 s  Forward Count: 39674
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 4
WER: 2.0
Trascription: peter peter peter peter
Recognition: the the the the peter the peck the the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.378299026750028 s  Speed of Backtrace: 0.000431290827691555 s  Forward Count: 71356
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: piper pickled pickled peppers
Recognition: the of piper the where's the peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0344.wav 
Speed of Viterbi Decoder: 5.303039126098156 s  Speed of Backtrace: 0.0006921980530023575 s  Forward Count: 117128
(Substitutions, Deletions, Insertions) N: (6, 0, 

In [23]:
experiment_set_up('b_w', 0.8, 0.2, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.223143548 -log(0.8)
Transist Weight: 1.60943794 -log(0.2)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7239870568737388 s  Speed of Backtrace: 0.0004618251696228981 s  Forward Count: 80795
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.356545468792319 s  Speed of Backtrace: 0.0008906535804271698 s  Forward Count: 151995
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 10
WER: 0.6
Trascription: piper peck peppers peter peter picked pickle



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.104625073261559 s  Speed of Backtrace: 0.00017861276865005493 s  Forward Count: 25852
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7538287164643407 s  Speed of Backtrace: 0.0003524329513311386 s  Forward Count: 62189
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.799836549907923 s  Speed of Backtrace: 0.0005972292274236679 s  Forward Count: 109121
(Substitutions, Dele



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.617350018583238 s  Speed of Backtrace: 0.0006152857095003128 s  Forward Count: 105296
(Substitutions, Deletions, Insertions) N: (7, 2, 5) 17
WER: 0.8235294117647058
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked of of peppers where's the a of picked the where's the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.336792167276144 s  Speed of Backtrace: 0.00029965024441480637 s  Forward Count: 51681
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterbi Decoder



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.6585557777434587 s  Speed of Backtrace: 0.00024191197007894516 s  Forward Count: 37101
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.3334706090390682 s  Speed of Backtrace: 0.00032201875001192093 s  Forward Count: 52767
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.9055161345750093 s  Speed of Backtrace: 0.0012162616476416588 s  Forward Count: 64483
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription:



*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.2919471757486463 s  Speed of Backtrace: 0.00018863845616579056 s  Forward Count: 29130
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.7830266375094652 s  Speed of Backtrace: 0.00025857333093881607 s  Forward Count: 41075
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 2.913823734037578 s  Speed of Backtrace: 0.0010178331285715103 s  Forward Count: 64593
(Substitutions, Deletions, Insert

...



*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.6856430545449257 s  Speed of Backtrace: 0.00035395286977291107 s  Forward Count: 57676
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: the where's of piper a picked of peck of picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 5.358780733309686 s  Speed of Backtrace: 0.0007188776507973671 s  Forward Count: 116885
(Substitutions, Deletions, Insertions) N: (4, 2, 6) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the a of piper picked of pickled the of peppers where's of peck of pickled where's a of piper picked the


*****************************************
File: /group/teaching/asr/l



*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 3.6623135628178716 s  Speed of Backtrace: 0.0004886267706751823 s  Forward Count: 81632
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 6
WER: 0.5
Trascription: peck peck pickled peck of peppers
Recognition: the a peck pickled peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0286.wav 
Speed of Viterbi Decoder: 5.605490528047085 s  Speed of Backtrace: 0.0007101455703377724 s  Forward Count: 126730
(Substitutions, Deletions, Insertions) N: (3, 0, 3) 13
WER: 0.46153846153846156
Trascription: piper picked piper picked piper peck where's of piper picked peck picked the
Recognition: the piper peck piper peck piper peck where's of piper picked picked picked a the the


*****************************************
File: /group/teaching/asr/labs/recordings/0287.wav 
Speed of Viterbi Decoder: 9.079497602768242 s  Speed



*****************************************
File: /group/teaching/asr/labs/recordings/0305.wav 
Speed of Viterbi Decoder: 5.784989594481885 s  Speed of Backtrace: 0.000720493495464325 s  Forward Count: 133430
(Substitutions, Deletions, Insertions) N: (8, 0, 6) 17
WER: 0.8235294117647058
Trascription: peter piper pickled a peck of picked peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper picked a a peck of the peck where's the a the peck of picked where's the a pickled picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0306.wav 
Speed of Viterbi Decoder: 6.346973930485547 s  Speed of Backtrace: 0.0008026575669646263 s  Forward Count: 146831
(Substitutions, Deletions, Insertions) N: (10, 1, 6) 17
WER: 1.0
Trascription: where's the peck of pickled peppers peter piper picked peter piper pickled a peck of picked peppers
Recognition: the pickled a the where's pickled where's of picked of of picked the pic



*****************************************
File: /group/teaching/asr/labs/recordings/0325.wav 
Speed of Viterbi Decoder: 2.9729543337598443 s  Speed of Backtrace: 0.0003962302580475807 s  Forward Count: 67238
(Substitutions, Deletions, Insertions) N: (5, 0, 3) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the of of picked of peck of picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0326.wav 
Speed of Viterbi Decoder: 4.065867993980646 s  Speed of Backtrace: 0.0005247937515377998 s  Forward Count: 89385
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers the piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0327.wav 
Speed of Viterbi Decoder: 2.7348321797326207 s  Speed of Backtrace: 0.00035484



*****************************************
File: /group/teaching/asr/labs/recordings/0345.wav 
Speed of Viterbi Decoder: 2.418025747872889 s  Speed of Backtrace: 0.0003311801701784134 s  Forward Count: 56392
(Substitutions, Deletions, Insertions) N: (2, 2, 4) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the piper a of peck pickled where's a the


*****************************************
File: /group/teaching/asr/labs/recordings/0346.wav 
Speed of Viterbi Decoder: 2.060979559086263 s  Speed of Backtrace: 0.0002974551171064377 s  Forward Count: 48849
(Substitutions, Deletions, Insertions) N: (4, 0, 2) 8
WER: 0.75
Trascription: a peck of pickled peppers peter piper picked
Recognition: the a picked of piper picked of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0347.wav 
Speed of Viterbi Decoder: 1.825152182020247 s  Speed of Backtrace: 0.00026643555611371994 s  Forward Count: 41380
(Subst

In [24]:
experiment_set_up('b_w', 0.9, 0.1, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.105360515 -log(0.9)
Transist Weight: 2.30258512 -log(0.1)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.6145446449518204 s  Speed of Backtrace: 0.0004547964781522751 s  Forward Count: 81197
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 8
WER: 1.125
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.143345786258578 s  Speed of Backtrace: 0.0008818367496132851 s  Forward Count: 152644
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 10
WER: 0.5
Trascription: piper peck peppers peter peter picked pickled peck pe



*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.6941605946049094 s  Speed of Backtrace: 0.0003576138988137245 s  Forward Count: 62726
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.737541252747178 s  Speed of Backtrace: 0.0006308434531092644 s  Forward Count: 109859
(Substitutions, Deletions, Insertions) N: (6, 3, 3) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the of of picked of peck picked where's peck the peck picked where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordin



*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.3355796234682202 s  Speed of Backtrace: 0.0003180326893925667 s  Forward Count: 51920
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 5
WER: 0.6
Trascription: pickled piper of the picked
Recognition: the of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterbi Decoder: 4.0724670039489865 s  Speed of Backtrace: 0.0005324818193912506 s  Forward Count: 94801
(Substitutions, Deletions, Insertions) N: (6, 2, 2) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked of picked peck of picked peppers where's peck of picked where's the piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0043.wav 
Speed of Viterbi Decoder: 2.92976



*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.8972765877842903 s  Speed of Backtrace: 0.00037288200110197067 s  Forward Count: 64907
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: peter piper picked a pickled peter
Recognition: the of of of picked the of a the the


*****************************************
File: /group/teaching/asr/labs/recordings/0064.wav 
Speed of Viterbi Decoder: 3.8169500418007374 s  Speed of Backtrace: 0.00048565957695245743 s  Forward Count: 83510
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 5
WER: 1.2
Trascription: piper peter picked pickled peppers
Recognition: the piper of a of a pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0065.wav 
Speed of Viterbi Decoder: 2.9612833252176642 s  Speed of Backtrace: 0.0012340191751718521 s  Forward Count: 64906
(Substitutions, Deletions,



*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.764256444759667 s  Speed of Backtrace: 0.000248979777097702 s  Forward Count: 41336
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 2.883345347829163 s  Speed of Backtrace: 0.0003896830603480339 s  Forward Count: 65189
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 4
WER: 1.75
Trascription: peck pickled peck piper
Recognition: peter the peck the a peck a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0086.wav 
Speed of Viterbi Decoder: 2.5391627149656415 s  Speed of Backtrace: 0.00030671898275613785 s  Forward Count: 58265
(Substitutions, Deletions, Insertion

...



*****************************************
File: /group/teaching/asr/labs/recordings/0268.wav 
Speed of Viterbi Decoder: 3.169985208660364 s  Speed of Backtrace: 0.00043103378266096115 s  Forward Count: 69897
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 7
WER: 1.1428571428571428
Trascription: peter picked a peck of pickled peppers
Recognition: the peter of picked of piper pickled pickled picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0269.wav 
Speed of Viterbi Decoder: 1.8094466514885426 s  Speed of Backtrace: 0.0002420525997877121 s  Forward Count: 39606
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 2
WER: 1.0
Trascription: pickled peppers
Recognition: the pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0270.wav 
Speed of Viterbi Decoder: 2.0163009399548173 s  Speed of Backtrace: 0.0002684537321329117 s  Forward Count: 45223
(Substitutions, Deletions, Inser



*****************************************
File: /group/teaching/asr/labs/recordings/0288.wav 
Speed of Viterbi Decoder: 5.166142770089209 s  Speed of Backtrace: 0.0006277207285165787 s  Forward Count: 111671
(Substitutions, Deletions, Insertions) N: (1, 2, 3) 8
WER: 0.75
Trascription: peter piper picked a peck of pickled peppers
Recognition: the of piper peck of pickled pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0289.wav 
Speed of Viterbi Decoder: 4.044457096606493 s  Speed of Backtrace: 0.0005158577114343643 s  Forward Count: 87682
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's of peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0290.wav 
Speed of Viterbi Decoder: 2.6909813107922673 s  Speed of Backtrace: 0.00036583



*****************************************
File: /group/teaching/asr/labs/recordings/0308.wav 
Speed of Viterbi Decoder: 6.334845338016748 s  Speed of Backtrace: 0.0007966784760355949 s  Forward Count: 142623
(Substitutions, Deletions, Insertions) N: (5, 1, 8) 17
WER: 0.8235294117647058
Trascription: peter piper pickled a picked peck of peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper the of a of picked peck of where's of the a the peck of picked where's the a piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0309.wav 
Speed of Viterbi Decoder: 1.8262563282623887 s  Speed of Backtrace: 0.00024652108550071716 s  Forward Count: 39493
(Substitutions, Deletions, Insertions) N: (0, 0, 1) 3
WER: 0.3333333333333333
Trascription: where's peter piper
Recognition: where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0310.wav 
Speed of Viterbi 



*****************************************
File: /group/teaching/asr/labs/recordings/0329.wav 
Speed of Viterbi Decoder: 7.955227610655129 s  Speed of Backtrace: 0.0016474910080432892 s  Forward Count: 173780
(Substitutions, Deletions, Insertions) N: (3, 1, 5) 17
WER: 0.5294117647058824
Trascription: peppers peck picked the piper where's piper peppers picked peter a peck pickled of peter of pickled
Recognition: the peppers peck peck picked the piper where's the piper peter picked picked a picked the pickled of of pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0330.wav 
Speed of Viterbi Decoder: 3.3794982424005866 s  Speed of Backtrace: 0.0010396670550107956 s  Forward Count: 74021
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 7
WER: 0.42857142857142855
Trascription: where's the peppers peter piper peck picked
Recognition: the where's the where's peter piper peck picked the


*****************************************
File: /group



*****************************************
File: /group/teaching/asr/labs/recordings/0350.wav 
Speed of Viterbi Decoder: 5.019904550164938 s  Speed of Backtrace: 0.0005349302664399147 s  Forward Count: 85838
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: the a peter piper picked picked of peck a pickled where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0351.wav 
Speed of Viterbi Decoder: 5.282295038923621 s  Speed of Backtrace: 0.0005853725597262383 s  Forward Count: 89429
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 9
WER: 0.8888888888888888
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the a where's of peck of the picked of where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0352.wav 
Speed of Viterbi Decoder: 3.1329625695943832 s  Speed of 

# Unigram Baseline selfloop weight & transist weight 0.1 -> 0.9

In [26]:
experiment_set_up('uni_w', 0.1, 0.9, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 2.30258512 -log(0.1)
Transist Weight: 0.105360515 -log(0.9)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.738458794541657 s  Speed of Backtrace: 0.0004935581237077713 s  Forward Count: 79168
(Substitutions, Deletions, Insertions) N: (1, 0, 15) 8
WER: 2.0
Trascription: of of a peter the piper the pickled
Recognition: peck the a of a of the of peter the peck a of picked a piper pickled the the pickled picked the a


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.191843839362264 s  Speed of Backtrace: 0.0008716369047760963 s  Forward Count: 149634
(Substitutions, Deletions, Insertions) N: (0, 1, 12) 10
WER: 1.3
Trascription: piper pec



*****************************************
File: /group/teaching/asr/labs/recordings/0019.wav 
Speed of Viterbi Decoder: 5.54453522246331 s  Speed of Backtrace: 0.002141037955880165 s  Forward Count: 116463
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: the peck of pickled peppers peter piper picked
Recognition: pickled the picked picked of pickled peppers the of peck picked picked the picked the the


*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1173085300251842 s  Speed of Backtrace: 0.00018816441297531128 s  Forward Count: 24648
(Substitutions, Deletions, Insertions) N: (1, 0, 7) 3
WER: 2.6666666666666665
Trascription: peter piper picked
Recognition: peck the peter of of of a peppers picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.866045478731394 s  Speed of Backtrace: 0.000401214696466922



*****************************************
File: /group/teaching/asr/labs/recordings/0038.wav 
Speed of Viterbi Decoder: 5.096957487985492 s  Speed of Backtrace: 0.0014890609309077263 s  Forward Count: 111763
(Substitutions, Deletions, Insertions) N: (7, 0, 11) 17
WER: 1.0588235294117647
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the pickled piper of a picked peck of the peck of where's where's picked of picked the peck of where's the pickled piper peck picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 5.8245539935305715 s  Speed of Backtrace: 0.0007610144093632698 s  Forward Count: 124310
(Substitutions, Deletions, Insertions) N: (4, 0, 14) 17
WER: 1.0588235294117647
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the of 



*****************************************
File: /group/teaching/asr/labs/recordings/0057.wav 
Speed of Viterbi Decoder: 4.4934186628088355 s  Speed of Backtrace: 0.0006294427439570427 s  Forward Count: 96811
(Substitutions, Deletions, Insertions) N: (2, 0, 10) 13
WER: 0.9230769230769231
Trascription: where's peter pickled peck of pickled peppers the peck piper picked a peppers
Recognition: the the where's peter of pickled peck of pickled peppers the peck picked picked picked of peppers picked the the picked the the


*****************************************
File: /group/teaching/asr/labs/recordings/0058.wav 
Speed of Viterbi Decoder: 3.5738073028624058 s  Speed of Backtrace: 0.00046881847083568573 s  Forward Count: 77326
(Substitutions, Deletions, Insertions) N: (2, 0, 8) 10
WER: 1.0
Trascription: a peck of peter pickled the peppers peck of pickled
Recognition: picked the of peck of peter of pickled of peppers peck of pickled picked the the the the


********************************



*****************************************
File: /group/teaching/asr/labs/recordings/0077.wav 
Speed of Viterbi Decoder: 1.9953478099778295 s  Speed of Backtrace: 0.0005495836958289146 s  Forward Count: 41495
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 6
WER: 1.0
Trascription: the pickled peppers picked peter piper
Recognition: picked the pickled peck where's picked peter of piper pickled peck


*****************************************
File: /group/teaching/asr/labs/recordings/0078.wav 
Speed of Viterbi Decoder: 2.917151862755418 s  Speed of Backtrace: 0.0004180101677775383 s  Forward Count: 63202
(Substitutions, Deletions, Insertions) N: (1, 0, 8) 9
WER: 1.0
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: picked the where's the peck of pickled the peck where's peter of piper picked picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0079.wav 
Speed of Viterbi Decoder: 6.049898570403457 s  S

...



*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.6950247269123793 s  Speed of Backtrace: 0.0003940379247069359 s  Forward Count: 56142
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: picked the picked where's of piper a picked of peck of pickled peck where's picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 5.366291684098542 s  Speed of Backtrace: 0.0007299613207578659 s  Forward Count: 113606
(Substitutions, Deletions, Insertions) N: (7, 0, 8) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked where's of piper picked of pickled pickled peppers picked where's of peck of pickled of where's a of piper picked picked the


*******



*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.70071206241846 s  Speed of Backtrace: 0.001071288250386715 s  Forward Count: 186476
(Substitutions, Deletions, Insertions) N: (2, 0, 12) 19
WER: 0.7368421052631579
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: picked picked the a the peck picked piper picked picked picked pickled pickled of peppers of of where's peppers picked where's piper picked the piper where's peppers pickled picked the the


*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 4.955272478051484 s  Speed of Backtrace: 0.0015027746558189392 s  Forward Count: 80448
(Substitutions, Deletions, Insertions) N: (1, 0, 10) 6
WER: 1.8333333333333333
Trascription: peck peck pickled peck of peppers
Recognition: picked picked the pick



*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.5243910551071167 s  Speed of Backtrace: 0.0003580944612622261 s  Forward Count: 54160
(Substitutions, Deletions, Insertions) N: (1, 0, 9) 6
WER: 1.6666666666666667
Trascription: where's the peck peter piper picked
Recognition: picked the where's where's of peck picked a peter of piper of picked picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 1.9624497629702091 s  Speed of Backtrace: 0.00025504641234874725 s  Forward Count: 42237
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 6
WER: 1.0
Trascription: where's a peck of pickled peter
Recognition: picked the where's of peck of pickled peter a picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.666856079362333 s  Speed of Backtrace: 0.00091185



*****************************************
File: /group/teaching/asr/labs/recordings/0320.wav 
Speed of Viterbi Decoder: 3.0608959775418043 s  Speed of Backtrace: 0.00043146125972270966 s  Forward Count: 66036
(Substitutions, Deletions, Insertions) N: (1, 1, 10) 8
WER: 1.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the peter piper the of the pickled picked the pickled picked a picked the of peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 2.9646248295903206 s  Speed of Backtrace: 0.0004081185907125473 s  Forward Count: 63141
(Substitutions, Deletions, Insertions) N: (3, 0, 7) 6
WER: 1.6666666666666667
Trascription: where's the peck of pickled peppers
Recognition: picked the where's where's picked where's pickled picked where's the of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.2972



*****************************************
File: /group/teaching/asr/labs/recordings/0338.wav 
Speed of Viterbi Decoder: 3.1352487234398723 s  Speed of Backtrace: 0.00045652128756046295 s  Forward Count: 66742
(Substitutions, Deletions, Insertions) N: (4, 0, 17) 8
WER: 2.625
Trascription: peter piper picked a peck of pickled peppers
Recognition: peter the picked where's where's of where's of of pickled the where's of picked where's picked where's picked picked pickled the picked the the the


*****************************************
File: /group/teaching/asr/labs/recordings/0339.wav 
Speed of Viterbi Decoder: 3.6588127994909883 s  Speed of Backtrace: 0.0004945751279592514 s  Forward Count: 78141
(Substitutions, Deletions, Insertions) N: (3, 0, 15) 8
WER: 2.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: peter the peter where's the of piper picked where's the of pickled picked the where's the picked of where's picked picked the the


************************

In [27]:
experiment_set_up('uni_w', 0.2, 0.8, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 1.60943794 -log(0.2)
Transist Weight: 0.223143548 -log(0.8)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.736281141638756 s  Speed of Backtrace: 0.0004793936386704445 s  Forward Count: 79566
(Substitutions, Deletions, Insertions) N: (3, 0, 12) 8
WER: 1.875
Trascription: of of a peter the piper the pickled
Recognition: peck the a of a of the of peter the peck a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 6.9876284915953875 s  Speed of Backtrace: 0.0009065289050340652 s  Forward Count: 150100
(Substitutions, Deletions, Insertions) N: (0, 1, 10) 10
WER: 1.1
Trascription: piper peck peppers pet



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1052045859396458 s  Speed of Backtrace: 0.00018295831978321075 s  Forward Count: 24925
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7697596875950694 s  Speed of Backtrace: 0.00037561822682619095 s  Forward Count: 60620
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper picked of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.838839055970311 s  Speed of Backtrace: 0.0006250692531466484 s  Forward Count: 106693
(



*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 5.708739676512778 s  Speed of Backtrace: 0.0007425285875797272 s  Forward Count: 125191
(Substitutions, Deletions, Insertions) N: (3, 2, 10) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the of peter of the of a of picked the pickled pickled peppers where's peck of pickled peppers the of piper picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.595157789066434 s  Speed of Backtrace: 0.0006053261458873749 s  Forward Count: 102639
(Substitutions, Deletions, Insertions) N: (4, 1, 9) 17
WER: 0.8235294117647058
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the peppers of piper of picke



*****************************************
File: /group/teaching/asr/labs/recordings/0059.wav 
Speed of Viterbi Decoder: 4.032139309681952 s  Speed of Backtrace: 0.0005086315795779228 s  Forward Count: 85091
(Substitutions, Deletions, Insertions) N: (2, 0, 8) 7
WER: 1.4285714285714286
Trascription: peter pickled a peck of pickled peppers
Recognition: the the picked the peter of pickled of peck of pickled the of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0060.wav 
Speed of Viterbi Decoder: 2.4440055461600423 s  Speed of Backtrace: 0.0007561510428786278 s  Forward Count: 52058
(Substitutions, Deletions, Insertions) N: (2, 0, 8) 5
WER: 2.0
Trascription: piper peter picked a peck
Recognition: the the pickled the of of peter of picked the of peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.6980227874591947 s  Speed of Backtrace: 0.00024841632694005966 s



*****************************************
File: /group/teaching/asr/labs/recordings/0080.wav 
Speed of Viterbi Decoder: 3.2835152065381408 s  Speed of Backtrace: 0.0004400936886668205 s  Forward Count: 71215
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 8
WER: 0.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked of peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0081.wav 
Speed of Viterbi Decoder: 2.9559476086869836 s  Speed of Backtrace: 0.00036600884050130844 s  Forward Count: 64360
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 9
WER: 0.2222222222222222
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.129102378152311 s  Speed of Backtrace: 0.

...



*****************************************
File: /group/teaching/asr/labs/recordings/0278.wav 
Speed of Viterbi Decoder: 7.3930434724316 s  Speed of Backtrace: 0.0007425118237733841 s  Forward Count: 121355
(Substitutions, Deletions, Insertions) N: (4, 0, 11) 13
WER: 1.1538461538461537
Trascription: peter picked a peck of peppers where's the peck of peppers peter picked
Recognition: picked the peter a picked picked piper of peck of the peppers where's picked of picked of the a where's peter picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0279.wav 
Speed of Viterbi Decoder: 9.137994909659028 s  Speed of Backtrace: 0.0009445333853363991 s  Forward Count: 151846
(Substitutions, Deletions, Insertions) N: (5, 0, 10) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked piper the peter piper picked the of peck of pickled peck wher



*****************************************
File: /group/teaching/asr/labs/recordings/0296.wav 
Speed of Viterbi Decoder: 1.8141180519014597 s  Speed of Backtrace: 0.0003804406151175499 s  Forward Count: 40351
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 6
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers
Recognition: the where's the peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0297.wav 
Speed of Viterbi Decoder: 2.5113137625157833 s  Speed of Backtrace: 0.0004644123837351799 s  Forward Count: 54701
(Substitutions, Deletions, Insertions) N: (0, 1, 2) 8
WER: 0.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0298.wav 
Speed of Viterbi Decoder: 2.87539635412395 s  Speed of Backtrace: 0.0009066471830010414 s  Forward Count: 63802



*****************************************
File: /group/teaching/asr/labs/recordings/0315.wav 
Speed of Viterbi Decoder: 4.236276919953525 s  Speed of Backtrace: 0.0004295278340578079 s  Forward Count: 70595
(Substitutions, Deletions, Insertions) N: (3, 1, 5) 8
WER: 1.125
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter a of piper picked the piper pickled piper where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0316.wav 
Speed of Viterbi Decoder: 3.305056537501514 s  Speed of Backtrace: 0.0003472752869129181 s  Forward Count: 54456
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 6
WER: 0.8333333333333334
Trascription: where's the peppers peter piper picked
Recognition: the where's of piper where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0317.wav 
Speed of Viterbi Decoder: 3.4764635302126408 s  Speed of Backtrace: 0.0003445791080594063



*****************************************
File: /group/teaching/asr/labs/recordings/0334.wav 
Speed of Viterbi Decoder: 3.5433391965925694 s  Speed of Backtrace: 0.0005119852721691132 s  Forward Count: 76440
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 7
WER: 1.2857142857142858
Trascription: picked peter peck pickled the piper peter
Recognition: picked the picked picked of a picked pickled the piper picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0335.wav 
Speed of Viterbi Decoder: 4.514242579229176 s  Speed of Backtrace: 0.000586862675845623 s  Forward Count: 98611
(Substitutions, Deletions, Insertions) N: (4, 0, 12) 8
WER: 2.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: a picked the picked a piper of pickled of pickled picked the pickled of where's picked picked where's picked picked


*****************************************
File: /group/teaching/asr/labs/recordings/0336.wav 
Speed of Viter



*****************************************
File: /group/teaching/asr/labs/recordings/0354.wav 
Speed of Viterbi Decoder: 3.773061655461788 s  Speed of Backtrace: 0.0004954952746629715 s  Forward Count: 81671
(Substitutions, Deletions, Insertions) N: (2, 0, 9) 8
WER: 1.375
Trascription: peter piper pickled a peck of picked peppers
Recognition: picked the a picked piper peter the pickled of peck of picked a picked peppers picked the
Average
Total Errors: 2899
Total Transcription Words: 2846
Total WER: 1.0186226282501756
The number of forward computations per wav:  75626.58028169014
Average decode time: 3.6390768747514404
Average backtrace time: 0.0005243820125158404


In [28]:
experiment_set_up('uni_w', 0.3, 0.7, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 1.20397282 -log(0.3)
Transist Weight: 0.356674939 -log(0.7)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7100959867239 s  Speed of Backtrace: 0.0005134977400302887 s  Forward Count: 79815
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 8
WER: 1.5
Trascription: of of a peter the piper the pickled
Recognition: the a of a of of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.132567171007395 s  Speed of Backtrace: 0.0009232545271515846 s  Forward Count: 150516
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pickl



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.109603874385357 s  Speed of Backtrace: 0.00019967369735240936 s  Forward Count: 25096
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7480966057628393 s  Speed of Backtrace: 0.00036937277764081955 s  Forward Count: 60984
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper picked of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.803796303458512 s  Speed of Backtrace: 0.0005948105826973915 s  Forward Count: 107103
(S



*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 5.71673428080976 s  Speed of Backtrace: 0.0007112445309758186 s  Forward Count: 125804
(Substitutions, Deletions, Insertions) N: (6, 1, 6) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the of peter of the of of picked the pickled pickled peppers where's peck of pickled peppers the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.6531542064622045 s  Speed of Backtrace: 0.0005976911634206772 s  Forward Count: 103100
(Substitutions, Deletions, Insertions) N: (6, 0, 7) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the picked piper of picked peck of the picke



*****************************************
File: /group/teaching/asr/labs/recordings/0059.wav 
Speed of Viterbi Decoder: 4.007478446699679 s  Speed of Backtrace: 0.000501696951687336 s  Forward Count: 85442
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 7
WER: 1.2857142857142858
Trascription: peter pickled a peck of pickled peppers
Recognition: the the peter of picked of peck of pickled the of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0060.wav 
Speed of Viterbi Decoder: 2.4252597857266665 s  Speed of Backtrace: 0.0003406582400202751 s  Forward Count: 52393
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 5
WER: 2.2
Trascription: piper peter picked a peck
Recognition: the the pickled the of of peter of of the of peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.6843391554430127 s  Speed of Backtrace: 0.00020567793399095535 s  Forward Count: 



*****************************************
File: /group/teaching/asr/labs/recordings/0080.wav 
Speed of Viterbi Decoder: 3.2941699670627713 s  Speed of Backtrace: 0.0004280414432287216 s  Forward Count: 71455
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 8
WER: 0.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper picked a peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0081.wav 
Speed of Viterbi Decoder: 2.898739672265947 s  Speed of Backtrace: 0.0003871684893965721 s  Forward Count: 64595
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 9
WER: 0.2222222222222222
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.0901894690468907 s  Speed of Backtrace: 0.000

...



*****************************************
File: /group/teaching/asr/labs/recordings/0259.wav 
Speed of Viterbi Decoder: 2.194258389994502 s  Speed of Backtrace: 0.00030459649860858917 s  Forward Count: 47979
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 8
WER: 0.875
Trascription: pickled peter piper picked a peck of peppers
Recognition: picked the pickled peter piper of picked of peck of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0260.wav 
Speed of Viterbi Decoder: 3.557468054816127 s  Speed of Backtrace: 0.00047529302537441254 s  Forward Count: 77759
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 10
WER: 0.2
Trascription: peppers peppers pickled peppers where's the peck of pickled peppers
Recognition: the peppers peppers pickled peppers where's the peck of pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0261.wav 
Speed of Viterbi Decoder: 2.420846584253013 s  Sp



*****************************************
File: /group/teaching/asr/labs/recordings/0279.wav 
Speed of Viterbi Decoder: 6.959823583252728 s  Speed of Backtrace: 0.0008658645674586296 s  Forward Count: 152599
(Substitutions, Deletions, Insertions) N: (5, 0, 7) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: piper the peter piper picked of peck of pickled peck where's where's of peck of pickled the where's peter pickled picked the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0280.wav 
Speed of Viterbi Decoder: 4.3739792965352535 s  Speed of Backtrace: 0.0005587693303823471 s  Forward Count: 93293
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 10
WER: 0.8
Trascription: peter piper picked peppers where's the peppers peter piper picked
Recognition: picked the of piper picked the where's where's the peppers peter where's pickled 



*****************************************
File: /group/teaching/asr/labs/recordings/0298.wav 
Speed of Viterbi Decoder: 2.904267568141222 s  Speed of Backtrace: 0.0003811623901128769 s  Forward Count: 64080
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter picked picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0299.wav 
Speed of Viterbi Decoder: 2.8525349106639624 s  Speed of Backtrace: 0.0003679143264889717 s  Forward Count: 63235
(Substitutions, Deletions, Insertions) N: (1, 0, 6) 6
WER: 1.1666666666666667
Trascription: pickled peppers peck where's peter piper
Recognition: picked the pickled of where's peck the where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0300.wav 
Speed of Viterbi Decoder: 3.621286392211914 s



*****************************************
File: /group/teaching/asr/labs/recordings/0317.wav 
Speed of Viterbi Decoder: 2.6632957980036736 s  Speed of Backtrace: 0.00033459998667240143 s  Forward Count: 58980
(Substitutions, Deletions, Insertions) N: (3, 1, 4) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter of piper picked the pickled pickled piper where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0318.wav 
Speed of Viterbi Decoder: 2.9999772366136312 s  Speed of Backtrace: 0.00037798937410116196 s  Forward Count: 66476
(Substitutions, Deletions, Insertions) N: (1, 1, 3) 9
WER: 0.5555555555555556
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's of picked pickled peppers peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0319.wav 
Speed of Viterbi Decoder: 8.520167506299913 s  Speed of Bac



*****************************************
File: /group/teaching/asr/labs/recordings/0336.wav 
Speed of Viterbi Decoder: 3.5877466332167387 s  Speed of Backtrace: 0.00045142602175474167 s  Forward Count: 79938
(Substitutions, Deletions, Insertions) N: (4, 0, 9) 8
WER: 1.625
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the where's the where's of of peter the of peck of the pickled peppers piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0337.wav 
Speed of Viterbi Decoder: 3.389982177875936 s  Speed of Backtrace: 0.0004358431324362755 s  Forward Count: 75976
(Substitutions, Deletions, Insertions) N: (6, 0, 6) 8
WER: 1.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the where's of peter where's of the pickled the of picked of the


*****************************************
File: /group/teaching/asr/labs/recordings/0338.wav 
Speed of Viterbi Decoder: 3.08473832719028 s  Speed of Bac

In [4]:
experiment_set_up('uni_w', 0.4, 0.6, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.91629076 -log(0.4)
Transist Weight: 0.510825634 -log(0.6)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.810639246366918 s  Speed of Backtrace: 0.0015863636508584023 s  Forward Count: 80063
(Substitutions, Deletions, Insertions) N: (3, 0, 9) 8
WER: 1.5
Trascription: of of a peter the piper the pickled
Recognition: the a of a of of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.235486156307161 s  Speed of Backtrace: 0.0024206656962633133 s  Forward Count: 150775
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pic



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1001015920192003 s  Speed of Backtrace: 0.00017981883138418198 s  Forward Count: 25198
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.744126023724675 s  Speed of Backtrace: 0.0006770230829715729 s  Forward Count: 61256
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.8127826899290085 s  Speed of Backtrace: 0.0006363922730088234 s  Forward Count: 107497
(Substi



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.658517744392157 s  Speed of Backtrace: 0.0006107660010457039 s  Forward Count: 103563
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: picked the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.3137066392228007 s  Speed of Backtrace: 0.0003208685666322708 s  Forward Count: 51150
(Substitutions, Deletions, Insertions) N: (1, 0, 4) 5
WER: 1.0
Trascription: pickled piper of the picked
Recognition: picked the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042



*****************************************
File: /group/teaching/asr/labs/recordings/0060.wav 
Speed of Viterbi Decoder: 2.3557299934327602 s  Speed of Backtrace: 0.0003092065453529358 s  Forward Count: 52705
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 5
WER: 1.8
Trascription: piper peter picked a peck
Recognition: the pickled the of of peter of of of peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.6710119927302003 s  Speed of Backtrace: 0.0002505062147974968 s  Forward Count: 36580
(Substitutions, Deletions, Insertions) N: (1, 0, 5) 2
WER: 3.0
Trascription: piper picked
Recognition: the peck the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.4720633579418063 s  Speed of Backtrace: 0.0008033467456698418 s  Forward Count: 51738
(Substitutions, Deletions, Insertions) N: (3, 0, 7) 3
WER: 3.33333333333333



*****************************************
File: /group/teaching/asr/labs/recordings/0081.wav 
Speed of Viterbi Decoder: 2.8959558438509703 s  Speed of Backtrace: 0.00038239825516939163 s  Forward Count: 64766
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 9
WER: 0.2222222222222222
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.097814993932843 s  Speed of Backtrace: 0.0003052670508623123 s  Forward Count: 46875
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.30175765696913 s  Speed of Backtrace: 0

...



*****************************************
File: /group/teaching/asr/labs/recordings/0262.wav 
Speed of Viterbi Decoder: 2.0290483199059963 s  Speed of Backtrace: 0.00027641840279102325 s  Forward Count: 48457
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 8
WER: 0.25
Trascription: where's the piper of peppers pickled peter peck
Recognition: the where's the piper of peppers pickled peter peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 2.5885864105075598 s  Speed of Backtrace: 0.0003713127225637436 s  Forward Count: 60338
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.2134387800469995 s  Speed of Backtrace: 0.000507039949297905 s  Forward Count: 71104




*****************************************
File: /group/teaching/asr/labs/recordings/0282.wav 
Speed of Viterbi Decoder: 4.165422924794257 s  Speed of Backtrace: 0.0005297539755702019 s  Forward Count: 94199
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 11
WER: 0.45454545454545453
Trascription: a peck of pickled peppers where's the peck of pickled peppers
Recognition: peck the of peck of pickled peppers where's the peck where's pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 4.746530706062913 s  Speed of Backtrace: 0.0005832873284816742 s  Forward Count: 105463
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decod



*****************************************
File: /group/teaching/asr/labs/recordings/0301.wav 
Speed of Viterbi Decoder: 3.4851239919662476 s  Speed of Backtrace: 0.00046441610902547836 s  Forward Count: 78018
(Substitutions, Deletions, Insertions) N: (0, 0, 5) 7
WER: 0.7142857142857143
Trascription: of pickled peppers picked peter piper peck
Recognition: the where's the of pickled peppers picked peter of piper peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.556083332747221 s  Speed of Backtrace: 0.0003388477489352226 s  Forward Count: 55053
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 1.84373186994344 s  Speed of Backtrace: 0.0002530934289097786 s  Fo



*****************************************
File: /group/teaching/asr/labs/recordings/0320.wav 
Speed of Viterbi Decoder: 2.9547113459557295 s  Speed of Backtrace: 0.0003872290253639221 s  Forward Count: 67694
(Substitutions, Deletions, Insertions) N: (0, 3, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the peter piper of picked pickled picked peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 2.784040307626128 s  Speed of Backtrace: 0.0003454228863120079 s  Forward Count: 64339
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.0839509395882487 s  Speed of Backtrace: 0.0004120049998164177 s  Forward Count



*****************************************
File: /group/teaching/asr/labs/recordings/0340.wav 
Speed of Viterbi Decoder: 2.9973080717027187 s  Speed of Backtrace: 0.0003847619518637657 s  Forward Count: 68159
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 5
WER: 1.4
Trascription: peter piper picked a peck
Recognition: the of peter picked piper the picked the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 2.5088051464408636 s  Speed of Backtrace: 0.00034304987639188766 s  Forward Count: 57495
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.689422176219523 s  Speed of Backtrace: 0.0003248797729611397 s  Forward Count: 39102
(Substitutions, Deletions, Insertions) N

In [5]:
experiment_set_up('uni_w', 0.5, 0.5, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.5242023691534996 s  Speed of Backtrace: 0.000443238765001297 s  Forward Count: 80226
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a of a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 6.720520666800439 s  Speed of Backtrace: 0.0008186791092157364 s  Forward Count: 151115
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pic



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.0555068887770176 s  Speed of Backtrace: 0.0003318358212709427 s  Forward Count: 25341
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.732098045758903 s  Speed of Backtrace: 0.00042837392538785934 s  Forward Count: 61465
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.70999969355762 s  Speed of Backtrace: 0.0006560329347848892 s  Forward Count: 107844
(Substitu



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.556278987787664 s  Speed of Backtrace: 0.0006112698465585709 s  Forward Count: 103958
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.305778536014259 s  Speed of Backtrace: 0.00030869897454977036 s  Forward Count: 51283
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Spe



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.7498506661504507 s  Speed of Backtrace: 0.00025410857051610947 s  Forward Count: 36698
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.528347705490887 s  Speed of Backtrace: 0.00032731611281633377 s  Forward Count: 51964
(Substitutions, Deletions, Insertions) N: (3, 0, 6) 3
WER: 3.0
Trascription: peck peppers peter
Recognition: the pickled of of of of picked of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.8960979133844376 s  Speed of Backtrace: 0.00037994515150785446 s  Forward Count: 63758
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter piper picked a



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.1328581869602203 s  Speed of Backtrace: 0.00031648389995098114 s  Forward Count: 46984
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.374813187867403 s  Speed of Backtrace: 0.00020629912614822388 s  Forward Count: 28682
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.8495784970000386 s  Speed of Backtrace: 0.0002713426947593689 s  Forward Count: 40649
(Substitutions, Deleti

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 2.71625348739326 s  Speed of Backtrace: 0.00036483537405729294 s  Forward Count: 60494
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.253712797537446 s  Speed of Backtrace: 0.0004572942852973938 s  Forward Count: 71306
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.5194380283355713 s  Speed of Backtrace: 0.0003302302211523



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 4.83079366851598 s  Speed of Backtrace: 0.0006156777963042259 s  Forward Count: 105724
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.49161268863827 s  Speed of Backtrace: 0.0031660376116633415 s  Forward Count: 188353
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the


*



*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.59294502902776 s  Speed of Backtrace: 0.00034188199788331985 s  Forward Count: 55176
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 1.9643757930025458 s  Speed of Backtrace: 0.00026055891066789627 s  Forward Count: 43085
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.423654303885996 s  Speed of Backtrace: 0.0008577276021242142 s  Forward Count: 145329
(Substitution



*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 3.02446021232754 s  Speed of Backtrace: 0.0003707297146320343 s  Forward Count: 64607
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.170957027003169 s  Speed of Backtrace: 0.00041895173490047455 s  Forward Count: 72108
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 7
WER: 1.2857142857142858
Trascription: where's the pickled peppers peter piper picked
Recognition: picked where's where's where's of of where's peck of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 1.9458993896842003 s  Speed of Backtrace: 0.000278



*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 2.61483122035861 s  Speed of Backtrace: 0.00035616662353277206 s  Forward Count: 57642
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.7963615339249372 s  Speed of Backtrace: 0.0002552177757024765 s  Forward Count: 39309
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 4
WER: 2.0
Trascription: peter peter peter peter
Recognition: the the the the peter the peck picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.2724846256896853 s  Speed of Backtrace: 0.0004261806607246399 s  Forward Count: 70976
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4

In [6]:
experiment_set_up('uni_w', 0.6, 0.4, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.510825634 -log(0.6)
Transist Weight: 0.91629076 -log(0.4)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.7452379632741213 s  Speed of Backtrace: 0.0004837391898036003 s  Forward Count: 80400
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 6.932582640089095 s  Speed of Backtrace: 0.0009347796440124512 s  Forward Count: 151411
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pickle



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.0871723340824246 s  Speed of Backtrace: 0.00016120541840791702 s  Forward Count: 25510
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7444076677784324 s  Speed of Backtrace: 0.00038150232285261154 s  Forward Count: 61630
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.647792241536081 s  Speed of Backtrace: 0.0006180871278047562 s  Forward Count: 108195
(Substitutio



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.5638632494956255 s  Speed of Backtrace: 0.0017522266134619713 s  Forward Count: 104310
(Substitutions, Deletions, Insertions) N: (3, 1, 5) 17
WER: 0.5294117647058824
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.2947212383151054 s  Speed of Backtrace: 0.00029993802309036255 s  Forward Count: 51385
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed 



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.710803385823965 s  Speed of Backtrace: 0.0005600648000836372 s  Forward Count: 36831
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.4024024149402976 s  Speed of Backtrace: 0.00032079312950372696 s  Forward Count: 52170
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.9286921126767993 s  Speed of Backtrace: 0.0003994256258010864 s  Forward Count: 63979
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: p



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.113996647298336 s  Speed of Backtrace: 0.00028074439615011215 s  Forward Count: 47094
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.2665520887821913 s  Speed of Backtrace: 0.00018020626157522202 s  Forward Count: 28791
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.7708492344245315 s  Speed of Backtrace: 0.0002393275499343872 s  Forward Count: 40791
(Substitutions, Deleti

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 2.7648183926939964 s  Speed of Backtrace: 0.00040192343294620514 s  Forward Count: 60651
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.4730577496811748 s  Speed of Backtrace: 0.0009088590741157532 s  Forward Count: 71486
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.56325535941869 s  Speed of Backtrace: 0.000363409519195



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 5.047286995686591 s  Speed of Backtrace: 0.000607730820775032 s  Forward Count: 105994
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.89416699577123 s  Speed of Backtrace: 0.0010785134509205818 s  Forward Count: 188742
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the


*



*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 2.0298488587141037 s  Speed of Backtrace: 0.0002758912742137909 s  Forward Count: 43174
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.709298050031066 s  Speed of Backtrace: 0.0009038075804710388 s  Forward Count: 145833
(Substitutions, Deletions, Insertions) N: (9, 1, 7) 17
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the of piper of picked the a where's picked where's where's the picked of picked where's a a piper a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0305.wav



*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.520991986617446 s  Speed of Backtrace: 0.0004242975264787674 s  Forward Count: 72476
(Substitutions, Deletions, Insertions) N: (4, 0, 3) 7
WER: 1.0
Trascription: where's the pickled peppers peter piper picked
Recognition: where's where's of of where's peck of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 2.0330309979617596 s  Speed of Backtrace: 0.0002968171611428261 s  Forward Count: 44579
(Substitutions, Deletions, Insertions) N: (2, 1, 3) 5
WER: 1.2
Trascription: a peck of pickled peppers
Recognition: the of pickled pickled of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0324.wav 
Speed of Viterbi Decoder: 8.389457419514656 s  Speed of Backtrace: 0.0011781314387917519 s  Forward Count: 160597
(Substitutions, Deletions



*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 2.0444229105487466 s  Speed of Backtrace: 0.0002677859738469124 s  Forward Count: 39520
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 4
WER: 2.0
Trascription: peter peter peter peter
Recognition: the the the the peter the peck picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.5557582825422287 s  Speed of Backtrace: 0.0004106098785996437 s  Forward Count: 71153
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: piper pickled pickled peppers
Recognition: the of piper the where's the peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0344.wav 
Speed of Viterbi Decoder: 5.247503396123648 s  Speed of Backtrace: 0.0006673391908407211 s  Forward Count: 116744
(Substitutions, Deletions, Insertions) N: (6,

In [7]:
experiment_set_up('uni_w', 0.7, 0.3, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.356674939 -log(0.7)
Transist Weight: 1.20397282 -log(0.3)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.8396291490644217 s  Speed of Backtrace: 0.0004716431722044945 s  Forward Count: 80584
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.002403778024018 s  Speed of Backtrace: 0.0008578784763813019 s  Forward Count: 151682
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 10
WER: 0.7
Trascription: piper peck peppers peter peter picked pickle



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.1185537027195096 s  Speed of Backtrace: 0.00018418580293655396 s  Forward Count: 25681
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.8223390728235245 s  Speed of Backtrace: 0.00037980638444423676 s  Forward Count: 61854
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.722397041507065 s  Speed of Backtrace: 0.0006413562223315239 s  Forward Count: 108601
(Substitutions, De



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 5.297534386627376 s  Speed of Backtrace: 0.0006293272599577904 s  Forward Count: 104774
(Substitutions, Deletions, Insertions) N: (5, 1, 5) 17
WER: 0.6470588235294118
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked peck of pickled peppers where's the a of pickled the where's the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.474676120094955 s  Speed of Backtrace: 0.0003234781324863434 s  Forward Count: 51519
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viter



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.7984444424510002 s  Speed of Backtrace: 0.0005475031211972237 s  Forward Count: 36969
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.4965281328186393 s  Speed of Backtrace: 0.0006627952679991722 s  Forward Count: 52451
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.9096528571099043 s  Speed of Backtrace: 0.0010675648227334023 s  Forward Count: 64280
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: p



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.0644943937659264 s  Speed of Backtrace: 0.000313696451485157 s  Forward Count: 47225
(Substitutions, Deletions, Insertions) N: (1, 0, 1) 7
WER: 0.2857142857142857
Trascription: the pickled peppers of the piper peter
Recognition: the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.2935374174267054 s  Speed of Backtrace: 0.0004404531791806221 s  Forward Count: 28935
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.7608879078179598 s  Speed of Backtrace: 0.00025978777557611465 s  Forward Count: 40934
(Substitutions, Deletions, Ins

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 2.7672309512272477 s  Speed of Backtrace: 0.0003536101430654526 s  Forward Count: 60869
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.596893056295812 s  Speed of Backtrace: 0.0004411255940794945 s  Forward Count: 71679
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.6744476733729243 s  Speed of Backtrace: 0.000366607680916



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 4.99606301356107 s  Speed of Backtrace: 0.0006269393488764763 s  Forward Count: 106285
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.885063634254038 s  Speed of Backtrace: 0.001128203235566616 s  Forward Count: 189202
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the


*



*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 2.18642614595592 s  Speed of Backtrace: 0.000638982281088829 s  Forward Count: 43308
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.8686101185157895 s  Speed of Backtrace: 0.0008374536409974098 s  Forward Count: 146384
(Substitutions, Deletions, Insertions) N: (9, 1, 6) 17
WER: 0.9411764705882353
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the piper of picked the a where's picked where's where's the picked of picked where's a a piper a peter the


*****************************************
File: /group/teaching/asr/labs/recording



*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.3563604271039367 s  Speed of Backtrace: 0.0004573855549097061 s  Forward Count: 72745
(Substitutions, Deletions, Insertions) N: (5, 0, 2) 7
WER: 1.0
Trascription: where's the pickled peppers peter piper picked
Recognition: where's where's of of where's peck of piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 2.0506969336420298 s  Speed of Backtrace: 0.000683911144733429 s  Forward Count: 44823
(Substitutions, Deletions, Insertions) N: (2, 1, 3) 5
WER: 1.2
Trascription: a peck of pickled peppers
Recognition: the of pickled pickled of where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0324.wav 
Speed of Viterbi Decoder: 8.254356181249022 s  Speed of Backtrace: 0.0010137008503079414 s  Forward Count: 161103
(Substitutions, Deletions, Inser



*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.7881295755505562 s  Speed of Backtrace: 0.00047389138489961624 s  Forward Count: 39690
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 4
WER: 1.75
Trascription: peter peter peter peter
Recognition: the the the the peter the peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.3672294253483415 s  Speed of Backtrace: 0.0005952296778559685 s  Forward Count: 71347
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: piper pickled pickled peppers
Recognition: the of piper the where's the peck of peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0344.wav 
Speed of Viterbi Decoder: 5.321064151823521 s  Speed of Backtrace: 0.0009571844711899757 s  Forward Count: 117138
(Substitutions, Deletions, Insertions) N: (6, 0

In [8]:
experiment_set_up('uni_w', 0.8, 0.2, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.223143548 -log(0.8)
Transist Weight: 1.60943794 -log(0.2)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.89161941036582 s  Speed of Backtrace: 0.0018632346764206886 s  Forward Count: 80796
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.3357308795675635 s  Speed of Backtrace: 0.0015276717022061348 s  Forward Count: 151995
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 10
WER: 0.6
Trascription: piper peck peppers peter peter picked pickled



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.176559998653829 s  Speed of Backtrace: 0.00021078158169984818 s  Forward Count: 25842
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.0183225283399224 s  Speed of Backtrace: 0.0010279817506670952 s  Forward Count: 62190
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.895303645171225 s  Speed of Backtrace: 0.0006328616291284561 s  Forward Count: 109129
(Substitutions, Dele



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 4.76090267021209 s  Speed of Backtrace: 0.0005798488855361938 s  Forward Count: 105303
(Substitutions, Deletions, Insertions) N: (8, 1, 4) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of picked of pickled peppers where's the a of picked the where's the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.4910834869369864 s  Speed of Backtrace: 0.0003590323030948639 s  Forward Count: 51674
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterbi Dec



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.8156255688518286 s  Speed of Backtrace: 0.0002527022734284401 s  Forward Count: 37097
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.6179989613592625 s  Speed of Backtrace: 0.00034860242158174515 s  Forward Count: 52756
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 3
WER: 2.3333333333333335
Trascription: peck peppers peter
Recognition: the pickled of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 3.140344548970461 s  Speed of Backtrace: 0.0003947308287024498 s  Forward Count: 64505
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: p



*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.2991408947855234 s  Speed of Backtrace: 0.00020383764058351517 s  Forward Count: 29112
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.8758888868615031 s  Speed of Backtrace: 0.00043465103954076767 s  Forward Count: 41079
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 3.126868484541774 s  Speed of Backtrace: 0.0010824445635080338 s  Forward Count: 64594
(Substitutions, Deletions, Insert

...



*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.3244947604835033 s  Speed of Backtrace: 0.0004603881388902664 s  Forward Count: 71947
(Substitutions, Deletions, Insertions) N: (1, 1, 3) 9
WER: 0.5555555555555556
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.628830825909972 s  Speed of Backtrace: 0.0003465227782726288 s  Forward Count: 57678
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: the where's of piper a picked of peck of picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0266.wav 
Speed of Viterbi Decoder: 5.320656965486705 s  Speed of Backtrace: 



*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 8.800340786576271 s  Speed of Backtrace: 0.0023634489625692368 s  Forward Count: 189746
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0285.wav 
Speed of Viterbi Decoder: 3.8749868189916015 s  Speed of Backtrace: 0.001471581868827343 s  Forward Count: 81641
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 6
WER: 0.5
Trascription: peck peck pickled peck of peppers
Recognition: the a peck pickled peck of peppers the


*****************************************
File: /g



*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 6.674664931371808 s  Speed of Backtrace: 0.0014950698241591454 s  Forward Count: 146985
(Substitutions, Deletions, Insertions) N: (11, 1, 4) 17
WER: 0.9411764705882353
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the where's the the a where's picked where's where's the picked of picked where's a a piper a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0305.wav 
Speed of Viterbi Decoder: 6.119443975389004 s  Speed of Backtrace: 0.0007916111499071121 s  Forward Count: 133469
(Substitutions, Deletions, Insertions) N: (8, 0, 6) 17
WER: 0.8235294117647058
Trascription: peter piper pickled a peck of picked peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper picked a a peck of the peck where's the a the 



*****************************************
File: /group/teaching/asr/labs/recordings/0324.wav 
Speed of Viterbi Decoder: 7.561784027144313 s  Speed of Backtrace: 0.0028480803593993187 s  Forward Count: 161768
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the the piper of picked the the pickled pickled peppers where's the peck of pickled peppers the the piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0325.wav 
Speed of Viterbi Decoder: 2.974259380251169 s  Speed of Backtrace: 0.000398857519030571 s  Forward Count: 67238
(Substitutions, Deletions, Insertions) N: (5, 0, 3) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the of of picked of peck of picked where's the


*****************************************
File: /group/teaching/asr/



*****************************************
File: /group/teaching/asr/labs/recordings/0344.wav 
Speed of Viterbi Decoder: 5.357418595813215 s  Speed of Backtrace: 0.0007021483033895493 s  Forward Count: 117581
(Substitutions, Deletions, Insertions) N: (6, 0, 7) 14
WER: 0.9285714285714286
Trascription: peter piper pickled a peck of pickled peppers the peck of pickled peppers picked
Recognition: the a of a of a the the peck of pickled peppers of picked of pickled the where's picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0345.wav 
Speed of Viterbi Decoder: 2.5839543230831623 s  Speed of Backtrace: 0.0003677438944578171 s  Forward Count: 56400
(Substitutions, Deletions, Insertions) N: (2, 2, 4) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the piper a of peck pickled where's a the


*****************************************
File: /group/teaching/asr/labs/recordings/0346.wav 
Speed of Viterbi

In [9]:
experiment_set_up('uni_w', 0.9, 0.1, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.105360515 -log(0.9)
Transist Weight: 2.30258512 -log(0.1)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 3.755227171815932 s  Speed of Backtrace: 0.0004953211173415184 s  Forward Count: 81192
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 8
WER: 1.125
Trascription: of of a peter the piper the pickled
Recognition: the a a of peter the a of peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.188380698673427 s  Speed of Backtrace: 0.0008726781234145164 s  Forward Count: 152647
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 10
WER: 0.5
Trascription: piper peck peppers peter peter picked pickled peck pet



*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 2.7616961700841784 s  Speed of Backtrace: 0.00039068330079317093 s  Forward Count: 62736
(Substitutions, Deletions, Insertions) N: (4, 0, 6) 8
WER: 1.25
Trascription: peter piper picked a peck of pickled peppers
Recognition: the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 4.886208903975785 s  Speed of Backtrace: 0.0006359517574310303 s  Forward Count: 109854
(Substitutions, Deletions, Insertions) N: (7, 3, 2) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the of of picked of peck picked peck peppers peck picked where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/



*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.37087017390877 s  Speed of Backtrace: 0.0009156744927167892 s  Forward Count: 51923
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 5
WER: 0.6
Trascription: pickled piper of the picked
Recognition: the of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterbi Decoder: 4.5019372422248125 s  Speed of Backtrace: 0.0005770819261670113 s  Forward Count: 94811
(Substitutions, Deletions, Insertions) N: (6, 2, 3) 17
WER: 0.6470588235294118
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked of picked peck of picked peppers where's peck of picked where's the piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0043.wav 
Speed of Viterbi Decoder: 3.2887



*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 2.963018896058202 s  Speed of Backtrace: 0.0004015956073999405 s  Forward Count: 64923
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 6
WER: 1.3333333333333333
Trascription: peter piper picked a pickled peter
Recognition: the of of of picked the of a the the


*****************************************
File: /group/teaching/asr/labs/recordings/0064.wav 
Speed of Viterbi Decoder: 3.803925600834191 s  Speed of Backtrace: 0.0004873964935541153 s  Forward Count: 83504
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 5
WER: 1.2
Trascription: piper peter picked pickled peppers
Recognition: the piper of a of a pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0065.wav 
Speed of Viterbi Decoder: 3.0032776603475213 s  Speed of Backtrace: 0.0003914814442396164 s  Forward Count: 64898
(Substitutions, Deletions, Ins



*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 2.0099612725898623 s  Speed of Backtrace: 0.0002839723601937294 s  Forward Count: 41325
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 7
WER: 0.42857142857142855
Trascription: the piper picked the peppers of peter
Recognition: the piper peck of peppers of peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 3.0935779279097915 s  Speed of Backtrace: 0.0004036780446767807 s  Forward Count: 65174
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 4
WER: 1.75
Trascription: peck pickled peck piper
Recognition: peter the peck the a peck a peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0086.wav 
Speed of Viterbi Decoder: 2.715519880875945 s  Speed of Backtrace: 0.0003856085240840912 s  Forward Count: 58238
(Substitutions, Deletions, Insertio

...



*****************************************
File: /group/teaching/asr/labs/recordings/0268.wav 
Speed of Viterbi Decoder: 3.1797420838847756 s  Speed of Backtrace: 0.0009244615212082863 s  Forward Count: 69886
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 7
WER: 1.1428571428571428
Trascription: peter picked a peck of pickled peppers
Recognition: the peter of picked of piper pickled pickled picked where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0269.wav 
Speed of Viterbi Decoder: 1.7507103001698852 s  Speed of Backtrace: 0.0002537183463573456 s  Forward Count: 39612
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 2
WER: 1.0
Trascription: pickled peppers
Recognition: the pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0270.wav 
Speed of Viterbi Decoder: 1.9671990694478154 s  Speed of Backtrace: 0.00027571525424718857 s  Forward Count: 45218
(Substitutions, Deletions, Inse



*****************************************
File: /group/teaching/asr/labs/recordings/0288.wav 
Speed of Viterbi Decoder: 7.735122762620449 s  Speed of Backtrace: 0.0023495331406593323 s  Forward Count: 111675
(Substitutions, Deletions, Insertions) N: (1, 2, 3) 8
WER: 0.75
Trascription: peter piper picked a peck of pickled peppers
Recognition: the of piper peck of pickled pickled peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0289.wav 
Speed of Viterbi Decoder: 4.926874361000955 s  Speed of Backtrace: 0.0005191266536712646 s  Forward Count: 87690
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's of peck of pickled peppers peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0290.wav 
Speed of Viterbi Decoder: 2.606296838261187 s  Speed of Backtrace: 0.000383810



*****************************************
File: /group/teaching/asr/labs/recordings/0308.wav 
Speed of Viterbi Decoder: 6.185073655098677 s  Speed of Backtrace: 0.0008159177377820015 s  Forward Count: 142635
(Substitutions, Deletions, Insertions) N: (5, 1, 8) 17
WER: 0.8235294117647058
Trascription: peter piper pickled a picked peck of peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper the of a of picked peck of where's of the a the peck of picked where's the a piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0309.wav 
Speed of Viterbi Decoder: 1.776699973270297 s  Speed of Backtrace: 0.0002541225403547287 s  Forward Count: 39493
(Substitutions, Deletions, Insertions) N: (0, 0, 1) 3
WER: 0.3333333333333333
Trascription: where's peter piper
Recognition: where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0310.wav 
Speed of Viterbi De



*****************************************
File: /group/teaching/asr/labs/recordings/0329.wav 
Speed of Viterbi Decoder: 7.6471364153549075 s  Speed of Backtrace: 0.0010369345545768738 s  Forward Count: 173777
(Substitutions, Deletions, Insertions) N: (3, 1, 5) 17
WER: 0.5294117647058824
Trascription: peppers peck picked the piper where's piper peppers picked peter a peck pickled of peter of pickled
Recognition: the peppers peck peck picked the piper where's the piper peter picked picked a picked the pickled of of pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0330.wav 
Speed of Viterbi Decoder: 3.305142712779343 s  Speed of Backtrace: 0.00047358032315969467 s  Forward Count: 74024
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 7
WER: 0.42857142857142855
Trascription: where's the peppers peter piper peck picked
Recognition: the where's the where's peter piper peck picked the


*****************************************
File: /grou



*****************************************
File: /group/teaching/asr/labs/recordings/0350.wav 
Speed of Viterbi Decoder: 3.760204242542386 s  Speed of Backtrace: 0.0004941169172525406 s  Forward Count: 85854
(Substitutions, Deletions, Insertions) N: (3, 0, 4) 8
WER: 0.875
Trascription: peter piper picked a peck of pickled peppers
Recognition: the a peter piper picked picked of peck a pickled where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0351.wav 
Speed of Viterbi Decoder: 3.910715769045055 s  Speed of Backtrace: 0.0005469508469104767 s  Forward Count: 89425
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 9
WER: 0.8888888888888888
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the a where's of peck of the picked of where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0352.wav 
Speed of Viterbi Decoder: 2.310781774111092 s  Speed of B

# Add silence baseline: selfloop & transist weight (0.9, 0.1) and (0.5, 0.5)

In [5]:
experiment_set_up('sil_b_w', 0.9, 0.1, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.105360515 -log(0.9)
Transist Weight: 2.30258512 -log(0.1)
Memory Cost: States Count: 132  Arcs Count:269


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 5.267812767997384 s  Speed of Backtrace: 0.0009861467406153679 s  Forward Count: 83373
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 8
WER: 0.875
Trascription: of of a peter the piper the pickled
Recognition: a a peter the a of peppers the the picked


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 7.604549575597048 s  Speed of Backtrace: 0.0009720595553517342 s  Forward Count: 156672
(Substitutions, Deletions, Insertions) N: (2, 0, 1) 10
WER: 0.3
Trascription: piper peck peppers peter peter picked pickled peck peter piper
Re



*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.153800771571696 s  Speed of Backtrace: 0.0003998810425400734 s  Forward Count: 63784
(Substitutions, Deletions, Insertions) N: (5, 0, 3) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: a of of of picked of peck of picked peck where's


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 5.467880453914404 s  Speed of Backtrace: 0.0006086835637688637 s  Forward Count: 113220
(Substitutions, Deletions, Insertions) N: (7, 3, 2) 17
WER: 0.7058823529411765
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the of of picked of peck picked where's peck the peck picked where's peter piper peck


*****************************************
File: /group/teaching/asr/labs/recordings/0023.wav 
Speed of 



*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.542766757309437 s  Speed of Backtrace: 0.0003199158236384392 s  Forward Count: 53121
(Substitutions, Deletions, Insertions) N: (1, 0, 1) 5
WER: 0.4
Trascription: pickled piper of the picked
Recognition: a of piper of the picked


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterbi Decoder: 4.504816731438041 s  Speed of Backtrace: 0.000530601479113102 s  Forward Count: 97436
(Substitutions, Deletions, Insertions) N: (7, 2, 1) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: a picked of picked peck of picked peppers where's peck of picked where's the piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0043.wav 
Speed of Viterbi Decoder: 4.269318290986121 s  Spee



*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 3.231953145004809 s  Speed of Backtrace: 0.0009637288749217987 s  Forward Count: 65490
(Substitutions, Deletions, Insertions) N: (5, 1, 0) 6
WER: 1.0
Trascription: peter piper picked a pickled peter
Recognition: of of of peck of


*****************************************
File: /group/teaching/asr/labs/recordings/0064.wav 
Speed of Viterbi Decoder: 4.18157571554184 s  Speed of Backtrace: 0.0004980051890015602 s  Forward Count: 84991
(Substitutions, Deletions, Insertions) N: (4, 0, 3) 5
WER: 1.4
Trascription: piper peter picked pickled peppers
Recognition: piper of a of a a of where's


*****************************************
File: /group/teaching/asr/labs/recordings/0065.wav 
Speed of Viterbi Decoder: 3.2196248350664973 s  Speed of Backtrace: 0.0003957226872444153 s  Forward Count: 65812
(Substitutions, Deletions, Insertions) N: (3, 0, 1) 6
WER: 0.6666666666666666



*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 3.2257855823263526 s  Speed of Backtrace: 0.00040521565824747086 s  Forward Count: 66333
(Substitutions, Deletions, Insertions) N: (2, 0, 2) 4
WER: 1.0
Trascription: peck pickled peck piper
Recognition: peck the a peck a peter


*****************************************
File: /group/teaching/asr/labs/recordings/0086.wav 
Speed of Viterbi Decoder: 2.765615942887962 s  Speed of Backtrace: 0.00034363754093647003 s  Forward Count: 59228
(Substitutions, Deletions, Insertions) N: (2, 0, 0) 5
WER: 0.4
Trascription: a of peppers piper peck
Recognition: piper of peppers peter peck


*****************************************
File: /group/teaching/asr/labs/recordings/0087.wav 
Speed of Viterbi Decoder: 1.7409876277670264 s  Speed of Backtrace: 0.00023994594812393188 s  Forward Count: 36929
(Substitutions, Deletions, Insertions) N: (0, 1, 0) 3
WER: 0.3333333333333333
Trascripti

...



*****************************************
File: /group/teaching/asr/labs/recordings/0253.wav 
Speed of Viterbi Decoder: 8.119467449374497 s  Speed of Backtrace: 0.0009689889848232269 s  Forward Count: 174438
(Substitutions, Deletions, Insertions) N: (8, 0, 1) 17
WER: 0.5294117647058824
Trascription: peter peppers picked a peck of peppers peppers where's the peck of peppers peppers peter piper picked
Recognition: the of peter the peck of picked peppers where's a peck of peck peter peppers peter peck picked


*****************************************
File: /group/teaching/asr/labs/recordings/0254.wav 
Speed of Viterbi Decoder: 10.562980906106532 s  Speed of Backtrace: 0.0022207554429769516 s  Forward Count: 223067
(Substitutions, Deletions, Insertions) N: (3, 6, 3) 17
WER: 0.7058823529411765
Trascription: peter peppers picked a peck of pickled peppers where's the peck of pickled peppers peter peppers picked
Recognition: peter piper picked picked peppers where's pickled picked peppers p



*****************************************
File: /group/teaching/asr/labs/recordings/0273.wav 
Speed of Viterbi Decoder: 3.1436039553955197 s  Speed of Backtrace: 0.00038218218833208084 s  Forward Count: 66446
(Substitutions, Deletions, Insertions) N: (0, 1, 0) 8
WER: 0.125
Trascription: peter piper picked a peck of pickled peppers
Recognition: peter piper picked peck of pickled peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0274.wav 
Speed of Viterbi Decoder: 2.8960040528327227 s  Speed of Backtrace: 0.0003581913188099861 s  Forward Count: 59904
(Substitutions, Deletions, Insertions) N: (1, 0, 0) 5
WER: 0.2
Trascription: pickled peppers where's the peck
Recognition: picked peppers where's the peck


*****************************************
File: /group/teaching/asr/labs/recordings/0275.wav 
Speed of Viterbi Decoder: 2.860172371380031 s  Speed of Backtrace: 0.0003738775849342346 s  Forward Count: 60147
(Substitutions, Deletions, Insertio



*****************************************
File: /group/teaching/asr/labs/recordings/0293.wav 
Speed of Viterbi Decoder: 11.801686523482203 s  Speed of Backtrace: 0.0014295391738414764 s  Forward Count: 242459
(Substitutions, Deletions, Insertions) N: (6, 0, 4) 17
WER: 0.5882352941176471
Trascription: a peck peppers where's picked peter of pickled of peppers peck the piper picked peter piper pickled
Recognition: of a peter a where's where's picked a peppers pickled of peppers a the peter picked peter of piper of pickled


*****************************************
File: /group/teaching/asr/labs/recordings/0294.wav 
Speed of Viterbi Decoder: 1.7779479157179594 s  Speed of Backtrace: 0.00023868493735790253 s  Forward Count: 38296
(Substitutions, Deletions, Insertions) N: (1, 1, 0) 5
WER: 0.4
Trascription: peter piper picked a peck
Recognition: peter picked picked peck


*****************************************
File: /group/teaching/asr/labs/recordings/0295.wav 
Speed of Viterbi Decoder:



*****************************************
File: /group/teaching/asr/labs/recordings/0314.wav 
Speed of Viterbi Decoder: 2.4497525189071894 s  Speed of Backtrace: 0.0003250986337661743 s  Forward Count: 53169
(Substitutions, Deletions, Insertions) N: (0, 0, 0) 5
WER: 0.0
Trascription: peter piper picked pickled peppers
Recognition: peter piper picked pickled peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0315.wav 
Speed of Viterbi Decoder: 3.453142585232854 s  Speed of Backtrace: 0.00041322968900203705 s  Forward Count: 74419
(Substitutions, Deletions, Insertions) N: (3, 1, 1) 8
WER: 0.625
Trascription: peter piper picked a peck of pickled peppers
Recognition: the the piper picked the piper pickled peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0316.wav 
Speed of Viterbi Decoder: 2.749430799856782 s  Speed of Backtrace: 0.00034759845584630966 s  Forward Count: 57376
(Substitutions, Deletions,



*****************************************
File: /group/teaching/asr/labs/recordings/0334.wav 
Speed of Viterbi Decoder: 3.823783151805401 s  Speed of Backtrace: 0.0012662354856729507 s  Forward Count: 79547
(Substitutions, Deletions, Insertions) N: (3, 0, 0) 7
WER: 0.42857142857142855
Trascription: picked peter peck pickled the piper peter
Recognition: picked of a pickled the piper picked


*****************************************
File: /group/teaching/asr/labs/recordings/0335.wav 
Speed of Viterbi Decoder: 4.9177546463906765 s  Speed of Backtrace: 0.0005861315876245499 s  Forward Count: 102625
(Substitutions, Deletions, Insertions) N: (2, 1, 1) 8
WER: 0.5
Trascription: peter piper picked a peck of pickled peppers
Recognition: the a piper pickled a of pickled peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0336.wav 
Speed of Viterbi Decoder: 3.9874705793336034 s  Speed of Backtrace: 0.000458291731774807 s  Forward Count: 82897
(Substitut

In [6]:
experiment_set_up('sil_b_w', 0.5, 0.5, 0.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 132  Arcs Count:269


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 7.140387162566185 s  Speed of Backtrace: 0.001826118677854538 s  Forward Count: 82444
(Substitutions, Deletions, Insertions) N: (2, 1, 5) 8
WER: 1.0
Trascription: of of a peter the piper the pickled
Recognition: a a peter the a of picked a peppers the the pickled


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 12.649979866109788 s  Speed of Backtrace: 0.0016451207920908928 s  Forward Count: 155189
(Substitutions, Deletions, Insertions) N: (2, 0, 2) 10
WER: 0.4
Trascription: piper peck peppers peter peter picked pickled peck peter



*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 5.635297558270395 s  Speed of Backtrace: 0.0005747685208916664 s  Forward Count: 62777
(Substitutions, Deletions, Insertions) N: (5, 0, 3) 8
WER: 1.0
Trascription: peter piper picked a peck of pickled peppers
Recognition: a of of of picked of peck of picked peck where's


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 10.735631555318832 s  Speed of Backtrace: 0.001831095665693283 s  Forward Count: 111183
(Substitutions, Deletions, Insertions) N: (9, 1, 3) 17
WER: 0.7647058823529411
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the of of of picked of peck picked peck picked peppers the peck peck picked where's peter piper peck


*****************************************
File: /group/teaching/asr/labs/recordings/0023



*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 5.5519490372389555 s  Speed of Backtrace: 0.0004792148247361183 s  Forward Count: 52577
(Substitutions, Deletions, Insertions) N: (1, 0, 1) 5
WER: 0.4
Trascription: pickled piper of the picked
Recognition: a of piper of the picked


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Speed of Viterbi Decoder: 7.398675610311329 s  Speed of Backtrace: 0.002023654989898205 s  Forward Count: 95326
(Substitutions, Deletions, Insertions) N: (5, 2, 2) 17
WER: 0.5294117647058824
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: a picked of picked peck of pickled peppers where's peck of pickled where's the piper of peck


*****************************************
File: /group/teaching/asr/labs/recordings/0043.wav 
Speed of Viterbi Decoder: 5.283995248377323 



*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 5.203938930295408 s  Speed of Backtrace: 0.0007071346044540405 s  Forward Count: 64858
(Substitutions, Deletions, Insertions) N: (3, 2, 1) 6
WER: 1.0
Trascription: peter piper picked a pickled peter
Recognition: of of of picked of


*****************************************
File: /group/teaching/asr/labs/recordings/0064.wav 
Speed of Viterbi Decoder: 7.019997418858111 s  Speed of Backtrace: 0.0007043378427624702 s  Forward Count: 84228
(Substitutions, Deletions, Insertions) N: (3, 0, 3) 5
WER: 1.2
Trascription: piper peter picked pickled peppers
Recognition: piper of a of a a of peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0065.wav 
Speed of Viterbi Decoder: 5.056862228550017 s  Speed of Backtrace: 0.0005556121468544006 s  Forward Count: 65134
(Substitutions, Deletions, Insertions) N: (4, 0, 1) 6
WER: 0.83333333333333



*****************************************
File: /group/teaching/asr/labs/recordings/0085.wav 
Speed of Viterbi Decoder: 5.866564557887614 s  Speed of Backtrace: 0.0005396753549575806 s  Forward Count: 65358
(Substitutions, Deletions, Insertions) N: (1, 0, 1) 4
WER: 0.5
Trascription: peck pickled peck piper
Recognition: peck pickled peck a peter


*****************************************
File: /group/teaching/asr/labs/recordings/0086.wav 
Speed of Viterbi Decoder: 5.138914367184043 s  Speed of Backtrace: 0.0005464069545269012 s  Forward Count: 58265
(Substitutions, Deletions, Insertions) N: (4, 0, 2) 5
WER: 1.2
Trascription: a of peppers piper peck
Recognition: piper pickled peck where's picked picked peck


*****************************************
File: /group/teaching/asr/labs/recordings/0087.wav 
Speed of Viterbi Decoder: 3.1146521447226405 s  Speed of Backtrace: 0.0003291033208370209 s  Forward Count: 36483
(Substitutions, Deletions, Insertions) N: (1, 0, 1) 3
WER: 0.66666666666

...



*****************************************
File: /group/teaching/asr/labs/recordings/0271.wav 
Speed of Viterbi Decoder: 3.990833478048444 s  Speed of Backtrace: 0.00044404249638319016 s  Forward Count: 51990
(Substitutions, Deletions, Insertions) N: (0, 2, 1) 6
WER: 0.5
Trascription: where's the peck of pickled peppers
Recognition: where's of where's pickled peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0272.wav 
Speed of Viterbi Decoder: 5.199193685315549 s  Speed of Backtrace: 0.0005562379956245422 s  Forward Count: 64605
(Substitutions, Deletions, Insertions) N: (1, 2, 2) 8
WER: 0.625
Trascription: peter piper picked a peck of pickled peppers
Recognition: peter of piper pickled of piper pickled peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0273.wav 
Speed of Viterbi Decoder: 5.835848486050963 s  Speed of Backtrace: 0.0005434071645140648 s  Forward Count: 65662
(Substitutions, Deletions,



*****************************************
File: /group/teaching/asr/labs/recordings/0291.wav 
Speed of Viterbi Decoder: 6.314647235907614 s  Speed of Backtrace: 0.0006420491263270378 s  Forward Count: 76606
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 8
WER: 0.25
Trascription: the peck of pickled peppers of peter piper
Recognition: the of peck of pickled peppers of peter of piper


*****************************************
File: /group/teaching/asr/labs/recordings/0292.wav 
Speed of Viterbi Decoder: 3.9612188106402755 s  Speed of Backtrace: 0.0009656483307480812 s  Forward Count: 44553
(Substitutions, Deletions, Insertions) N: (0, 0, 1) 3
WER: 0.3333333333333333
Trascription: where's peter piper
Recognition: where's peter of piper


*****************************************
File: /group/teaching/asr/labs/recordings/0293.wav 
Speed of Viterbi Decoder: 19.024415253661573 s  Speed of Backtrace: 0.0018660593777894974 s  Forward Count: 238786
(Substitutions, Deletions, Insertions) 



*****************************************
File: /group/teaching/asr/labs/recordings/0311.wav 
Speed of Viterbi Decoder: 3.7007333235815167 s  Speed of Backtrace: 0.0005642622709274292 s  Forward Count: 47147
(Substitutions, Deletions, Insertions) N: (0, 0, 0) 5
WER: 0.0
Trascription: of pickled peppers peter piper
Recognition: of pickled peppers peter piper


*****************************************
File: /group/teaching/asr/labs/recordings/0312.wav 
Speed of Viterbi Decoder: 2.1766000064089894 s  Speed of Backtrace: 0.0002795569598674774 s  Forward Count: 29049
(Substitutions, Deletions, Insertions) N: (0, 0, 0) 5
WER: 0.0
Trascription: the pickled peck of peter
Recognition: the pickled peck of peter


*****************************************
File: /group/teaching/asr/labs/recordings/0313.wav 
Speed of Viterbi Decoder: 3.0349939819425344 s  Speed of Backtrace: 0.00024367216974496841 s  Forward Count: 38998
(Substitutions, Deletions, Insertions) N: (0, 0, 0) 6
WER: 0.0
Trascription



*****************************************
File: /group/teaching/asr/labs/recordings/0332.wav 
Speed of Viterbi Decoder: 8.097079223021865 s  Speed of Backtrace: 0.0007449211552739143 s  Forward Count: 90434
(Substitutions, Deletions, Insertions) N: (3, 0, 0) 12
WER: 0.25
Trascription: where's piper of a peter pickled picked of piper peter the pickled
Recognition: where's piper of picked of pickled picked of piper picked the pickled


*****************************************
File: /group/teaching/asr/labs/recordings/0333.wav 
Speed of Viterbi Decoder: 6.85939409583807 s  Speed of Backtrace: 0.0021429425105452538 s  Forward Count: 85427
(Substitutions, Deletions, Insertions) N: (1, 1, 0) 11
WER: 0.18181818181818182
Trascription: of piper of a peck picked piper peter picked pickled peter
Recognition: of piper of peck picked piper picked picked pickled peter


*****************************************
File: /group/teaching/asr/labs/recordings/0334.wav 
Speed of Viterbi Decoder: 6.482733



*****************************************
File: /group/teaching/asr/labs/recordings/0353.wav 
Speed of Viterbi Decoder: 4.81011248473078 s  Speed of Backtrace: 0.0005749687552452087 s  Forward Count: 66749
(Substitutions, Deletions, Insertions) N: (1, 1, 3) 7
WER: 0.7142857142857143
Trascription: where's peter piper peck of pickled peppers
Recognition: where's peter of piper where's peck pickled of where's


*****************************************
File: /group/teaching/asr/labs/recordings/0354.wav 
Speed of Viterbi Decoder: 6.151677425019443 s  Speed of Backtrace: 0.000704561360180378 s  Forward Count: 84279
(Substitutions, Deletions, Insertions) N: (2, 1, 0) 8
WER: 0.375
Trascription: peter piper pickled a peck of picked peppers
Recognition: peter piper pickled of peck a peppers
Average
Total Errors: 1357
Total Transcription Words: 2846
Total WER: 0.4768095572733661
The number of forward computations per wav:  78235.62253521127
Average decode time: 6.247740471882509
Average backtr

# Add pruning baseline: pruning threshold 3000, 6000, 10000, 20000, 30000

In [9]:
experiment_set_up('pru_b_w', 0.5, 0.5, 3000.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 127  Arcs Count:252
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 5.138022564351559 s  Speed of Backtrace: 0.0012525832280516624 s  Forward Count: 68201
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a of a of peter the a of picked a peppers the the picked where's
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 2.572869093157351 s  Speed of Backtrace: 0.0012143412604928017 s  Forward Count: 30830
(Substitutions, Deletions, I

No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0019.wav 
Speed of Viterbi Decoder: 3.980230347253382 s  Speed of Backtrace: 0.0009468477219343185 s  Forward Count: 49508
(Substitutions, Deletions, Insertions) N: (2, 3, 2) 8
WER: 0.875
Trascription: the peck of pickled peppers peter piper picked
Recognition: peck the picked picked of pickled where's


*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.8443729532882571 s  Speed of Backtrace: 0.00028388481587171555 s  Forward Count: 25342
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 4.5132543267682195 s  Speed of B

No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0038.wav 
Speed of Viterbi Decoder: 6.017059773206711 s  Speed of Backtrace: 0.0009397575631737709 s  Forward Count: 81069
(Substitutions, Deletions, Insertions) N: (7, 3, 4) 17
WER: 0.8235294117647058
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper of a picked peck of the peck of where's where's picked peck of the where's
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0039.wav 
Speed of Viterbi Decoder: 6.011009061709046 s  Speed of Backtrace: 0.0010289857164025307 s  Forward Count: 84743
(Substitutions, Deletions, Insertions) N: (11, 2, 2) 17
WER: 0.8823529411764706
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Re

No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0057.wav 
Speed of Viterbi Decoder: 6.5824948363006115 s  Speed of Backtrace: 0.0008625360205769539 s  Forward Count: 85784
(Substitutions, Deletions, Insertions) N: (1, 1, 3) 13
WER: 0.38461538461538464
Trascription: where's peter pickled peck of pickled peppers the peck piper picked a peppers
Recognition: the where's peter pickled peck of pickled peppers the peck picked picked peppers the where's
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0058.wav 
Speed of Viterbi Decoder: 4.666398747824132 s  Speed of Backtrace: 0.0007094684988260269 s  Forward Count: 64155
(Substitutions, Deletions, Insertions) N: (1, 1, 4) 10
WER: 0.6
Trascription: a peck of peter pickled the peppers peck of pickled
Recognition: the of peck of peter of pickled peppers peck of pickled the where's
No p



*****************************************
File: /group/teaching/asr/labs/recordings/0077.wav 
Speed of Viterbi Decoder: 3.086977190338075 s  Speed of Backtrace: 0.0004264144226908684 s  Forward Count: 42425
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 6
WER: 0.5
Trascription: the pickled peppers picked peter piper
Recognition: the pickled peck where's picked peter piper pickled


*****************************************
File: /group/teaching/asr/labs/recordings/0078.wav 
Speed of Viterbi Decoder: 5.002667077817023 s  Speed of Backtrace: 0.0007024668157100677 s  Forward Count: 64302
(Substitutions, Deletions, Insertions) N: (0, 0, 3) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled peppers peter piper a picked the
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0079.wav 
Speed of Viterbi Decoder: 6.32756372

...



*****************************************
File: /group/teaching/asr/labs/recordings/0270.wav 
Speed of Viterbi Decoder: 3.345153111964464 s  Speed of Backtrace: 0.00041701458394527435 s  Forward Count: 44525
(Substitutions, Deletions, Insertions) N: (0, 0, 4) 4
WER: 1.0
Trascription: peter piper picked peppers
Recognition: the peter of piper of picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0271.wav 
Speed of Viterbi Decoder: 3.877701082266867 s  Speed of Backtrace: 0.0004516514018177986 s  Forward Count: 50624
(Substitutions, Deletions, Insertions) N: (1, 1, 2) 6
WER: 0.6666666666666666
Trascription: where's the peck of pickled peppers
Recognition: the where's of piper pickled pickled peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0272.wav 
Speed of Viterbi Decoder: 4.713766966946423 s  Speed of Backtrace: 0.0005516372621059418 s  Forward Count: 62870
(Substitutions, Deletions, I

No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0289.wav 
Speed of Viterbi Decoder: 6.0323467422276735 s  Speed of Backtrace: 0.0009632492437958717 s  Forward Count: 79857
(Substitutions, Deletions, Insertions) N: (1, 0, 2) 9
WER: 0.3333333333333333
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's picked peck of pickled peppers peter piper picked where's
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0290.wav 
Speed of Viterbi Decoder: 3.9740234930068254 s  Speed of Backtrace: 0.0005053356289863586 s  Forward Count: 53673
(Substitutions, Deletions, Insertions) N: (2, 0, 2) 4
WER: 1.0
Trascription: peter picked pickled peppers
Recognition: the of peck pickled peppers where's
No path got to the end of the observations.


*****************************************
File: /group/teachi

No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0308.wav 
Speed of Viterbi Decoder: 4.039451344870031 s  Speed of Backtrace: 0.0010808790102601051 s  Forward Count: 51280
(Substitutions, Deletions, Insertions) N: (4, 9, 1) 17
WER: 0.8235294117647058
Trascription: peter piper pickled a picked peck of peppers where's the peck of pickled peppers peter piper picked
Recognition: the picked piper the of a of picked where's


*****************************************
File: /group/teaching/asr/labs/recordings/0309.wav 
Speed of Viterbi Decoder: 2.8525815373286605 s  Speed of Backtrace: 0.00038139987736940384 s  Forward Count: 39132
(Substitutions, Deletions, Insertions) N: (0, 0, 3) 3
WER: 1.0
Trascription: where's peter piper
Recognition: the where's peter piper of the


*****************************************
File: /group/teaching/asr/labs/recordings/0310.wav 
Speed of Viterbi Decoder: 2.2961293617263436 s  S

No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0328.wav 
Speed of Viterbi Decoder: 4.641182577237487 s  Speed of Backtrace: 0.0006447257474064827 s  Forward Count: 57326
(Substitutions, Deletions, Insertions) N: (1, 0, 8) 6
WER: 1.5
Trascription: where's the peppers peter piper picked
Recognition: the where's the of peck of peter of picked of piper of picked where's
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0329.wav 
Speed of Viterbi Decoder: 3.290143839083612 s  Speed of Backtrace: 0.0009429296478629112 s  Forward Count: 40860
(Substitutions, Deletions, Insertions) N: (1, 13, 0) 17
WER: 0.8235294117647058
Trascription: peppers peck picked the piper where's piper peppers picked peter a peck pickled of peter of pickled
Recognition: the peppers peck where's
No path got to the end of the observations.


*****************



*****************************************
File: /group/teaching/asr/labs/recordings/0347.wav 
Speed of Viterbi Decoder: 2.956106660887599 s  Speed of Backtrace: 0.00027783866971731186 s  Forward Count: 40498
(Substitutions, Deletions, Insertions) N: (3, 0, 3) 8
WER: 0.75
Trascription: peter piper picked a peck of pickled peppers
Recognition: piper a piper of picked of peck of pickled of where's


*****************************************
File: /group/teaching/asr/labs/recordings/0348.wav 
Speed of Viterbi Decoder: 3.760262433439493 s  Speed of Backtrace: 0.000508524477481842 s  Forward Count: 51561
(Substitutions, Deletions, Insertions) N: (4, 0, 4) 8
WER: 1.0
Trascription: a peck of pickled peppers peter piper picked
Recognition: the peck a pickled of where's of of piper a picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0349.wav 
Speed of Viterbi Decoder: 3.762214817106724 s  Speed of Backtrace: 0.00047578755766153336 s  Forward Count

In [10]:
experiment_set_up('pru_b_w', 0.5, 0.5, 6000.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 4.289769165217876 s  Speed of Backtrace: 0.0005148937925696373 s  Forward Count: 80212
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a of a of peter the a of picked a peppers the the picked the
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 4.586818906478584 s  Speed of Backtrace: 0.0008985130116343498 s  Forward Count: 85450
(Substitutions, Deletions, Insertions) N: (8, 2, 0) 10
WER: 1.0
Trascription



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.2716408725827932 s  Speed of Backtrace: 0.00021174084395170212 s  Forward Count: 25342
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.1047055684030056 s  Speed of Backtrace: 0.0004114937037229538 s  Forward Count: 61467
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 5.283226154744625 s  Speed of Backtrace: 0.0006548333913087845 s  Forward Count: 107839
(Substi



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 5.510676346719265 s  Speed of Backtrace: 0.0006276173517107964 s  Forward Count: 103946
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.736771318130195 s  Speed of Backtrace: 0.00035536475479602814 s  Forward Count: 51282
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Spe



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.7910621985793114 s  Speed of Backtrace: 0.000264875590801239 s  Forward Count: 36693
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.5921836104243994 s  Speed of Backtrace: 0.00034768227487802505 s  Forward Count: 51959
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 3
WER: 2.6666666666666665
Trascription: peck peppers peter
Recognition: the pickled of of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 3.146620564162731 s  Speed of Backtrace: 0.00043665338307619095 s  Forward Count: 63724
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter piper p



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.225736876949668 s  Speed of Backtrace: 0.0002911454066634178 s  Forward Count: 46976
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.3435108568519354 s  Speed of Backtrace: 0.00019733794033527374 s  Forward Count: 28689
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 1.9510170882567763 s  Speed of Backtrace: 0.00027807895094156265 s  Forward Count: 40652
(Substitutions, Deleti

...



*****************************************
File: /group/teaching/asr/labs/recordings/0262.wav 
Speed of Viterbi Decoder: 2.545130969956517 s  Speed of Backtrace: 0.00031245406717061996 s  Forward Count: 48640
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 8
WER: 0.25
Trascription: where's the piper of peppers pickled peter peck
Recognition: the where's the piper of peppers pickled peter peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 3.2410717867314816 s  Speed of Backtrace: 0.0003935340791940689 s  Forward Count: 60495
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.821239847689867 s  Speed of Backtrace: 0.00046846363693475723 s  Forward Count: 71296




*****************************************
File: /group/teaching/asr/labs/recordings/0282.wav 
Speed of Viterbi Decoder: 4.996426243335009 s  Speed of Backtrace: 0.0008311290293931961 s  Forward Count: 94386
(Substitutions, Deletions, Insertions) N: (2, 0, 3) 11
WER: 0.45454545454545453
Trascription: a peck of pickled peppers where's the peck of pickled peppers
Recognition: peck the of peck of pickled peppers where's the peck where's pickled peppers the
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 5.372932901605964 s  Speed of Backtrace: 0.0006370879709720612 s  Forward Count: 98519
(Substitutions, Deletions, Insertions) N: (3, 1, 4) 9
WER: 0.8888888888888888
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the where's
No path got to the end of the observations.


*********************



*****************************************
File: /group/teaching/asr/labs/recordings/0301.wav 
Speed of Viterbi Decoder: 4.182363793253899 s  Speed of Backtrace: 0.0005050515756011009 s  Forward Count: 78156
(Substitutions, Deletions, Insertions) N: (0, 0, 5) 7
WER: 0.7142857142857143
Trascription: of pickled peppers picked peter piper peck
Recognition: the where's the of pickled peppers picked peter of piper peck the


*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.977347733452916 s  Speed of Backtrace: 0.00036775320768356323 s  Forward Count: 55172
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 2.3302869061008096 s  Speed of Backtrace: 0.00029934942722320557 s  



*****************************************
File: /group/teaching/asr/labs/recordings/0320.wav 
Speed of Viterbi Decoder: 3.473364168778062 s  Speed of Backtrace: 0.00042225513607263565 s  Forward Count: 67977
(Substitutions, Deletions, Insertions) N: (0, 3, 3) 8
WER: 0.75
Trascription: peter piper picked a peck of pickled peppers
Recognition: the peter piper of picked pickled picked peppers


*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 3.3564488627016544 s  Speed of Backtrace: 0.0003939066082239151 s  Forward Count: 64578
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.742272180505097 s  Speed of Backtrace: 0.0010088831186294556 s  Forward Count: 7211



*****************************************
File: /group/teaching/asr/labs/recordings/0340.wav 
Speed of Viterbi Decoder: 3.7005129605531693 s  Speed of Backtrace: 0.000455731526017189 s  Forward Count: 68332
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 5
WER: 1.4
Trascription: peter piper picked a peck
Recognition: the of peter picked piper the picked the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 3.1206133915111423 s  Speed of Backtrace: 0.00038377847522497177 s  Forward Count: 57639
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 2.043551942333579 s  Speed of Backtrace: 0.0002780156210064888 s  Forward Count: 39309
(Substitutions, Deletions, Insertions) N:

In [11]:
experiment_set_up('pru_b_w', 0.5, 0.5, 10000.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 4.278954142704606 s  Speed of Backtrace: 0.0005391761660575867 s  Forward Count: 80212
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a of a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 8.129388832487166 s  Speed of Backtrace: 0.0008858870714902878 s  Forward Count: 151127
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pic



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.3572850972414017 s  Speed of Backtrace: 0.00022814422845840454 s  Forward Count: 25342
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.1228978540748358 s  Speed of Backtrace: 0.00042490847408771515 s  Forward Count: 61467
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 5.417154094204307 s  Speed of Backtrace: 0.000689944252371788 s  Forward Count: 107839
(Substi



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 5.488355794921517 s  Speed of Backtrace: 0.0006363140419125557 s  Forward Count: 103946
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.7667020689696074 s  Speed of Backtrace: 0.00033011939376592636 s  Forward Count: 51282
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Sp



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.9413809766992927 s  Speed of Backtrace: 0.0002573961392045021 s  Forward Count: 36693
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.6837299410253763 s  Speed of Backtrace: 0.00034090690314769745 s  Forward Count: 51959
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 3
WER: 2.6666666666666665
Trascription: peck peppers peter
Recognition: the pickled of of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 3.314536554738879 s  Speed of Backtrace: 0.00041812099516391754 s  Forward Count: 63724
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter piper 



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.545991772785783 s  Speed of Backtrace: 0.00030633434653282166 s  Forward Count: 46976
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.2820769436657429 s  Speed of Backtrace: 0.0005949717015028 s  Forward Count: 28689
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 2.0461019575595856 s  Speed of Backtrace: 0.0002856021746993065 s  Forward Count: 40652
(Substitutions, Deletions,

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 3.167378752492368 s  Speed of Backtrace: 0.0004033530130982399 s  Forward Count: 60495
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.596067199483514 s  Speed of Backtrace: 0.0004720240831375122 s  Forward Count: 71296
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.8315766490995884 s  Speed of Backtrace: 0.0003937352448701



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 5.123263447545469 s  Speed of Backtrace: 0.0006546620279550552 s  Forward Count: 105715
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the
No path got to the end of the observations.


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 9.619886714033782 s  Speed of Backtrace: 0.0023510735481977463 s  Forward Count: 187574
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 19
WER: 0.3684210526315789
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper pi



*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.821314310654998 s  Speed of Backtrace: 0.0003555417060852051 s  Forward Count: 55172
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 2.280097523704171 s  Speed of Backtrace: 0.0003042779862880707 s  Forward Count: 43085
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 7.580479426309466 s  Speed of Backtrace: 0.0008865352720022202 s  Forward Count: 145301
(Substitutions,



*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 3.520332073792815 s  Speed of Backtrace: 0.0004306389018893242 s  Forward Count: 64578
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.8121603252366185 s  Speed of Backtrace: 0.000649038702249527 s  Forward Count: 72117
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 7
WER: 1.2857142857142858
Trascription: where's the pickled peppers peter piper picked
Recognition: the where's where's where's of of where's peck of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 2.2448010556399822 s  Speed of Backtrace: 0.000297685



*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 2.9722946379333735 s  Speed of Backtrace: 0.0003810487687587738 s  Forward Count: 57639
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 1.998650656081736 s  Speed of Backtrace: 0.0002762060612440109 s  Forward Count: 39309
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 4
WER: 2.0
Trascription: peter peter peter peter
Recognition: the the the the peter the peck picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.84358814265579 s  Speed of Backtrace: 0.00045265350490808487 s  Forward Count: 70961
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4


In [12]:
experiment_set_up('pru_b_w', 0.5, 0.5, 20000.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 4.128780470229685 s  Speed of Backtrace: 0.0011962680146098137 s  Forward Count: 80212
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a of a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 8.173031149432063 s  Speed of Backtrace: 0.0014557521790266037 s  Forward Count: 151127
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pic



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.21371840685606 s  Speed of Backtrace: 0.00019838660955429077 s  Forward Count: 25342
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.021032893098891 s  Speed of Backtrace: 0.0005734730511903763 s  Forward Count: 61467
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 5.2762016374617815 s  Speed of Backtrace: 0.0009583542123436928 s  Forward Count: 107839
(Substitu



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 5.068367995321751 s  Speed of Backtrace: 0.0006398698315024376 s  Forward Count: 103946
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.627979136072099 s  Speed of Backtrace: 0.0011119823902845383 s  Forward Count: 51282
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Spee



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 1.8892367584630847 s  Speed of Backtrace: 0.0002657705917954445 s  Forward Count: 36693
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.6992971654981375 s  Speed of Backtrace: 0.00033017341047525406 s  Forward Count: 51959
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 3
WER: 2.6666666666666665
Trascription: peck peppers peter
Recognition: the pickled of of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 3.3167460272088647 s  Speed of Backtrace: 0.0006159208714962006 s  Forward Count: 63724
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter piper 



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.568991974927485 s  Speed of Backtrace: 0.0004313793033361435 s  Forward Count: 46976
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.4743942841887474 s  Speed of Backtrace: 0.0002275640144944191 s  Forward Count: 28689
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 2.135140670463443 s  Speed of Backtrace: 0.00027904845774173737 s  Forward Count: 40652
(Substitutions, Deletion

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 3.1782240606844425 s  Speed of Backtrace: 0.00038138870149850845 s  Forward Count: 60495
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 3.652716500684619 s  Speed of Backtrace: 0.000447162427008152 s  Forward Count: 71296
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 2.7932436745613813 s  Speed of Backtrace: 0.000541687011718



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 5.575363038107753 s  Speed of Backtrace: 0.0006592003628611565 s  Forward Count: 105715
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 9.794363367371261 s  Speed of Backtrace: 0.001143115572631359 s  Forward Count: 188341
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the






*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.7870780183002353 s  Speed of Backtrace: 0.00038843322545289993 s  Forward Count: 55172
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 2.2118125250563025 s  Speed of Backtrace: 0.00029177218675613403 s  Forward Count: 43085
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 7.514057355932891 s  Speed of Backtrace: 0.0011666081845760345 s  Forward Count: 145301
(Substituti



*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 3.2144544422626495 s  Speed of Backtrace: 0.00042010843753814697 s  Forward Count: 64578
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 3.6749952090904117 s  Speed of Backtrace: 0.0004537254571914673 s  Forward Count: 72117
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 7
WER: 1.2857142857142858
Trascription: where's the pickled peppers peter piper picked
Recognition: the where's where's where's of of where's peck of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 2.213814064860344 s  Speed of Backtrace: 0.0003103



*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 3.4619786432012916 s  Speed of Backtrace: 0.0006923526525497437 s  Forward Count: 57639
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 2.3022708408534527 s  Speed of Backtrace: 0.00037686247378587723 s  Forward Count: 39309
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 4
WER: 2.0
Trascription: peter peter peter peter
Recognition: the the the the peter the peck picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 3.6311708614230156 s  Speed of Backtrace: 0.0005726795643568039 s  Forward Count: 70961
(Substitutions, Deletions, Insertions) N: (2, 0, 6)

In [14]:
experiment_set_up('pru_b_w', 0.5, 0.5, 30000.0)

Mode: Baseline Recognition, WFST set only word label output on its arc path
Phone per state: 3
Start Weight: -log(1.0)
End Weight: initial(0.0)
Selfloop Weight: 0.693147182 -log(0.5)
Transist Weight: 0.693147182 -log(0.5)
Memory Cost: States Count: 127  Arcs Count:252


*****************************************
File: /group/teaching/asr/labs/recordings/0000.wav 
Speed of Viterbi Decoder: 5.391091619618237 s  Speed of Backtrace: 0.0007341774180531502 s  Forward Count: 80212
(Substitutions, Deletions, Insertions) N: (3, 0, 8) 8
WER: 1.375
Trascription: of of a peter the piper the pickled
Recognition: the a of a of peter the a of picked a peppers the the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0001.wav 
Speed of Viterbi Decoder: 10.423150723800063 s  Speed of Backtrace: 0.0009013460949063301 s  Forward Count: 151127
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 10
WER: 0.8
Trascription: piper peck peppers peter peter picked pi



*****************************************
File: /group/teaching/asr/labs/recordings/0020.wav 
Speed of Viterbi Decoder: 1.4538215575739741 s  Speed of Backtrace: 0.00019213370978832245 s  Forward Count: 25342
(Substitutions, Deletions, Insertions) N: (2, 0, 5) 3
WER: 2.3333333333333335
Trascription: peter piper picked
Recognition: the peter of of of a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0021.wav 
Speed of Viterbi Decoder: 3.4187190337106586 s  Speed of Backtrace: 0.00040461309254169464 s  Forward Count: 61467
(Substitutions, Deletions, Insertions) N: (4, 0, 7) 8
WER: 1.375
Trascription: peter piper picked a peck of pickled peppers
Recognition: peck the piper a of of of picked of peck of picked peck where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0022.wav 
Speed of Viterbi Decoder: 5.44652808830142 s  Speed of Backtrace: 0.000669148750603199 s  Forward Count: 107839
(Substit



*****************************************
File: /group/teaching/asr/labs/recordings/0040.wav 
Speed of Viterbi Decoder: 5.409244908951223 s  Speed of Backtrace: 0.0006437720730900764 s  Forward Count: 103946
(Substitutions, Deletions, Insertions) N: (5, 0, 5) 17
WER: 0.5882352941176471
Trascription: peter piper picked a peck of pickled peppers where's the peck of pickled peppers peter piper picked
Recognition: peck the picked piper of picked peck of pickled peppers where's the a of pickled the where's peter piper of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0041.wav 
Speed of Viterbi Decoder: 2.7662166291847825 s  Speed of Backtrace: 0.0003417832776904106 s  Forward Count: 51282
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 5
WER: 0.8
Trascription: pickled piper of the picked
Recognition: the picked of piper of the picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0042.wav 
Spe



*****************************************
File: /group/teaching/asr/labs/recordings/0061.wav 
Speed of Viterbi Decoder: 2.010025623254478 s  Speed of Backtrace: 0.00025415513664484024 s  Forward Count: 36693
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 2
WER: 2.0
Trascription: piper picked
Recognition: the of of picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0062.wav 
Speed of Viterbi Decoder: 2.820645075291395 s  Speed of Backtrace: 0.0003440454602241516 s  Forward Count: 51959
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 3
WER: 2.6666666666666665
Trascription: peck peppers peter
Recognition: the pickled of of of the of the


*****************************************
File: /group/teaching/asr/labs/recordings/0063.wav 
Speed of Viterbi Decoder: 3.469389542005956 s  Speed of Backtrace: 0.001019858755171299 s  Forward Count: 63724
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter piper pick



*****************************************
File: /group/teaching/asr/labs/recordings/0082.wav 
Speed of Viterbi Decoder: 2.4495226023718715 s  Speed of Backtrace: 0.0003328705206513405 s  Forward Count: 46976
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 7
WER: 0.5714285714285714
Trascription: the pickled peppers of the piper peter
Recognition: the of the pickled where's of the piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0083.wav 
Speed of Viterbi Decoder: 1.5069838827475905 s  Speed of Backtrace: 0.00020487327128648758 s  Forward Count: 28689
(Substitutions, Deletions, Insertions) N: (0, 0, 2) 3
WER: 0.6666666666666666
Trascription: where's peter piper
Recognition: the where's peter piper the


*****************************************
File: /group/teaching/asr/labs/recordings/0084.wav 
Speed of Viterbi Decoder: 2.5475742984563112 s  Speed of Backtrace: 0.00040199141949415207 s  Forward Count: 40652
(Substitutions, Delet

...



*****************************************
File: /group/teaching/asr/labs/recordings/0263.wav 
Speed of Viterbi Decoder: 3.4196935622021556 s  Speed of Backtrace: 0.00044272933155298233 s  Forward Count: 60495
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 6
WER: 1.5
Trascription: peter picked a peck of peppers
Recognition: the a of picked where's of pickled peck a where's the


*****************************************
File: /group/teaching/asr/labs/recordings/0264.wav 
Speed of Viterbi Decoder: 4.028847279958427 s  Speed of Backtrace: 0.00046074390411376953 s  Forward Count: 71296
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 9
WER: 0.4444444444444444
Trascription: where's the peck of pickled peppers peter piper picked
Recognition: the where's the peck of pickled a where's peter piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0265.wav 
Speed of Viterbi Decoder: 3.3984934808686376 s  Speed of Backtrace: 0.0003805281594



*****************************************
File: /group/teaching/asr/labs/recordings/0283.wav 
Speed of Viterbi Decoder: 6.137877134606242 s  Speed of Backtrace: 0.0013906583189964294 s  Forward Count: 105715
(Substitutions, Deletions, Insertions) N: (3, 1, 3) 9
WER: 0.7777777777777778
Trascription: pickled peter of peppers the peppers a pickled of
Recognition: peck the pickled peter a peppers of a peppers pickled the


*****************************************
File: /group/teaching/asr/labs/recordings/0284.wav 
Speed of Viterbi Decoder: 10.337219171226025 s  Speed of Backtrace: 0.0011234879493713379 s  Forward Count: 188341
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 19
WER: 0.3157894736842105
Trascription: peter peck piper pickled pickled of peppers of peppers peppers picked where's piper picked the piper where's peppers pickled
Recognition: the a the peck piper pickled pickled of peppers of a where's peppers picked where's piper picked the piper where's peppers pickled the




*****************************************
File: /group/teaching/asr/labs/recordings/0302.wav 
Speed of Viterbi Decoder: 2.907385004684329 s  Speed of Backtrace: 0.00037641171365976334 s  Forward Count: 55172
(Substitutions, Deletions, Insertions) N: (2, 0, 4) 6
WER: 1.0
Trascription: where's the peck peter piper picked
Recognition: the where's where's peck a the of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0303.wav 
Speed of Viterbi Decoder: 2.3154748268425465 s  Speed of Backtrace: 0.0002949638292193413 s  Forward Count: 43085
(Substitutions, Deletions, Insertions) N: (1, 0, 3) 6
WER: 0.6666666666666666
Trascription: where's a peck of pickled peter
Recognition: the where's of peck of pickled peter a the


*****************************************
File: /group/teaching/asr/labs/recordings/0304.wav 
Speed of Viterbi Decoder: 7.753853862173855 s  Speed of Backtrace: 0.0008878801017999649 s  Forward Count: 145301
(Substitution



*****************************************
File: /group/teaching/asr/labs/recordings/0321.wav 
Speed of Viterbi Decoder: 3.51636809296906 s  Speed of Backtrace: 0.00041227322071790695 s  Forward Count: 64578
(Substitutions, Deletions, Insertions) N: (2, 1, 2) 6
WER: 0.8333333333333334
Trascription: where's the peck of pickled peppers
Recognition: the where's where's pickled picked peppers the


*****************************************
File: /group/teaching/asr/labs/recordings/0322.wav 
Speed of Viterbi Decoder: 4.118596346117556 s  Speed of Backtrace: 0.00046465080231428146 s  Forward Count: 72117
(Substitutions, Deletions, Insertions) N: (4, 0, 5) 7
WER: 1.2857142857142858
Trascription: where's the pickled peppers peter piper picked
Recognition: the where's where's where's of of where's peck of piper picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0323.wav 
Speed of Viterbi Decoder: 2.414302697405219 s  Speed of Backtrace: 0.000421155



*****************************************
File: /group/teaching/asr/labs/recordings/0341.wav 
Speed of Viterbi Decoder: 3.2695667948573828 s  Speed of Backtrace: 0.000374453142285347 s  Forward Count: 57639
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
WER: 2.0
Trascription: peppers peck peter piper
Recognition: the of where's peck the the of piper peter the


*****************************************
File: /group/teaching/asr/labs/recordings/0342.wav 
Speed of Viterbi Decoder: 2.259350573644042 s  Speed of Backtrace: 0.00027469731867313385 s  Forward Count: 39309
(Substitutions, Deletions, Insertions) N: (3, 0, 5) 4
WER: 2.0
Trascription: peter peter peter peter
Recognition: the the the the peter the peck picked the


*****************************************
File: /group/teaching/asr/labs/recordings/0343.wav 
Speed of Viterbi Decoder: 4.055814212188125 s  Speed of Backtrace: 0.0011043800041079521 s  Forward Count: 70961
(Substitutions, Deletions, Insertions) N: (2, 0, 6) 4
